<a href="https://colab.research.google.com/github/Ryong1998/Git-Tutorial/blob/main/EDA_file4.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 프로젝트 주제

- 해당 프로젝트는 미래의 아파트 집 값을 예측하는 프로젝트 입니다

# 프로젝트 소개 

- 다양한 지역의 다양한 부동산의 종류(아파트, 단독주택 등)들 중 '서울'의 '아파트'의 '미래 가격 변화율'을 예측함
- 최종적으로면 '미래 가격 변화율'이 가장 좋을 것으로 예상되는, 즉, 가장 수익률이 높을 것으로 예상되는 아파트를 찾는 것이 목적
- 부동산의 가치는 '1. 거주지로서의 특성'과 '2. 금융상품으로서의 특성' 두가지를 통해서 평가를 할 수 있다고 가정
- '1. 거주지로서의 특성'은 주변 편의시설, 교육시설, 아파트 평수, 주변 교통시설 등 더 편한 거주환경을 제공하는 요소들을 포함
- '2. 금융상품으로서의 특성'은 기준금리, 아파트 공급량, 아파트 미분양, 현재 매매가, 전세가율 등 금융관련 수치들로 표현이 되는 요소들을 포함
- '1. 거주지로서의 특성'에서 높은 가치를 의미하는 요소들은 시대가 변함에 따라서 바뀔 수가 있음(예를 들어 대가족에서 소가족 형태로 가족 구성원 구조가 바뀌면서 시대에 따라 사람들이 선호하는 아파트 평수가 바뀔 수도 있고, 인터넷 강의의 발달로 인해서 교육시설 인프라의 중요성이 향후 낮아질 수 있음음)
- '1. 거주지로서의 특성'에서 높은 가치들은 과거 계속 변화했을 수 있지만 어떻게 변했는지 파악하기가 쉽지 않고, 미래에 어떻게 변할지 알 수 없기에 평가의 기준이 '변동적'이라는 특징이 있음
- 하지만 '2. 금융상품으로서의 특성'은 가격과 경제를 바탕으로 한 '수치'들을 표현 하기에 '1. 거주지로서의 특성'보다 일관성 있게 부동산의 가치를 평가할 수 있음
- '2. 금융상품으로서의 특성'에 해당하는 수치들은 그 자체로 변화하는 '1. 거주지로서의 특성'의 가치를 내포하고 있다고 가정
- 해당 프로젝트는 '2. 금융상품으로서의 특성'에 집중하여서 집값의 변화를 예측 할 예정

# original_data 확보

- 'http://rtdown.molit.go.kr/' 사이트를 통해서 아파트매매가, 아파트 전/월세 가격 정보 파일로 얻음
- 'https://kr.investing.com/' 사이트를 통해서 한국국채금리, 미국국채금리, 코스피 정보를 얻음 
- 'https://data.kbland.kr/publicdata/unsold-apartments' 사이트를 통해서 미분양 아파트 수량 정보를 얻음
- 'https://asil.kr/asil/sub/movein.jsp' 사이트를 통해서 분양 아파트 수량 정보를 얻음
- 'https://www.bok.or.kr/portal/singl/baseRate/list.do?dataSeCd=01&menuNo=200643' 사이트를 통해서 기준금리 정보를 얻음
- 'https://data.seoul.go.kr/dataList/801/S/2/datasetView.do' 사이트를 통해서 서울시 주택가격지수를 얻음



>> 공공데이터포털의 api를 이용해서 아파트매매가, 아파트 전/월세 가격 정보를 얻으려 했지만 일일 트래픽 제한으로 인해서 직접 'http://rtdown.molit.go.kr/' 사이트에 접속해서 파일들을 다운 받아 필요 데이터를 확보

In [1]:
# 구글 드라이브 마운트
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# 파이썬 버전 확인인
!python --version

Python 3.8.10


In [ ]:
# 라이브러리 버전 확인인
pip list

Package                       Version
----------------------------- ----------------------
absl-py                       1.4.0
aeppl                         0.0.33
aesara                        2.7.9
aiohttp                       3.8.4
aiosignal                     1.3.1
alabaster                     0.7.13
albumentations                1.2.1
altair                        4.2.2
appdirs                       1.4.4
argon2-cffi                   21.3.0
argon2-cffi-bindings          21.2.0
arviz                         0.12.1
astor                         0.8.1
astropy                       4.3.1
astunparse                    1.6.3
async-timeout                 4.0.2
atari-py                      0.2.9
atomicwrites                  1.4.1
attrs                         22.2.0
audioread                     3.0.0
autograd                      1.5
Babel                         2.11.0
backcall                      0.2.0
beautifulsoup4                4.6.3
bleach                        6.0.0
blis

# apartment_deal.csv 파일 생성

- apartment_deal(아파트 매매) 파일 생성
- 'http://rtdown.molit.go.kr/' 사이트를 통해서 아파트매매가 정보 파일로 얻음

## csv 파일들 불러오기 및 병합

- 아파트 매매 정보 원본본파일들은 연도별로 파일들이 나누어져 되어있고, 각 csv 파일 내의 모든 정보들이 필요하지는 않기에 전처리 과정 진행

In [ ]:
import pandas as pd
import os

# 연도별 아파트 매매 정보들이 들어있는 csv경로 설정 
dir_path = "/content/drive/MyDrive/house_price/original_data/deal_price/Seoul" 
file_list = os.listdir(dir_path)
file_list.sort()
df_list = list()
# 해당 폴더 안에 있는 csv 파일들을 읽어서 리스트 안에 데이터프레임들을 담음
for csv_file in file_list:
    df_list.append(pd.read_csv(dir_path+"/"+csv_file ,skiprows=15,  encoding='cp949'))

>> 코랩은 파일을 읽어올 때 업로드한 순서대로 파일을 불러오는 듯

In [ ]:
df_list[0].info() # 리스트 안에 잘 담겼는지 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 120812 entries, 0 to 120811
Data columns (total 15 columns):
 #   Column    Non-Null Count   Dtype  
---  ------    --------------   -----  
 0   시군구       120812 non-null  object 
 1   번지        120812 non-null  object 
 2   본번        120812 non-null  int64  
 3   부번        120812 non-null  int64  
 4   단지명       120812 non-null  object 
 5   전용면적(㎡)   120812 non-null  float64
 6   계약년월      120812 non-null  int64  
 7   계약일       120812 non-null  int64  
 8   거래금액(만원)  120812 non-null  object 
 9   층         120812 non-null  int64  
 10  건축년도      120812 non-null  int64  
 11  도로명       120812 non-null  object 
 12  해제사유발생일   0 non-null       float64
 13  거래유형      120812 non-null  object 
 14  중개사소재지    120812 non-null  object 
dtypes: float64(2), int64(6), object(7)
memory usage: 13.8+ MB


In [ ]:
df_list[0].head()

시군구     번지   본번  부번             단지명  전용면적(㎡)    계약년월  계약일  \
0  서울특별시 강남구 개포동  655-2  655   2  개포2차현대아파트(220)    77.75  200603   10   
1  서울특별시 강남구 개포동  655-2  655   2  개포2차현대아파트(220)    77.75  200603   29   
2  서울특별시 강남구 개포동  655-2  655   2  개포2차현대아파트(220)    77.75  200604   29   
3  서울특별시 강남구 개포동  655-2  655   2  개포2차현대아파트(220)    77.75  200606    1   
4  서울특별시 강남구 개포동  655-2  655   2  개포2차현대아파트(220)    77.75  200610   20   

  거래금액(만원)  층  건축년도      도로명  해제사유발생일 거래유형 중개사소재지  
0   59,500  7  1988  언주로 103      NaN    -      -  
1   60,000  6  1988  언주로 103      NaN    -      -  
2   67,000  9  1988  언주로 103      NaN    -      -  
3   60,000  4  1988  언주로 103      NaN    -      -  
4   72,250  5  1988  언주로 103      NaN    -      -

In [ ]:
# 모든 데이터프레임을 하나의 데이터프레임으로 통합
df_default = df_list[0]
for df_csv in df_list[1:]:
    df_default = pd.concat([df_default, df_csv], axis=0)
df_default.reset_index(drop=True, inplace=True) # concat으로 합쳐질 때 인덱스 재설정
df_default.loc[1] 

시군구          서울특별시 강남구 개포동
번지                   655-2
본번                   655.0
부번                     2.0
단지명         개포2차현대아파트(220)
전용면적(㎡)              77.75
계약년월                200603
계약일                     29
거래금액(만원)            60,000
층                        6
건축년도                1988.0
도로명                언주로 103
해제사유발생일                NaN
거래유형                     -
중개사소재지                   -
Name: 1, dtype: object

In [ ]:
df_default.head() # 병합한 테이블의 정보 파악

시군구     번지     본번   부번             단지명  전용면적(㎡)    계약년월  계약일  \
0  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    77.75  200603   10   
1  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    77.75  200603   29   
2  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    77.75  200604   29   
3  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    77.75  200606    1   
4  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    77.75  200610   20   

  거래금액(만원)  층    건축년도      도로명  해제사유발생일 거래유형 중개사소재지  
0   59,500  7  1988.0  언주로 103      NaN    -      -  
1   60,000  6  1988.0  언주로 103      NaN    -      -  
2   67,000  9  1988.0  언주로 103      NaN    -      -  
3   60,000  4  1988.0  언주로 103      NaN    -      -  
4   72,250  5  1988.0  언주로 103      NaN    -      -

In [ ]:
df_default.info() # 데이터프레임 합친 결과 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1237491 entries, 0 to 1237490
Data columns (total 15 columns):
 #   Column    Non-Null Count    Dtype  
---  ------    --------------    -----  
 0   시군구       1237491 non-null  object 
 1   번지        1237270 non-null  object 
 2   본번        1237416 non-null  float64
 3   부번        1237416 non-null  float64
 4   단지명       1237491 non-null  object 
 5   전용면적(㎡)   1237491 non-null  float64
 6   계약년월      1237491 non-null  int64  
 7   계약일       1237491 non-null  int64  
 8   거래금액(만원)  1237491 non-null  object 
 9   층         1237491 non-null  int64  
 10  건축년도      1237489 non-null  float64
 11  도로명       1237491 non-null  object 
 12  해제사유발생일   5242 non-null     float64
 13  거래유형      1237491 non-null  object 
 14  중개사소재지    1237491 non-null  object 
dtypes: float64(5), int64(3), object(7)
memory usage: 141.6+ MB


## 필요한 컬럼만 선택

- df_default 데이터프레임에서 모든 컬럼들을 사용하지 않기에, 사용할 컬럼들만을 선택

In [ ]:
# 사용할 컬럼들만 거르고 컬럼명 영어로 치환 - 필요한 컬럼들만 선택
df_default = df_default[['시군구','본번','부번','도로명','단지명','계약년월','계약일','전용면적(㎡)','거래금액(만원)','층']]
df_default.columns = ['address','main_number','sub_number','road','name','year_month','day','area','deal_price','floor']
df_default.head() # 잘 걸러졌는지 확인

address  main_number  sub_number     road            name  \
0  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   
1  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   
2  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   
3  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   
4  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   

   year_month  day   area deal_price  floor  
0      200603   10  77.75     59,500      7  
1      200603   29  77.75     60,000      6  
2      200604   29  77.75     67,000      9  
3      200606    1  77.75     60,000      4  
4      200610   20  77.75     72,250      5

In [ ]:
# 타입 변경을 통해서 deal_price,year_month, day 타입 변경
df_default["deal_price"] = df_default["deal_price"].str.replace(",", "") # 'deal_price'에서 ','가 들어있는 부분 제거(추후 계산에 사용하기 위해서서)
df = df_default.astype({'year_month':'str','day':'str','deal_price':'int64'}).copy()
df.head() # 형태가 변경된거 확인

address  main_number  sub_number     road            name year_month  \
0  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)     200603   
1  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)     200603   
2  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)     200604   
3  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)     200606   
4  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)     200610   

  day   area  deal_price  floor  
0  10  77.75       59500      7  
1  29  77.75       60000      6  
2  29  77.75       67000      9  
3   1  77.75       60000      4  
4  20  77.75       72250      5

In [ ]:
df.info() # 타입변경 및 null 확인 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1237491 entries, 0 to 1237490
Data columns (total 10 columns):
 #   Column       Non-Null Count    Dtype  
---  ------       --------------    -----  
 0   address      1237491 non-null  object 
 1   main_number  1237416 non-null  float64
 2   sub_number   1237416 non-null  float64
 3   road         1237491 non-null  object 
 4   name         1237491 non-null  object 
 5   year_month   1237491 non-null  object 
 6   day          1237491 non-null  object 
 7   area         1237491 non-null  float64
 8   deal_price   1237491 non-null  int64  
 9   floor        1237491 non-null  int64  
dtypes: float64(3), int64(2), object(5)
memory usage: 94.4+ MB


In [ ]:
# 'main_number'혹은 'sub_number'이 null 인데 'road'도 null 인 값을 확인 -> 없음
# 즉, 'road가 주소에 관한한 정보가 더욱 많음'
df[((df['main_number'].isnull()) |(df['sub_number'].isnull())) &(df['road'].isnull()) ]

Empty DataFrame
Columns: [address, main_number, sub_number, road, name, year_month, day, area, deal_price, floor]
Index: []

- main_number와 sub_number에 null 값들이 있음을 확인 -> road 정보가 주소에 관한 정보로 적합하다는 판단

## 새로운 컬럼 생성

- 날짜 관련한 컬럼들을 추후 그룹화등을 할 때 사용하기에 'year_month' 컬럼과 'day' 컬럼을 가공하여서 다양한 날짜 관련 컬럼들을 생성

In [ ]:
# 추후 데이터들 그룹화에 사용하기 위해서 날짜관련 컬럼들들 분리 및 생성
df['year'] = df['year_month'].str[0:4] # '연','월' 합쳐져 있는 컬럼에서 연도만 추출
df['month'] = df['year_month'].str[4:] # '연','월' 합쳐져 있는 컬럼에서 월만 추출
df.loc[df["day"].str.len()==1,"day"]='0'+df.loc[df["day"].str.len()==1,"day"] # '일'이 있는 컬럼에서 해당 '일'이 1일, 2일 처럼 1자리 숫자인 경우 앞에 0을 추가
df['date'] = pd.to_datetime(df['year']+df['month']+df['day']) # 일자들을 합쳐서 date 컬럼 생성
df = df.astype({'year':'int64','month':'int64','day':'int64'}) # 원하는 타입으로 변경경
df = df.drop(['year_month'], axis=1) # 사용 안하는 컬럼들 제거
df.head()

address  main_number  sub_number     road            name  day  \
0  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   10   
1  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   29   
2  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   29   
3  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)    1   
4  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   20   

    area  deal_price  floor  year  month       date  
0  77.75       59500      7  2006      3 2006-03-10  
1  77.75       60000      6  2006      3 2006-03-29  
2  77.75       67000      9  2006      4 2006-04-29  
3  77.75       60000      4  2006      6 2006-06-01  
4  77.75       72250      5  2006     10 2006-10-20

In [ ]:
df.info() # 타입들이 원하는데로 변경됨을 확인인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1237491 entries, 0 to 1237490
Data columns (total 12 columns):
 #   Column       Non-Null Count    Dtype         
---  ------       --------------    -----         
 0   address      1237491 non-null  object        
 1   main_number  1237416 non-null  float64       
 2   sub_number   1237416 non-null  float64       
 3   road         1237491 non-null  object        
 4   name         1237491 non-null  object        
 5   day          1237491 non-null  int64         
 6   area         1237491 non-null  float64       
 7   deal_price   1237491 non-null  int64         
 8   floor        1237491 non-null  int64         
 9   year         1237491 non-null  int64         
 10  month        1237491 non-null  int64         
 11  date         1237491 non-null  datetime64[ns]
dtypes: datetime64[ns](1), float64(3), int64(5), object(3)
memory usage: 113.3+ MB


In [ ]:
# 주소 및 도로명들 분리
df["address_0"] = df["address"].str.split(' ',expand=True)[0] # '시' 만 추출해야 하나, 서울만 함으로 일단은 실행 X
df["address_1"] = df["address"].str.split(' ',expand=True)[1] # '구' 만 추출
df["address_2"] = df["address"].str.split(' ',expand=True)[2] # '동' 만 추출
df["road_name"] = df["road"].str.split(' ',expand=True)[0] # '도로명' 만 추출
df["road_number"] = df["road"].str.split(' ',expand=True)[1] # '도로숫자' 만 추출
df= df[['year','month','day','address_0','address_1','address_2','road_name','road_number','area','deal_price','name','main_number','sub_number','date']] # 사용할 컬럼만 선택
df.head()

year  month  day address_0 address_1 address_2 road_name road_number  \
0  2006      3   10     서울특별시       강남구       개포동       언주로         103   
1  2006      3   29     서울특별시       강남구       개포동       언주로         103   
2  2006      4   29     서울특별시       강남구       개포동       언주로         103   
3  2006      6    1     서울특별시       강남구       개포동       언주로         103   
4  2006     10   20     서울특별시       강남구       개포동       언주로         103   

    area  deal_price            name  main_number  sub_number       date  
0  77.75       59500  개포2차현대아파트(220)        655.0         2.0 2006-03-10  
1  77.75       60000  개포2차현대아파트(220)        655.0         2.0 2006-03-29  
2  77.75       67000  개포2차현대아파트(220)        655.0         2.0 2006-04-29  
3  77.75       60000  개포2차현대아파트(220)        655.0         2.0 2006-06-01  
4  77.75       72250  개포2차현대아파트(220)        655.0         2.0 2006-10-20

## 결측치 처리1

In [ ]:
df.info() # road_number에 1개의의 null 값이 생김을 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1237491 entries, 0 to 1237490
Data columns (total 14 columns):
 #   Column       Non-Null Count    Dtype         
---  ------       --------------    -----         
 0   year         1237491 non-null  int64         
 1   month        1237491 non-null  int64         
 2   day          1237491 non-null  int64         
 3   address_0    1237491 non-null  object        
 4   address_1    1237491 non-null  object        
 5   address_2    1237491 non-null  object        
 6   road_name    1237491 non-null  object        
 7   road_number  1237490 non-null  object        
 8   area         1237491 non-null  float64       
 9   deal_price   1237491 non-null  int64         
 10  name         1237491 non-null  object        
 11  main_number  1237416 non-null  float64       
 12  sub_number   1237416 non-null  float64       
 13  date         1237491 non-null  datetime64[ns]
dtypes: datetime64[ns](1), float64(3), int64(4), object(6)
memory usage

In [ ]:
df[df['road_number'].isnull()] # road_number에 null값이 들어 있는 row를 확인

year  month  day address_0 address_1 address_2 road_name road_number  \
1177515  2020     12   31     서울특별시        중구     만리동2가      만리재로        None   

            area  deal_price          name  main_number  sub_number       date  
1177515  39.9541      161000  서울역센트럴자이(임대)        176.0         1.0 2020-12-31

In [ ]:
# '서울역센트럴자이'를 확인 -> '' 값이 존재함을 확인..
df.loc[df['name'] == '서울역센트럴자이',:]

year  month  day address_0 address_1 address_2 road_name road_number  \
936223   2017      5    3     서울특별시        중구     만리동2가      만리재로         175   
936224   2017     12   20     서울특별시        중구     만리동2가      만리재로         175   
936225   2017     12   30     서울특별시        중구     만리동2가                         
1018067  2018      3   20     서울특별시        중구     만리동2가                         
1093938  2019      7   13     서울특별시        중구     만리동2가      만리재로         175   
1093939  2019      8   20     서울특별시        중구     만리동2가      만리재로         175   
1093940  2019      8   23     서울특별시        중구     만리동2가      만리재로         175   
1093941  2019      9    8     서울특별시        중구     만리동2가      만리재로         175   
1093942  2019      9   21     서울특별시        중구     만리동2가      만리재로         175   
1093943  2019     11   30     서울특별시        중구     만리동2가      만리재로         175   
1093944  2019     12   12     서울특별시        중구     만리동2가      만리재로         175   
1093945  2019     12   14     서울특별시        중구     만리동2가      만리재로         175   
1177510  2020      1    8     서울특별시        중구     만리동2가      만리재로         175   
1177511  2020      5   20     서울특별시        중구     만리동2가      만리재로         175   
1177512  2020      7   12     서울특별시        중구     만리동2가      만리재로         175   
1177513  2020      8   13     서울특별시        중구     만리동2가      만리재로         175   
1177514  2020     10   17     서울특별시        중구     만리동2가      만리재로         175   
1222610  2021     12   14     서울특별시        중구     만리동2가      만리재로         175   
1236741  2022      1   17     서울특별시        중구     만리동2가      만리재로         175   
1236742  2022      3    2     서울특별시        중구     만리동2가      만리재로         175   
1236743  2022      6    5     서울특별시        중구     만리동2가      만리재로         175   
1236744  2022     12   14     서울특별시        중구     만리동2가      만리재로         175   

            area  deal_price      name  main_number  sub_number       date  
936223   84.9720       79390  서울역센트럴자이        176.0         1.0 2017-05-03  
936224   59.9430       85000  서울역센트럴자이        176.0         1.0 2017-12-20  
936225   59.9400       85000  서울역센트럴자이        176.0         1.0 2017-12-30  
1018067  72.9900       85000  서울역센트럴자이        176.0         1.0 2018-03-20  
1093938  84.9720      134500  서울역센트럴자이        176.0         1.0 2019-07-13  
1093939  59.9400       95000  서울역센트럴자이        176.0         1.0 2019-08-20  
1093940  84.9720      139000  서울역센트럴자이        176.0         1.0 2019-08-23  
1093941  59.9400      113800  서울역센트럴자이        176.0         1.0 2019-09-08  
1093942  72.9733      132000  서울역센트럴자이        176.0         1.0 2019-09-21  
1093943  59.9808      120000  서울역센트럴자이        176.0         1.0 2019-11-30  
1093944  84.9720      136500  서울역센트럴자이        176.0         1.0 2019-12-12  
1093945  84.9720      141000  서울역센트럴자이        176.0         1.0 2019-12-14  
1177510  84.9918      141500  서울역센트럴자이        176.0         1.0 2020-01-08  
1177511  73.0000      133500  서울역센트럴자이        176.0         1.0 2020-05-20  
1177512  84.9720      142000  서울역센트럴자이        176.0         1.0 2020-07-12  
1177513  84.9720      158000  서울역센트럴자이        176.0         1.0 2020-08-13  
1177514  72.9733      136500  서울역센트럴자이        176.0         1.0 2020-10-17  
1222610  84.9791      183000  서울역센트럴자이        176.0         1.0 2021-12-14  
1236741  84.9720      170000  서울역센트럴자이        176.0         1.0 2022-01-17  
1236742  84.9918      179500  서울역센트럴자이        176.0         1.0 2022-03-02  
1236743  59.9808      148750  서울역센트럴자이        176.0         1.0 2022-06-05  
1236744  59.9707      145000  서울역센트럴자이        176.0         1.0 2022-12-14

In [ ]:
# 값이 '' 로 되어 있는 row들을 확인인
df.loc[df['road_name'] == '',:]

year  month  day address_0 address_1 address_2 road_name road_number  \
1606     2006      2   23     서울특별시       강남구       논현동                         
1628     2006     10   19     서울특별시       강남구       논현동                         
2799     2006      1   24     서울특별시       강남구       대치동                         
2806     2006      2   14     서울특별시       강남구       대치동                         
2807     2006      2   14     서울특별시       강남구       대치동                         
...       ...    ...  ...       ...       ...       ...       ...         ...   
1234065  2022      6   24     서울특별시       송파구       거여동                         
1234066  2022      7   21     서울특별시       송파구       거여동                         
1234067  2022      7   23     서울특별시       송파구       거여동                         
1234069  2022      8   19     서울특별시       송파구       거여동                         
1234071  2022     10    7     서울특별시       송파구       거여동                         

           area  deal_price          name  main_number  sub_number       date  
1606     128.67       73500            경복        276.0         0.0 2006-02-23  
1628      95.48       71000            경복        276.0         0.0 2006-10-19  
2799      76.56       80000           청실1        633.0         0.0 2006-01-24  
2806     102.64      143500           청실1        633.0         0.0 2006-02-14  
2807     102.64      142000           청실1        633.0         0.0 2006-02-14  
...         ...         ...           ...          ...         ...        ...  
1234065   84.95      128000  e편한세상송파파크센트럴        696.0         0.0 2022-06-24  
1234066   84.97      135000  e편한세상송파파크센트럴        696.0         0.0 2022-07-21  
1234067   59.96      125000  e편한세상송파파크센트럴        696.0         0.0 2022-07-23  
1234069   84.96      130000  e편한세상송파파크센트럴        696.0         0.0 2022-08-19  
1234071  113.18      148000  e편한세상송파파크센트럴        696.0         0.0 2022-10-07  

[2031 rows x 14 columns]

>> null 값이 없다고 ''값도 없는건 아니구나! -> 의미적으로는 결측치이지만 ''로 표시되어서 마치 값이 있는 것처럼 있을 수도 있음

In [ ]:
df.loc[df['name'] == '서울역센트럴자이(임대)','name']='서울역센트럴자이' # '서울역센트럴자이(임대)' 명칭을을 '서울역센트럴자이'로 수정
df.loc[df['name'] == '서울역센트럴자이','road_name']='만리재로' # 위에서 확인한 '서울역센트럴자이'의 값들로 'road_name' 수정
df.loc[df['name'] == '서울역센트럴자이','road_number']='175' # 위에서 확인한 '서울역센트럴자이'의 값들로 'road_number' 수정
df.info() # 우선 1차적으로 null 로 표시되는는 null 값들은 처리함을 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1237491 entries, 0 to 1237490
Data columns (total 14 columns):
 #   Column       Non-Null Count    Dtype         
---  ------       --------------    -----         
 0   year         1237491 non-null  int64         
 1   month        1237491 non-null  int64         
 2   day          1237491 non-null  int64         
 3   address_0    1237491 non-null  object        
 4   address_1    1237491 non-null  object        
 5   address_2    1237491 non-null  object        
 6   road_name    1237491 non-null  object        
 7   road_number  1237491 non-null  object        
 8   area         1237491 non-null  float64       
 9   deal_price   1237491 non-null  int64         
 10  name         1237491 non-null  object        
 11  main_number  1237416 non-null  float64       
 12  sub_number   1237416 non-null  float64       
 13  date         1237491 non-null  datetime64[ns]
dtypes: datetime64[ns](1), float64(3), int64(4), object(6)
memory usage

## 결측치 처리2

- 앞에서 과정들을 통해서 ''들이 값들로 들어 있을 수도 있음을 깨닫고 '' 값들을 null로 간주하여서 결측치 처리 진행

In [ ]:
import numpy as np
df = df.replace('', np.nan) # ''값만 있는 값들을 null 값들로 수정
df.info() # 수정한 후 정보 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1237491 entries, 0 to 1237490
Data columns (total 14 columns):
 #   Column       Non-Null Count    Dtype         
---  ------       --------------    -----         
 0   year         1237491 non-null  int64         
 1   month        1237491 non-null  int64         
 2   day          1237491 non-null  int64         
 3   address_0    1237491 non-null  object        
 4   address_1    1237491 non-null  object        
 5   address_2    1237491 non-null  object        
 6   road_name    1235462 non-null  object        
 7   road_number  1234196 non-null  object        
 8   area         1237491 non-null  float64       
 9   deal_price   1237491 non-null  int64         
 10  name         1237491 non-null  object        
 11  main_number  1237416 non-null  float64       
 12  sub_number   1237416 non-null  float64       
 13  date         1237491 non-null  datetime64[ns]
dtypes: datetime64[ns](1), float64(3), int64(4), object(6)
memory usage

In [ ]:
df.isnull().sum() # df의 'road_name'과 'road_number'의 null 값들이 증가함을 확인, 

year              0
month             0
day               0
address_0         0
address_1         0
address_2         0
road_name      2029
road_number    3295
area              0
deal_price        0
name              0
main_number      75
sub_number       75
date              0
dtype: int64

- 처음에는 도로주소가 null값이 더 적은 줄 알았지만, 전처리 과정 중 지번주소가 null 값이 더 적은 것을 확인

In [ ]:
# 'main_number'나 'sub_number' 둘중 하나만 null 인 것을 확인 -> 없음
# 즉, 2개가 동시에 null 값을 가지고 있음
df[((df['main_number'].isnull()) &(df['sub_number'].notnull()))
  |((df['main_number'].notnull()) &(df['sub_number'].isnull()))]

Empty DataFrame
Columns: [year, month, day, address_0, address_1, address_2, road_name, road_number, area, deal_price, name, main_number, sub_number, date]
Index: []

In [ ]:
# 도로명정보에는 null이고 지번주소도 null인 데이터를 확인 -> 없다
# 즉, 도로명주소나 지번주소 둘 중 하나를 활용해서 주소에 대한 정보를 얻을 수 있다
df[((df['road_name'].isnull()) | (df['road_number'].isnull())) & (df['main_number'].isnull())] 

Empty DataFrame
Columns: [year, month, day, address_0, address_1, address_2, road_name, road_number, area, deal_price, name, main_number, sub_number, date]
Index: []

In [ ]:
# 처리해야 할 null 값이 있는 데이터프레임을 조회
df.loc[df['main_number'].isnull(),['address_0','address_1','address_2','road_name','road_number','name','main_number','sub_number']] 

address_0 address_1 address_2 road_name road_number           name  \
681633      서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
681634      서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
681635      서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
681636      서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
681637      서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
...           ...       ...       ...       ...         ...            ...   
1209122     서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
1209123     서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
1209124     서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
1232880     서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
1232881     서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   

         main_number  sub_number  
681633           NaN         NaN  
681634           NaN         NaN  
681635           NaN         NaN  
681636           NaN         NaN  
681637           NaN         NaN  
...              ...         ...  
1209122          NaN         NaN  
1209123          NaN         NaN  
1209124          NaN         NaN  
1232880          NaN         NaN  
1232881          NaN         NaN  

[75 rows x 8 columns]

In [ ]:
df.loc[df['main_number'].isnull(),'name'].unique() # 처리해야 할 지번주소에 null 값이 있는 아파트명들 조회
                                                   # '힐스테이트 서초 젠트리스'만 수정하면 될듯

array(['힐스테이트 서초 젠트리스'], dtype=object)

In [ ]:
df.loc[df['name']=='힐스테이트 서초 젠트리스',:] # 기존 name 컬럼이 '힐스테이트 서초 젠트리스' 인 전체 값들이이 지번주소가 null값으로 되어 있음

year  month  day address_0 address_1 address_2 road_name road_number  \
681633   2015      3    1     서울특별시       서초구       신원동     헌릉로8길       10-12   
681634   2015      4   17     서울특별시       서초구       신원동     헌릉로8길       10-12   
681635   2015      5    1     서울특별시       서초구       신원동     헌릉로8길       10-12   
681636   2015      6   16     서울특별시       서초구       신원동     헌릉로8길       10-12   
681637   2015      6   26     서울특별시       서초구       신원동     헌릉로8길       10-12   
...       ...    ...  ...       ...       ...       ...       ...         ...   
1209122  2021      4   27     서울특별시       서초구       신원동     헌릉로8길       10-12   
1209123  2021      5   26     서울특별시       서초구       신원동     헌릉로8길       10-12   
1209124  2021      7   26     서울특별시       서초구       신원동     헌릉로8길       10-12   
1232880  2022      6   23     서울특별시       서초구       신원동     헌릉로8길       10-12   
1232881  2022      9   28     서울특별시       서초구       신원동     헌릉로8길       10-12   

           area  deal_price           name  main_number  sub_number       date  
681633    84.95       73430  힐스테이트 서초 젠트리스          NaN         NaN 2015-03-01  
681634    84.99       79000  힐스테이트 서초 젠트리스          NaN         NaN 2015-04-17  
681635   101.90       95000  힐스테이트 서초 젠트리스          NaN         NaN 2015-05-01  
681636    84.95       87200  힐스테이트 서초 젠트리스          NaN         NaN 2015-06-16  
681637   101.90       94500  힐스테이트 서초 젠트리스          NaN         NaN 2015-06-26  
...         ...         ...            ...          ...         ...        ...  
1209122  101.90      184500  힐스테이트 서초 젠트리스          NaN         NaN 2021-04-27  
1209123   84.95      165000  힐스테이트 서초 젠트리스          NaN         NaN 2021-05-26  
1209124   84.99      182000  힐스테이트 서초 젠트리스          NaN         NaN 2021-07-26  
1232880  101.90      204000  힐스테이트 서초 젠트리스          NaN         NaN 2022-06-23  
1232881   84.95      173000  힐스테이트 서초 젠트리스          NaN         NaN 2022-09-28  

[75 rows x 14 columns]

In [ ]:
# 지번주소 null 값들을 네이버를 통해 검색하여서 정보를 얻고 수정
df.loc[df['name']=='힐스테이트 서초 젠트리스','main_number'] = 557
df.loc[df['name']=='힐스테이트 서초 젠트리스','sub_number'] = 0

In [ ]:
# 사용할 컬럼들 선택택과, 컬럼명들 수정
df_deal = df[['date','year','month','day','address_0','address_1','address_2','main_number','sub_number','name','area','deal_price']].copy()
df_deal.columns =['date','year','month','day','address_0','address_1','address_2','address_3','address_4','name','area','deal_price']
df_deal = df_deal[df_deal['year']>=2011] # 전세/월세데이터가 2011년 이후로 있어서 연도 선택
df_deal.head()

date  year  month  day address_0 address_1 address_2  address_3  \
355306 2011-07-09  2011      7    9     서울특별시       강남구       개포동      655.0   
355307 2011-07-28  2011      7   28     서울특별시       강남구       개포동      655.0   
355308 2011-01-19  2011      1   19     서울특별시       강남구       개포동      658.0   
355309 2011-09-02  2011      9    2     서울특별시       강남구       개포동      658.0   
355310 2011-12-17  2011     12   17     서울특별시       강남구       개포동      658.0   

        address_4            name   area  deal_price  
355306        2.0  개포2차현대아파트(220)  77.75       64000  
355307        2.0  개포2차현대아파트(220)  77.75       65500  
355308        1.0  개포6차우성아파트1동~8동  67.28       70500  
355309        1.0  개포6차우성아파트1동~8동  79.97       85000  
355310        1.0  개포6차우성아파트1동~8동  67.28       68000

In [ ]:
df_deal.info() # 데이터프레임 정보 확인

<class 'pandas.core.frame.DataFrame'>
Int64Index: 882185 entries, 355306 to 1237490
Data columns (total 12 columns):
 #   Column      Non-Null Count   Dtype         
---  ------      --------------   -----         
 0   date        882185 non-null  datetime64[ns]
 1   year        882185 non-null  int64         
 2   month       882185 non-null  int64         
 3   day         882185 non-null  int64         
 4   address_0   882185 non-null  object        
 5   address_1   882185 non-null  object        
 6   address_2   882185 non-null  object        
 7   address_3   882185 non-null  float64       
 8   address_4   882185 non-null  float64       
 9   name        882185 non-null  object        
 10  area        882185 non-null  float64       
 11  deal_price  882185 non-null  int64         
dtypes: datetime64[ns](1), float64(3), int64(4), object(4)
memory usage: 87.5+ MB


In [ ]:
df_deal.iloc[200] # 정보들 제대로 있는지 확인

date          2011-12-23 00:00:00
year                         2011
month                          12
day                            23
address_0                   서울특별시
address_1                     강남구
address_2                     개포동
address_3                   141.0
address_4                     0.0
name                      개포주공1단지
area                        56.57
deal_price                  95000
Name: 355506, dtype: object

In [ ]:
df_deal.to_csv('/content/drive/MyDrive/house_price/after_data/ver_4/apartment_deal.csv',index=False)

# apartment_full_rent.csv, apartment_month_rent.csv 파일 생성

- apartment_full_rent(아파트 전세), apartment_month_rent(아파트 월세) 파일 생성
- 'http://rtdown.molit.go.kr/' 사이트를 통해서 아파트전세,월세 정보 파일로 얻음
- 아파트 전세정보 csv 파일들은 연도별로 파일들이 분류가 되어있고, 각 csv 파일 내의 모든 정보들이 전부 필요하지는 않기에 전처리 과정 진행

## csv 파일들 불러오기 및 병합

In [ ]:
import pandas as pd
import os


dir_path = "/content/drive/MyDrive/house_price/original_data/rent_price/Seoul"
file_list = os.listdir(dir_path)
file_list.sort()
df_list = list()

# 해당 폴더 안에 있는 csv 파일들을 읽어서 리스트 안에 데이터프레임들을 담음
for csv_file in file_list:
    df_list.append(pd.read_csv(dir_path+"/"+csv_file ,skiprows=15,  encoding='cp949'))


<ipython-input-123-1889cf88dc67>:12: DtypeWarning:

Columns (10) have mixed types. Specify dtype option on import or set low_memory=False.

<ipython-input-123-1889cf88dc67>:12: DtypeWarning:

Columns (10) have mixed types. Specify dtype option on import or set low_memory=False.

<ipython-input-123-1889cf88dc67>:12: DtypeWarning:

Columns (10) have mixed types. Specify dtype option on import or set low_memory=False.

<ipython-input-123-1889cf88dc67>:12: DtypeWarning:

Columns (10) have mixed types. Specify dtype option on import or set low_memory=False.

<ipython-input-123-1889cf88dc67>:12: DtypeWarning:

Columns (10) have mixed types. Specify dtype option on import or set low_memory=False.

<ipython-input-123-1889cf88dc67>:12: DtypeWarning:

Columns (10) have mixed types. Specify dtype option on import or set low_memory=False.

<ipython-input-123-1889cf88dc67>:12: DtypeWarning:

Columns (10) have mixed types. Specify dtype option on import or set low_memory=False.

<ipython-input-123-1

In [ ]:
df_list[-1].info() # 리스트 안에 잘 담겼는지 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 231846 entries, 0 to 231845
Data columns (total 19 columns):
 #   Column         Non-Null Count   Dtype  
---  ------         --------------   -----  
 0   시군구            231846 non-null  object 
 1   번지             231657 non-null  object 
 2   본번             231819 non-null  float64
 3   부번             231819 non-null  float64
 4   단지명            231846 non-null  object 
 5   전월세구분          231846 non-null  object 
 6   전용면적(㎡)        231846 non-null  float64
 7   계약년월           231846 non-null  int64  
 8   계약일            231846 non-null  int64  
 9   보증금(만원)        231846 non-null  object 
 10  월세(만원)         231846 non-null  object 
 11  층              231846 non-null  int64  
 12  건축년도           231749 non-null  float64
 13  도로명            231846 non-null  object 
 14  계약기간           231846 non-null  object 
 15  계약구분           231846 non-null  object 
 16  갱신요구권 사용       231846 non-null  object 
 17  종전계약 보증금 (만원)  188985 non-nul

In [ ]:
# 모든 데이터프레임을을 통합
df_default = df_list[0]
for df_csv in df_list[1:]:
    df_default = pd.concat([df_default, df_csv], axis=0)
df_default.reset_index(drop=True, inplace=True) # concat으로 합쳐질 때 인덱스 재설정
df_default.info() # 데이터프레임 합친 결과 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2085775 entries, 0 to 2085774
Data columns (total 19 columns):
 #   Column         Dtype  
---  ------         -----  
 0   시군구            object 
 1   번지             object 
 2   본번             float64
 3   부번             float64
 4   단지명            object 
 5   전월세구분          object 
 6   전용면적(㎡)        float64
 7   계약년월           int64  
 8   계약일            int64  
 9   보증금(만원)        object 
 10  월세(만원)         object 
 11  층              float64
 12  건축년도           float64
 13  도로명            object 
 14  계약기간           object 
 15  계약구분           object 
 16  갱신요구권 사용       object 
 17  종전계약 보증금 (만원)  object 
 18  종전계약 월세 (만원)   object 
dtypes: float64(5), int64(2), object(12)
memory usage: 302.4+ MB


In [ ]:
df_default.loc[1]

시군구               서울특별시 강남구 개포동
번지                        655-2
본번                        655.0
부번                          2.0
단지명              개포2차현대아파트(220)
전월세구분                        전세
전용면적(㎡)                   77.75
계약년월                     201101
계약일                          18
보증금(만원)                  20,000
월세(만원)                        0
층                           8.0
건축년도                     1988.0
도로명                     언주로 103
계약기간                          -
계약구분                          -
갱신요구권 사용                      -
종전계약 보증금 (만원)               NaN
종전계약 월세 (만원)                NaN
Name: 1, dtype: object

In [ ]:
df_default.head() # 데이터 형태 확인 

시군구     번지     본번   부번             단지명 전월세구분  전용면적(㎡)    계약년월  \
0  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    전세    77.75  201101   
1  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    전세    77.75  201101   
2  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    전세    77.75  201102   
3  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    전세    77.75  201102   
4  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    전세    77.75  201102   

   계약일 보증금(만원) 월세(만원)    층    건축년도      도로명 계약기간 계약구분 갱신요구권 사용 종전계약 보증금 (만원)  \
0    5  35,000      0  7.0  1988.0  언주로 103    -    -        -           NaN   
1   18  20,000      0  8.0  1988.0  언주로 103    -    -        -           NaN   
2    1  24,000      0  5.0  1988.0  언주로 103    -    -        -           NaN   
3   11  31,000      0  9.0  1988.0  언주로 103    -    -        -           NaN   
4   24  30,500      0  9.0  1988.0  언주로 103    -    -        -           NaN   

  종전계약 월세 (만원)  
0          NaN  
1          NaN  
2          NaN  
3          NaN  
4          NaN

In [ ]:
df_default.isnull().sum() # 번지, 본번, 부번이 null 값들이 있음

시군구                    0
번지                  1586
본번                   234
부번                   234
단지명                    0
전월세구분                  0
전용면적(㎡)               36
계약년월                   0
계약일                    0
보증금(만원)                0
월세(만원)                 0
층                     36
건축년도                 249
도로명                    0
계약기간                   0
계약구분                   0
갱신요구권 사용               0
종전계약 보증금 (만원)    1793799
종전계약 월세 (만원)     1793799
dtype: int64

In [ ]:
df_default['전월세구분'].unique()

array(['전세', '월세'], dtype=object)

- 전월세구분이 '전세'와 '월세' 두 가지만 있음으로 조건문을 활용해서 나누기에 용이함

## 전세 데이터 프레임 생성 

- apartment_deal 과 진행 과정이 거의 동일하기에 apartment_deal.ipynb 파일의 진행과정을 참조해서 하나의 셀로 합쳐서 진행
- 주석 부분들은 중간과정 확인 부분

In [ ]:
# 전세 데이터 프레임 생성 - 주석부분은 중간에서 값 확인하는 부분들
df_full_rent = df_default.loc[df_default['전월세구분']=='전세',['시군구','본번','부번','도로명','계약년월','계약일','보증금(만원)','전용면적(㎡)','단지명']].copy()
df_full_rent.columns = ['address','main_number','sub_number','road','year_month','day','full_rent_price','area','name']
# print(df_full_rent.head())
# print(df_full_rent.info())

df_full_rent = df_full_rent.astype({'full_rent_price':'str','year_month':'str','day':'str','full_rent_price':'str'})
df_full_rent["full_rent_price"] = df_full_rent["full_rent_price"].str.replace(",", "")
df_full_rent.loc[df_full_rent["day"].str.len()==1,"day"]='0'+df_full_rent.loc[df_full_rent["day"].str.len()==1,"day"] # 일이 있는 컬럼에서 1자리 숫자인 경우 앞에 0을 추가성
df_full_rent['year'] = df_full_rent['year_month'].str[0:4] # 연,월 합쳐져 있는 컬럼에서 연도만 추출
df_full_rent['month'] = df_full_rent['year_month'].str[4:] # 연,월 합쳐져 있는 컬럼에서 월만 추출
df_full_rent['date'] = pd.to_datetime(df_full_rent['year']+df_full_rent['month']+df_full_rent['day']) # 일자들을 합쳐서 date 컬럼 생
df_full_rent = df_full_rent.astype({'year':'int64','month':'int64','day':'int64','full_rent_price':'int64'})
df_full_rent = df_full_rent.drop(['year_month'], axis=1) # 사용 안하는 컬럼들 제거
# print(df_full_rent.head())
# print(df_full_rent.info())

df_full_rent["address_0"] = df_full_rent["address"].str.split(' ',expand=True)[0] # '시' 만 추출해야 하나, 서울만 함으로 일단은 실행 X
df_full_rent["address_1"] = df_full_rent["address"].str.split(' ',expand=True)[1] # '구' 만 추출
df_full_rent["address_2"] = df_full_rent["address"].str.split(' ',expand=True)[2] # '동' 만 추출
df_full_rent["road_name"] = df_full_rent["road"].str.split(' ',expand=True)[0] # '도로명' 만 추출
df_full_rent["road_number"] = df_full_rent["road"].str.split(' ',expand=True)[1] # '도로숫자' 만 추출
df_full_rent= df_full_rent[['year','month','day','address_0','address_1','address_2','main_number','sub_number','road_name','road_number','area',"full_rent_price",'name','date']] # 사용할 컬럼만 선택
# print(df_full_rent.head())
# print(df_full_rent.info())
# print(df_full_rent.isnull().sum())

df_full_rent = df_full_rent.replace('', None) # ''값만 있는 값들을 null 값들로 수정
# print(df_full_rent.isnull().sum())

# df_full_rent[((df_full_rent['main_number'].isnull()) &(df_full_rent['sub_number'].notnull()))
#   |((df_full_rent['main_number'].notnull()) &(df_full_rent['sub_number'].isnull()))]

# df_full_rent[((df_full_rent['road_name'].isnull()) | (df_full_rent['road_number'].isnull())) & (df_full_rent['main_number'].isnull())] 

# df_full_rent.loc[df_full_rent['main_number'].isnull(),['address_0','address_1','address_2','main_number','sub_number','road_name','road_number','name']]

# df_full_rent.loc[df_full_rent['main_number'].isnull(),'name'].unique()

# df_full_rent.loc[df_full_rent['name']=='힐스테이트 서초 젠트리스',:]

df_full_rent.loc[df_full_rent['name']=='힐스테이트 서초 젠트리스','main_number'] = 557
df_full_rent.loc[df_full_rent['name']=='힐스테이트 서초 젠트리스','sub_number'] = 0


df_full_rent = df_full_rent[['date','year','month','day','address_0','address_1','address_2','main_number','sub_number','name','area','full_rent_price']].copy()
df_full_rent.columns =['date','year','month','day','address_0','address_1','address_2','address_3','address_4','name','area','full_rent_price']
# df_full_rent.head()

# df_full_rent.info() 

In [ ]:
df_full_rent.isnull().sum()

date                0
year                0
month               0
day                 0
address_0           0
address_1           0
address_2           0
address_3           0
address_4           0
name                0
area               25
full_rent_price     0
dtype: int64

### 'area' 컬럼 결측치 처리

- apartment_deal.ipynb 와 달리 area 컬럼에 결측치가 존재하기에 결측치 처리 부분 추가
- 결측치는 해당 주소의 전세 아파트의 거래 내역 중 가장 거래가 많았던 area 컬럼의 값 으로 대체하여 처리

In [ ]:
# area의 빈 칸들 해결
df_full_rent[df_full_rent['area'].isnull()].tail()

date  year  month  day address_0 address_1 address_2  address_3  \
357440 2013-11-16  2013     11   16     서울특별시       노원구       공릉동      683.0   
375219 2013-11-30  2013     11   30     서울특별시      동대문구       장안동      312.0   
389892 2013-01-17  2013      1   17     서울특별시      서대문구       창천동      501.0   
439901 2013-01-20  2013      1   20     서울특별시      영등포구    영등포동4가      103.0   
490009 2014-02-19  2014      2   19     서울특별시       강서구       화곡동       29.0   

        address_4          name  area  full_rent_price  
357440       14.0        한일휴니스빌   NaN             8000  
375219        8.0         태솔에버빌   NaN            12000  
389892       14.0         삼성아트빌   NaN             9000  
439901        0.0       영등포그랑그루   NaN             8000  
490009       47.0  드림하우스(29-47)   NaN             9500

In [ ]:
# area가 null값인 row들이 다른 주소정보관련 컬럼들을 리스트 화
add_1 = list(df_full_rent.loc[df_full_rent['area'].isnull(),'address_1'])
add_2 = list(df_full_rent.loc[df_full_rent['area'].isnull(),'address_2'])
add_3 = list(df_full_rent.loc[df_full_rent['area'].isnull(),'address_3'])
add_4 = list(df_full_rent.loc[df_full_rent['area'].isnull(),'address_4'])
area_list = list()

In [ ]:
# area_list 에 값 추가
for i in range(len(add_1)):
    # 해당 주소에서 거래된 매물들의 '층' 정보가 없을 경우, area null을 처리할 참조 자료가 없음으로 ''으로 처리리
    if (len(df_full_rent.loc[(df_full_rent['address_1'] ==add_1[i]) & 
                     (df_full_rent['address_2'] ==add_2[i]) &
                     (df_full_rent['address_3'] ==add_3[i]) &
                     (df_full_rent['address_4'] ==add_4[i]),
                     'area'].value_counts())) == 0:

        area_list.append('')
    else:
        # 해당 주소에서 가장 많이 거래되었던 층수를 null 값에 채움움
        area_list.append(df_full_rent.loc[(df_full_rent['address_1'] ==add_1[i]) & 
                     (df_full_rent['address_2'] ==add_2[i]) &
                     (df_full_rent['address_3'] ==add_3[i]) &
                     (df_full_rent['address_4'] ==add_4[i]),
                     'area'].value_counts().idxmax())
print(area_list) # area 이 null 값인 주소의 매물들의 가장 많이 거래된 층들을 출력력

[84.9, 33.33, 15.94, 15.94, 84.98, 142.034, 142.034, 142.034, 142.034, 17.07, 17.07, 17.07, 17.07, 17.07, 64.52, 23.47, 23.47, 13.2195, 13.2195, 13.2195, 13.2195, 49.65, 39.28, 12.1, '']


- 마지막에 ''인 값이 있는데 이건 해당 매물은 참조할 만할 거래내역이 없음을 의미

In [ ]:
# len을 통해서 리스트들이 다 만들어 졌는지 확인
print(len(add_1),len(add_2),len(add_3),len(add_4),len(area_list)) 

25 25 25 25 25


In [ ]:
# 맨 마지막 row가 '' 여서 해당 row의 area 값을 채우기 위해 참조할 값을 확인 -> 없음
# 해당은 area를 알수있는 방법이 없음 - 다른 참조할만할 area 값들이 없음 -> 추후 제거 필요
df_full_rent.loc[(df_full_rent['address_3']==29)&(df_full_rent['address_4']==47),:] # 테스트로 area이 null 값인 row를 대표로 확인인

date  year  month  day address_0 address_1 address_2  address_3  \
490009 2014-02-19  2014      2   19     서울특별시       강서구       화곡동       29.0   

        address_4          name  area  full_rent_price  
490009       47.0  드림하우스(29-47)   NaN             9500

In [ ]:
# floor가 null인 값들을 처리, 가장 많이 거래된 '층'의 정보로 결측치 처리리
for i in range(len(add_1)):
    df_full_rent.loc[(df_full_rent['address_1'] ==add_1[i]) & 
                         (df_full_rent['address_2'] ==add_2[i]) &
                         (df_full_rent['address_3'] ==add_3[i]) &
                         (df_full_rent['address_4'] ==add_4[i]),
                         'area']=area_list[i]

In [ ]:
# null 대신 ''이 잘 들어있는지 확인
df_full_rent.loc[df_full_rent['area']=='',:]

date  year  month  day address_0 address_1 address_2  address_3  \
490009 2014-02-19  2014      2   19     서울특별시       강서구       화곡동       29.0   

        address_4          name area  full_rent_price  
490009       47.0  드림하우스(29-47)                  9500

In [ ]:
# floor이 ''인 값 제거
df_full_rent=df_full_rent.drop(df_full_rent[df_full_rent['area']==''].index)

# 제거후 값 확인
df_full_rent.loc[df_full_rent['area']=='',:] # 제거가 된음 확인인

Empty DataFrame
Columns: [date, year, month, day, address_0, address_1, address_2, address_3, address_4, name, area, full_rent_price]
Index: []

In [ ]:
df_full_rent.info() # 값확인을 통해서 null값 처리가 되었는지 확인인

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1448686 entries, 0 to 2085774
Data columns (total 12 columns):
 #   Column           Non-Null Count    Dtype         
---  ------           --------------    -----         
 0   date             1448686 non-null  datetime64[ns]
 1   year             1448686 non-null  int64         
 2   month            1448686 non-null  int64         
 3   day              1448686 non-null  int64         
 4   address_0        1448686 non-null  object        
 5   address_1        1448686 non-null  object        
 6   address_2        1448686 non-null  object        
 7   address_3        1448686 non-null  float64       
 8   address_4        1448686 non-null  float64       
 9   name             1448686 non-null  object        
 10  area             1448686 non-null  object        
 11  full_rent_price  1448686 non-null  int64         
dtypes: datetime64[ns](1), float64(2), int64(4), object(5)
memory usage: 143.7+ MB


In [ ]:
df_full_rent.to_csv('/content/drive/MyDrive/house_price/after_data/ver_4/apartment_full_rent.csv', index=False) # 전세 csv 파일 생성성

## 월세 데이터 프레임 생성

- 전세 데이터프레임 생성 파트 참조

In [ ]:
# 월세 데이터 프레임 생성, 필요한 컬럼들만 필터링
df_month_rent = df_default.loc[df_default['전월세구분']=='월세',['시군구','본번','부번','도로명','계약년월','계약일','보증금(만원)','월세(만원)','전용면적(㎡)','단지명']].copy()
df_month_rent.columns = ['address','main_number','sub_number','road','year_month','day','rent_deposit','month_rent_price','area','name']
# df_month_rent.head()

df_month_rent.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 637088 entries, 25 to 2085770
Data columns (total 10 columns):
 #   Column            Non-Null Count   Dtype  
---  ------            --------------   -----  
 0   address           637088 non-null  object 
 1   main_number       637039 non-null  float64
 2   sub_number        637039 non-null  float64
 3   road              637088 non-null  object 
 4   year_month        637088 non-null  int64  
 5   day               637088 non-null  int64  
 6   rent_deposit      637088 non-null  object 
 7   month_rent_price  637088 non-null  object 
 8   area              637077 non-null  float64
 9   name              637088 non-null  object 
dtypes: float64(3), int64(2), object(5)
memory usage: 53.5+ MB


전세 파트와 다른 부분 확인! ↓

In [ ]:
df_month_rent["month_rent_price2"] = df_month_rent["month_rent_price"].str.replace(',','')
df_month_rent.info() 

<class 'pandas.core.frame.DataFrame'>
Int64Index: 637088 entries, 25 to 2085770
Data columns (total 11 columns):
 #   Column             Non-Null Count   Dtype  
---  ------             --------------   -----  
 0   address            637088 non-null  object 
 1   main_number        637039 non-null  float64
 2   sub_number         637039 non-null  float64
 3   road               637088 non-null  object 
 4   year_month         637088 non-null  int64  
 5   day                637088 non-null  int64  
 6   rent_deposit       637088 non-null  object 
 7   month_rent_price   637088 non-null  object 
 8   area               637077 non-null  float64
 9   name               637088 non-null  object 
 10  month_rent_price2  349840 non-null  object 
dtypes: float64(3), int64(2), object(6)
memory usage: 58.3+ MB


- "month_rent_price"를 replace를 적용해서 month_rent_price2를 생성하는데 replace 함수가 제데로 처리가 안됨을 확인

>> df_month_rent["month_rent_price"].str.replace(',','') 

>> 진행했을 때, 'month_rent_price2' 컬럼에서의 null 값이 매우 커짐 -> replace 매소드가 제대로 동작 안함을 확인

>> 왜 동작을 안할까? -> string 과 object 타입의 차이, object는 타입의 혼용?

In [ ]:
# 해당 파트를 통해서 우선 type 을 변경한 다음에 진행해야 함
df_month_rent = df_month_rent.astype({'month_rent_price':'str','rent_deposit':'str'})

- apartment_deal 과 진행 과정이 거의 동일하기에 한 셀로 합쳐서 진행
- 주석 부분들은 중간과정 확인 부분

In [ ]:
df_month_rent["rent_deposit"] = df_month_rent["rent_deposit"].str.replace(",", "")
df_month_rent["month_rent_price"] = df_month_rent["month_rent_price"].str.replace(',','')
df_month_rent = df_month_rent.astype({'year_month':'str','day':'str','rent_deposit':'int64','month_rent_price':'int64'})
df_month_rent['year'] = df_month_rent['year_month'].str[0:4] # 연,월 합쳐져 있는 컬럼에서 연도만 추출
df_month_rent['month'] = df_month_rent['year_month'].str[4:] # 연,월 합쳐져 있는 컬럼에서 월만 추출
df_month_rent.loc[df_month_rent["day"].str.len()==1,"day"]='0'+df_month_rent.loc[df_month_rent["day"].str.len()==1,"day"] # 일이 있는 컬럼에서 1자리 숫자인 경우 앞에 0을 추가성
df_month_rent['date'] = pd.to_datetime(df_month_rent['year']+df_month_rent['month']+df_month_rent['day']) # 일자들을 합쳐서 date 컬럼 생
df_month_rent = df_month_rent.astype({'year':'int64','month':'int64','day':'int64'})
df_month_rent = df_month_rent.drop(['year_month'], axis=1) # 사용 안하는 컬럼들 제거
# print(df_month_rent.head())

df_month_rent["address_0"] = df_month_rent["address"].str.split(' ',expand=True)[0] # '시' 만 추출해야 하나, 서울만 함으로 일단은 실행 X
df_month_rent["address_1"] = df_month_rent["address"].str.split(' ',expand=True)[1] # '구' 만 추출
df_month_rent["address_2"] = df_month_rent["address"].str.split(' ',expand=True)[2] # '동' 만 추출
df_month_rent["road_name"] = df_month_rent["road"].str.split(' ',expand=True)[0] # '도로명' 만 추출
df_month_rent["road_number"] = df_month_rent["road"].str.split(' ',expand=True)[1] # '도로숫자' 만 추출
df_month_rent= df_month_rent[['year','month','day','address_0','address_1','address_2','main_number','sub_number','road_name','road_number','area',"rent_deposit","month_rent_price",'name','date']] # 사용할 컬럼만 선택
# print(df_month_rent.head())

# print(df_month_rent.info())
# print(df_month_rent.isnull().sum())

df_month_rent = df_month_rent.replace('', None) # ''값만 있는 값들을 null 값들로 수정
# print(df_month_rent.isnull().sum()) # 수정한 후 정보 확인 -> road_name과 road_number가 기하급수적으로 증가함

# df_month_rent[((df_month_rent['main_number'].isnull()) &(df_month_rent['sub_number'].notnull()))
#   |((df_month_rent['main_number'].notnull()) &(df_month_rent['sub_number'].isnull()))]

# df_month_rent[((df_month_rent['road_name'].isnull()) | (df_month_rent['road_number'].isnull())) & (df_month_rent['main_number'].isnull())] 

# df_month_rent.loc[df_month_rent['main_number'].isnull(),['address_0','address_1','address_2','main_number','sub_number','road_name','road_number','name']]

# df_month_rent.loc[df_month_rent['main_number'].isnull(),'name'].unique()

# df_month_rent.loc[df_month_rent['name']=='힐스테이트 서초 젠트리스',:]


df_month_rent.loc[df_month_rent['name']=='힐스테이트 서초 젠트리스','main_number'] = 557
df_month_rent.loc[df_month_rent['name']=='힐스테이트 서초 젠트리스','sub_number'] = 0

df_month_rent = df_month_rent[['date','year','month','day','address_0','address_1','address_2','main_number','sub_number','name','area','rent_deposit','month_rent_price']]
df_month_rent.columns =['date','year','month','day','address_0','address_1','address_2','address_3','address_4','name','area','rent_deposit','month_rent_price']
# df_month_rent.head()

# df_month_rent.info()

In [ ]:
df_month_rent.isnull().sum()

date                 0
year                 0
month                0
day                  0
address_0            0
address_1            0
address_2            0
address_3            0
address_4            0
name                 0
area                11
rent_deposit         0
month_rent_price     0
dtype: int64

### 'area' 컬럼 결측치 처리

- 전세의 floor 결측치 처리 부분 참조

In [ ]:
# df_month_rent[df_month_rent['area'].isnull()].tail()


add_1 = list(df_month_rent.loc[df_month_rent['area'].isnull(),'address_1'])
add_2 = list(df_month_rent.loc[df_month_rent['area'].isnull(),'address_2'])
add_3 = list(df_month_rent.loc[df_month_rent['area'].isnull(),'address_3'])
add_4 = list(df_month_rent.loc[df_month_rent['area'].isnull(),'address_4'])
area_list = list()
# area_list 에 값 추가
for i in range(len(add_1)):
    # 해당 주소에서 거래된 매물들의 '층' 정보가 없을 경우, area null을 처리할 참조 자료가 없음으로 ''으로 처리리
    if (len(df_month_rent.loc[(df_month_rent['address_1'] ==add_1[i]) & 
                     (df_month_rent['address_2'] ==add_2[i]) &
                     (df_month_rent['address_3'] ==add_3[i]) &
                     (df_month_rent['address_4'] ==add_4[i]),
                     'area'].value_counts())) == 0:

        area_list.append('')
    else:
        # 해당 주소에서 가장 많이 거래되었던 층수를 null 값에 채울거임
        area_list.append(df_month_rent.loc[(df_month_rent['address_1'] ==add_1[i]) & 
                     (df_month_rent['address_2'] ==add_2[i]) &
                     (df_month_rent['address_3'] ==add_3[i]) &
                     (df_month_rent['address_4'] ==add_4[i]),
                     'area'].value_counts().idxmax())
# print(area_list)

# print(len(add_1),len(add_2),len(add_3),len(add_4),len(area_list)) 

for i in range(len(add_1)):
    df_month_rent.loc[(df_month_rent['address_1'] ==add_1[i]) & 
                         (df_month_rent['address_2'] ==add_2[i]) &
                         (df_month_rent['address_3'] ==add_3[i]) &
                         (df_month_rent['address_4'] ==add_4[i]),
                         'area']=area_list[i]

# df_month_rent.head()

# df_month_rent.info()



In [ ]:
df_month_rent.isnull().sum()

date                0
year                0
month               0
day                 0
address_0           0
address_1           0
address_2           0
address_3           0
address_4           0
name                0
area                0
rent_deposit        0
month_rent_price    0
dtype: int64

In [ ]:
df_month_rent.head()

date  year  month  day address_0 address_1 address_2  address_3  \
25 2011-03-18  2011      3   18     서울특별시       강남구       개포동      658.0   
28 2011-04-09  2011      4    9     서울특별시       강남구       개포동      658.0   
38 2011-07-09  2011      7    9     서울특별시       강남구       개포동      658.0   
46 2011-09-19  2011      9   19     서울특별시       강남구       개포동      658.0   
47 2011-09-20  2011      9   20     서울특별시       강남구       개포동      658.0   

    address_4            name   area  rent_deposit  month_rent_price  
25        1.0  개포6차우성아파트1동~8동  79.97         19000                63  
28        1.0  개포6차우성아파트1동~8동  79.97         21000                35  
38        1.0  개포6차우성아파트1동~8동  79.97          3000               160  
46        1.0  개포6차우성아파트1동~8동  79.97          6000               140  
47        1.0  개포6차우성아파트1동~8동  79.97          5000               160

In [ ]:
df_month_rent.to_csv('/content/drive/MyDrive/house_price/after_data/ver_4/apartment_month_rent.csv', index=False)

# economic_data.csv 파일생성

- economic_data(거시경제 정보관련) 파일 생성
- economic_data 에는 한국기준금리, 부동산지수, 기준금리, 코스피지수, 한국국채금리, 미국국채금리, 장단기금리차, 아파트 분양 공급량, 아파트 미분양수, 아파트 미분양률 의 정보를 포함함

## 기준금리 정보관련 데이터 프레임 생성

- 'https://www.bok.or.kr/portal/singl/baseRate/list.do?dataSeCd=01&menuNo=200643' 홈페이지에서 기준금리의 변경 일자들을 제공하기에 크롤링을 하여 일자별 기준금리를 나타내는 데이터프레임을 생성

### 크롤링을 통해서 기준금리 정보 가져오기

In [ ]:
#라이브러리 임포트

import requests
from bs4 import BeautifulSoup
import pandas as pd
import re
#웹페이지 가져오기

res = requests.get('https://www.bok.or.kr/portal/singl/baseRate/list.do?dataSeCd=01&menuNo=200643')

#웹페이지 파싱하기
soup = BeautifulSoup(res.content,'html.parser')

#필요한 데이터 추출하기
items = soup.select('#content > div.table.tac > table > tbody > tr')

# 크롤링할 정보들을 담을 리스트 -> 추후 데이터프레임의 컬럼으로 대입할 예정정
change_year_list = list()
change_date_list = list()
rp_list = list()

# 사이트에서 표 안에 있는 정보들(text 정보들)을 가져와서 각 리스트에 삽입입
for item in items:
    table_list = item.select('td')
    change_year_list.append(table_list[0].get_text())
    change_date_list.append(table_list[1].get_text())
    rp_list.append(table_list[2].get_text())
    
# df는 기준금리 정보를 가져온 데이터 프레임 생성성
df = pd.DataFrame({
    "year": change_year_list,
    "change_date": change_date_list,
    "korea_rp": rp_list
}, columns=["year", "change_date", "korea_rp"])

df.tail() # 데이터프레임 형태 확인인

year change_date korea_rp
50  2001     07월 05일     4.75
51  2001     02월 08일     5.00
52  2000     10월 05일     5.25
53  2000     02월 10일     5.00
54  1999     05월 06일     4.75

- change_date는 기준금리가 변경된 일자를, korea_rp는 변경한 기준금리를 나타냄

### 컬럼 통합

- year 컬럼과 change_date 컬럼이 일자를 나타내는 컬럼이므로 하나의 컬럼으로 통합

In [ ]:
df['month']=df['change_date'].str[0:2] # 월의 정보만 추출
df['date'] = df['change_date'].str[4:6] # 일의 정보만 추출
df = df.astype({'korea_rp':'float64'}) # rp 컬럼 타입 변경
df['rp_date'] = df['year']+df['month']+df['date'] # 새로운 컬럼 생성
df = df.drop(['change_date', 'year','month','date'], axis=1) # 안쓰는 컬럼 제거
df=df.sort_index(ascending=False) # 날짜가 역순으로 되어 있어서 정렬
df['rp_date'] = pd.to_datetime(df['rp_date'], format='%Y-%m-%d %H:%M:%S', errors='raise') # date 타입으로 변경

In [ ]:
df.head() # 데이터프레임 형태 확인

korea_rp    rp_date
54      4.75 1999-05-06
53      5.00 2000-02-10
52      5.25 2000-10-05
51      5.00 2001-02-08
50      4.75 2001-07-05

In [ ]:
df.tail() # 데이터프레임 형태 확인

korea_rp    rp_date
4      2.25 2022-07-13
3      2.50 2022-08-25
2      3.00 2022-10-12
1      3.25 2022-11-24
0      3.50 2023-01-13

### '기준금리 변경날짜'들 사이에 있는 날짜들의 기준금리 정보 생성

- 위에서의 데이터 프레임은 '기준금리 변경일자'와 '변경된 기준금리'의 정보를 나타내는데, '기준금리 변경일자'들 사이에 있는 모든 날짜들에 대응하는 '기준금리'에 대한 정보도 필요하기에 사이 날짜들에 대한 기준금리 정보들을 생성 

In [ ]:
import datetime

# 크롤링한 날짜 기간에 있는 모든 날짜들을 계산
start = datetime.datetime.strptime("06-05-1999", "%d-%m-%Y") # 시작날짜 설정
end = datetime.datetime.strptime("31-01-2023", "%d-%m-%Y") # 끝날짜 설정정
date_generated = [start + datetime.timedelta(days=x) for x in range(0, (end-start).days)] # 시작날짜와 끝날짜 사이에 있는 날짜들 생성
date_list=list()
for date in date_generated:
    date_list.append(date.strftime("%Y-%m-%d")) # date_list 에서 생성한 날짜들의 형식을 맞춰서 대입 

In [ ]:
# df_date는 조회할 모든 날짜들의 정보가 들어있는 series
df_date = pd.DataFrame({
    "date": date_list
}, columns=["date"])
df_date['date'] = pd.to_datetime(df_date['date'], format='%Y-%m-%d %H:%M:%S', errors='raise') # date 타입으로 변경

In [ ]:
df_date.head() # 데이터 프레임 형태 확인 

date
0 1999-05-06
1 1999-05-07
2 1999-05-08
3 1999-05-09
4 1999-05-10

In [ ]:
# 두개의 데이터프레임 결합을 통해서 날짜별 기준금리 현황을 생성
df_rp=pd.merge(df_date, df, left_on='date', right_on='rp_date', how='left')

In [ ]:
# 사용할 컬럼만을 선택
df_rp = df_rp[['date','korea_rp']]
df_rp # 생성한 데이터 프레임 형태 확인 

date  korea_rp
0    1999-05-06      4.75
1    1999-05-07       NaN
2    1999-05-08       NaN
3    1999-05-09       NaN
4    1999-05-10       NaN
...         ...       ...
8666 2023-01-26       NaN
8667 2023-01-27       NaN
8668 2023-01-28       NaN
8669 2023-01-29       NaN
8670 2023-01-30       NaN

[8671 rows x 2 columns]

In [ ]:
# 가장 최근에 변경된 기준금리가 이후 변경되기 전까지 유지가 되기에, null값들을 젤 위에 있는 값(변경된 가장 최근의 기준금리 값)들로 채움
# 일자별 기준금리의 정보들을 생성
df_rp=df_rp.ffill() # ffill() 매소드를 통해서 젤 위의 있는 값으로 null 값들을 채움 
df_rp

date  korea_rp
0    1999-05-06      4.75
1    1999-05-07      4.75
2    1999-05-08      4.75
3    1999-05-09      4.75
4    1999-05-10      4.75
...         ...       ...
8666 2023-01-26      3.50
8667 2023-01-27      3.50
8668 2023-01-28      3.50
8669 2023-01-29      3.50
8670 2023-01-30      3.50

[8671 rows x 2 columns]

In [ ]:
# 기준금리 현황 그래프 출력
# x축을 날짜, y축을 기준금리 값으로 한 그래프 출력력
import plotly.graph_objects as go

# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_rp['date'], y=df_rp['korea_rp'],
                    mode='lines',
                    name='korea_rp',yaxis='y1'))


fig.show(renderer="colab")

## 부동산 지수 데이터 프레임 생성

- https://data.seoul.go.kr/dataList/801/S/2/datasetView.do 사이트에서 아파트 매매 지수 파일을 다운 받아서 진행
- 아파트 매매 지수는 거시경제관련 지표들이 아파트 가격에 연관이 있는지 대략적인 확인을 위해서 사용 -> 추후 사용은 X

In [ ]:
# 부동산지수 파일을 불러옴
df_real_estate = pd.read_csv("/content/drive/MyDrive/house_price/original_data/seoul_deal_index.csv",  encoding='UTF8') # 부동산 지수 불러오기
df_real_estate= df_real_estate.loc[(df_real_estate['시점']>1998) & (df_real_estate['자치구별(2)']=='소계'),['시점','아파트']]# 해당 조건에 대응하는 데이터만 거르기
df_real_estate.head()


시점   아파트
39  1999  38.7
42  2000  40.3
45  2001  48.1
48  2002  62.9
51  2003  61.2

In [ ]:
df_real_estate.info() # 데이터프레임 정보 확인인

<class 'pandas.core.frame.DataFrame'>
Int64Index: 23 entries, 39 to 519
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   시점      23 non-null     int64  
 1   아파트     23 non-null     float64
dtypes: float64(1), int64(1)
memory usage: 552.0 bytes


In [ ]:
#  지수의 head를 파악
df_real_estate['시점'] = pd.to_datetime(df_real_estate['시점'], format='%Y') # 연도만을 datetime형식으로 변환
df_real_estate.head()

시점   아파트
39 1999-01-01  38.7
42 2000-01-01  40.3
45 2001-01-01  48.1
48 2002-01-01  62.9
51 2003-01-01  61.2

In [ ]:
df_real_estate.info() # 타입이 변경된을 확인인

<class 'pandas.core.frame.DataFrame'>
Int64Index: 23 entries, 39 to 519
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype         
---  ------  --------------  -----         
 0   시점      23 non-null     datetime64[ns]
 1   아파트     23 non-null     float64       
dtypes: datetime64[ns](1), float64(1)
memory usage: 552.0 bytes


## 기준금리 & 부동산지수 통합

- 기준금리와 부동산지수 데이터프레임들을 통합
- 기준금리 데이터프레임이 모든 날짜들에 대한 정보를 가지고 있기에, 기준금리 데이터 프레임을 left로 두어서 merge 실행
- 부동산지수 데이터프레임의 수치들은 1년동안 값이 일정하다 가정

In [ ]:
df_final=pd.merge(df_rp, df_real_estate, left_on='date', right_on='시점', how='left') # 기준금리 데이터 프레임과 부동산지수 데이터 프레임을 병합합
df_final=df_final.ffill() # 젤 위의 값으로 null 값을 채움, 부동산지수의 수치가 1년동안 일정하다 가정정
df_final.head()

date  korea_rp  시점  아파트
0 1999-05-06      4.75 NaT  NaN
1 1999-05-07      4.75 NaT  NaN
2 1999-05-08      4.75 NaT  NaN
3 1999-05-09      4.75 NaT  NaN
4 1999-05-10      4.75 NaT  NaN

In [ ]:
df_final.info() # 데이터프레임 정보 확인인

<class 'pandas.core.frame.DataFrame'>
Int64Index: 8671 entries, 0 to 8670
Data columns (total 4 columns):
 #   Column    Non-Null Count  Dtype         
---  ------    --------------  -----         
 0   date      8671 non-null   datetime64[ns]
 1   korea_rp  8671 non-null   float64       
 2   시점        8431 non-null   datetime64[ns]
 3   아파트       8431 non-null   float64       
dtypes: datetime64[ns](2), float64(2)
memory usage: 338.7 KB


In [ ]:
df_final.tail()

date  korea_rp         시점    아파트
8666 2023-01-26       3.5 2021-01-01  104.4
8667 2023-01-27       3.5 2021-01-01  104.4
8668 2023-01-28       3.5 2021-01-01  104.4
8669 2023-01-29       3.5 2021-01-01  104.4
8670 2023-01-30       3.5 2021-01-01  104.4

In [ ]:
df_final = df_final.fillna(38.7) # 결측치를 채움, 38.7이 가장 과거의 값이기에 해당 값으로 값을 채움
df_final = df_final[['date','korea_rp','아파트']] # 사용할 컬럼만을 선택
df_final.columns = ['date','korea_rp','apartment_index'] # 컬럼명 수정정

In [ ]:
df_final.head()

date  korea_rp  apartment_index
0 1999-05-06      4.75             38.7
1 1999-05-07      4.75             38.7
2 1999-05-08      4.75             38.7
3 1999-05-09      4.75             38.7
4 1999-05-10      4.75             38.7

### 기준금리(역) 과 부동산지수 비교

In [ ]:
# 기준금리와 부동산지수 2개의 그래프를 출력
# 기준금리는 x축을 기준으로 뒤짚은 값값

import plotly.graph_objects as go

# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_rp'],
                    mode='lines',
                    name='korea_rp',yaxis='y1'))
# x축으로 그래프를 뒤집음
fig.update_layout(
    yaxis = dict(autorange="reversed")
)


fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['apartment_index'],
                    mode='lines',
                    name='apartment_index',
                    yaxis="y2"))
fig.update_layout(

   # create first Y-axis
   yaxis=dict(
      title="rp point",
      titlefont=dict(color="blue"),
      tickfont=dict(color="blue")
   ),

   # create second Y-axis
   yaxis2=dict(
      title="apartment index",
      overlaying="y",
      side="right")
)
fig.show(renderer="colab")

2005년 이전까지는 동일한움직임, 2005년 부터 2008년은 반대로, 2008년 이후로는 어느정도 동일하게 움직인다
2008년 이후부터 양적완화의 등장으로 인한 유동성의 증가로 기준금리(역)과 부동산 가격이 유사하게 움직이는 건가?

## 데이터프레임 기간 수정

- 전세,월세에 대한 정보가 2011년 이후 부터 있기에 데이터 프레임을 2011년 ~2022년 으로 자름

In [ ]:
df_final = df_final[(df_final['date']>='2011-01-01') & (df_final['date']<='2022-12-31')] # 사용할 날자만 자름
df_final.head()

date  korea_rp  apartment_index
4258 2011-01-01       2.5             93.0
4259 2011-01-02       2.5             93.0
4260 2011-01-03       2.5             93.0
4261 2011-01-04       2.5             93.0
4262 2011-01-05       2.5             93.0

In [ ]:
df_final.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4383 entries, 4258 to 8640
Data columns (total 3 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   date             4383 non-null   datetime64[ns]
 1   korea_rp         4383 non-null   float64       
 2   apartment_index  4383 non-null   float64       
dtypes: datetime64[ns](1), float64(2)
memory usage: 137.0 KB


### 기준금리(역) 과 부동산지수 비교

In [ ]:
# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_rp'],
                    mode='lines',
                    name='korea_rp',yaxis='y1'))
# x축으로 그래프를 뒤집음
fig.update_layout(
    yaxis = dict(autorange="reversed")
)


fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['apartment_index'],
                    mode='lines',
                    name='apartment_index',
                    yaxis="y2"))
fig.update_layout(

   # create first Y-axis
   yaxis=dict(
      title="rp point",
      titlefont=dict(color="blue"),
      tickfont=dict(color="blue")
   ),

   # create second Y-axis
   yaxis2=dict(
      title="apartment index",
      overlaying="y",
      side="right")
)

- 기준금리(역)과 부동산 지수는 연관성이 있는듯

## 코스피 지수 데이터 프레임 생성

In [ ]:
df_kospi = pd.read_csv("/content/drive/MyDrive/house_price/original_data/kospi.csv",  encoding='UTF8') # 코스피 지수 정보 불러오기
df_kospi.head()

날짜        종가        오픈        고가        저가      거래량    변동 %
0  2022- 12- 29  2,236.40  2,265.73  2,272.67  2,236.38  361.19M  -1.93%
1  2022- 12- 28  2,280.45  2,296.45  2,296.45  2,276.90  405.89M  -2.24%
2  2022- 12- 27  2,332.79  2,327.52  2,335.99  2,321.48  448.50M   0.68%
3  2022- 12- 26  2,317.14  2,312.54  2,321.92  2,304.20  427.84M   0.15%
4  2022- 12- 23  2,313.69  2,325.86  2,333.08  2,311.90  366.99M  -1.83%

In [ ]:
df_kospi=df_kospi.sort_index(ascending=False) # 날짜가 역순으로 되어 있어서 정렬
df_kospi.reset_index(drop=True, inplace=True) # index 재설정
df_kospi.head()

날짜        종가        오픈        고가        저가      거래량    변동 %
0  2007- 01- 02  1,435.26  1,438.89  1,439.71  1,430.06  147.74M   0.06%
1  2007- 01- 03  1,409.35  1,436.42  1,437.79  1,409.31  203.21M  -1.81%
2  2007- 01- 04  1,397.29  1,410.55  1,411.12  1,388.50  241.17M  -0.86%
3  2007- 01- 05  1,385.76  1,398.60  1,400.59  1,372.36  277.29M  -0.83%
4  2007- 01- 08  1,370.81  1,376.76  1,384.65  1,366.48  177.59M  -1.08%

In [ ]:
df_kospi.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3956 entries, 0 to 3955
Data columns (total 7 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   날짜      3956 non-null   object
 1   종가      3956 non-null   object
 2   오픈      3956 non-null   object
 3   고가      3956 non-null   object
 4   저가      3956 non-null   object
 5   거래량     3956 non-null   object
 6   변동 %    3956 non-null   object
dtypes: object(7)
memory usage: 216.5+ KB


In [ ]:
# 필요한 컬럼만 선택 후, 컬럼명 수정, 타입변경경
df_kospi = df_kospi[['날짜','종가']]
df_kospi.columns = ['kospi_date','kospi_index']
df_kospi["kospi_date"] = pd.to_datetime(df_kospi["kospi_date"])
df_kospi.head()

kospi_date kospi_index
0 2007-01-02    1,435.26
1 2007-01-03    1,409.35
2 2007-01-04    1,397.29
3 2007-01-05    1,385.76
4 2007-01-08    1,370.81

In [ ]:
df_kospi.info() 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3956 entries, 0 to 3955
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   kospi_date   3956 non-null   datetime64[ns]
 1   kospi_index  3956 non-null   object        
dtypes: datetime64[ns](1), object(1)
memory usage: 61.9+ KB


In [ ]:
# kospi_index 값을 이후 계산에 사용하기 위해서 숫자 형태로 수정
df_kospi["kospi_index"] = df_kospi["kospi_index"].str.replace(",", "") # 문자형으로 되어 있기에 , 을 제거 
df_kospi = df_kospi.astype({'kospi_index': 'float64'})# 컬럼 타입 변경 
df_kospi.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3956 entries, 0 to 3955
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   kospi_date   3956 non-null   datetime64[ns]
 1   kospi_index  3956 non-null   float64       
dtypes: datetime64[ns](1), float64(1)
memory usage: 61.9 KB


In [ ]:
df_kospi.head() # 데이터프레임 형태 확인 

kospi_date  kospi_index
0 2007-01-02      1435.26
1 2007-01-03      1409.35
2 2007-01-04      1397.29
3 2007-01-05      1385.76
4 2007-01-08      1370.81

## 코스피 지수 데이터 프레임과 병합

In [ ]:
# 기준금리&부동산지수 데이터프레임과 코스피 지수 데이터프레임 병합합
df_final=pd.merge(df_final, df_kospi, left_on='date', right_on='kospi_date', how='left') # 두 데이터프레임을 결함
df_final.head()

date  korea_rp  apartment_index kospi_date  kospi_index
0 2011-01-01       2.5             93.0        NaT          NaN
1 2011-01-02       2.5             93.0        NaT          NaN
2 2011-01-03       2.5             93.0 2011-01-03      2070.08
3 2011-01-04       2.5             93.0 2011-01-04      2085.14
4 2011-01-05       2.5             93.0 2011-01-05      2082.55

In [ ]:
df_final.info() # 정보확인 -> 주말등 휴장일들의 존재로 kospi_date 컬럼과 kospi_index 컬럼에서 null 값들이 있음

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4383 entries, 0 to 4382
Data columns (total 5 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   date             4383 non-null   datetime64[ns]
 1   korea_rp         4383 non-null   float64       
 2   apartment_index  4383 non-null   float64       
 3   kospi_date       2958 non-null   datetime64[ns]
 4   kospi_index      2958 non-null   float64       
dtypes: datetime64[ns](2), float64(3)
memory usage: 205.5 KB


In [ ]:
# 휴장일에는 이전의 지수가 유지된다고 가정 
# 해결방안으로 이전의 값으로 null 값을 채우기
df_final["kospi_index"]=df_final["kospi_index"].fillna(method='ffill')
df_final.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4383 entries, 0 to 4382
Data columns (total 5 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   date             4383 non-null   datetime64[ns]
 1   korea_rp         4383 non-null   float64       
 2   apartment_index  4383 non-null   float64       
 3   kospi_date       2958 non-null   datetime64[ns]
 4   kospi_index      4381 non-null   float64       
dtypes: datetime64[ns](2), float64(3)
memory usage: 205.5 KB


In [ ]:
# 가장 위에 있는 null 값은 직접 찾아서(네이버 검색을 통해서서) 대입
df_final["kospi_index"] = df_final["kospi_index"].fillna(2051)
df_final.info() # 값들 대입이 되었는지 확인

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4383 entries, 0 to 4382
Data columns (total 5 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   date             4383 non-null   datetime64[ns]
 1   korea_rp         4383 non-null   float64       
 2   apartment_index  4383 non-null   float64       
 3   kospi_date       2958 non-null   datetime64[ns]
 4   kospi_index      4383 non-null   float64       
dtypes: datetime64[ns](2), float64(3)
memory usage: 205.5 KB


In [ ]:
df_final.head() # 형태 확인

date  korea_rp  apartment_index kospi_date  kospi_index
0 2011-01-01       2.5             93.0        NaT      2051.00
1 2011-01-02       2.5             93.0        NaT      2051.00
2 2011-01-03       2.5             93.0 2011-01-03      2070.08
3 2011-01-04       2.5             93.0 2011-01-04      2085.14
4 2011-01-05       2.5             93.0 2011-01-05      2082.55

In [ ]:
# 사용할 컬럼만 설정
df_final = df_final[['date','korea_rp','apartment_index','kospi_index']]
df_final.head()

date  korea_rp  apartment_index  kospi_index
0 2011-01-01       2.5             93.0      2051.00
1 2011-01-02       2.5             93.0      2051.00
2 2011-01-03       2.5             93.0      2070.08
3 2011-01-04       2.5             93.0      2085.14
4 2011-01-05       2.5             93.0      2082.55

### 코스피지수의 필요성 그래프로 점검

In [ ]:
# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['kospi_index'],
                    mode='lines',
                    name='kospi_index',yaxis='y1'))



fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['apartment_index'],
                    mode='lines',
                    name='apartment_index',
                    yaxis="y2"))
fig.update_layout(

   # create first Y-axis
   yaxis=dict(
      title="kospi index",
      titlefont=dict(color="blue"),
      tickfont=dict(color="blue")
   ),

   # create second Y-axis
   yaxis2=dict(
      title="apartment index",
      overlaying="y",
      side="right")
)

- 코스피지수와 부동산 지수는 어느정도의 상관성은 있나? 그래프로 봐서는 잘 모르겠음

## 한국국채 금리 데이터프레임 생성

- 코스피 데이터프레임 생성과정과 거의 비슷

In [ ]:
import os


dir_path = "/content/drive/MyDrive/house_price/original_data/korean_bond"
file_list = os.listdir(dir_path)
file_list.sort()
name_list = list()
df_list = list()

# 해당 폴더 안에 있는 csv 파일들을 읽어서 리스트 안에 데이터프레임들을 담음
for csv_file in file_list:
    df_list.append(pd.read_csv(dir_path+"/"+csv_file , encoding='UTF8'))
    name_list.append(csv_file.split('.')[0])
for i in range(len(df_list)):
    df_korea = df_list[i] # 파일이 잘 들어갔는지 확인
    df_korea=df_korea.sort_index(ascending=False) # 날짜가 역순으로 되어 있어서 정렬
    df_korea.reset_index(drop=True, inplace=True) # index 재설정
    df_korea = df_korea[['날짜','종가']]
    df_korea.columns = ['korea_date',name_list[i]]
    df_korea['korea_date'] = pd.to_datetime(df_korea['korea_date'])
    df_final=pd.merge(df_final, df_korea, left_on='date', right_on='korea_date', how='left')
    df_final[name_list[i]]=df_final[name_list[i]].fillna(method='ffill') # 중간 공휴일들을 처리
    df_final[name_list[i]]=df_final[name_list[i]].fillna(method='bfill') # 제일 위의 있는 값을 근처 값으로 처리
    df_final = df_final.drop(['korea_date'], axis=1)

In [ ]:
df_final.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4383 entries, 0 to 4382
Data columns (total 11 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   date             4383 non-null   datetime64[ns]
 1   korea_rp         4383 non-null   float64       
 2   apartment_index  4383 non-null   float64       
 3   kospi_index      4383 non-null   float64       
 4   korea_10_year    4383 non-null   float64       
 5   korea_1_year     4383 non-null   float64       
 6   korea_20_year    4383 non-null   float64       
 7   korea_2_year     4383 non-null   float64       
 8   korea_3_year     4383 non-null   float64       
 9   korea_4_year     4383 non-null   float64       
 10  korea_5_year     4383 non-null   float64       
dtypes: datetime64[ns](1), float64(10)
memory usage: 410.9 KB


In [ ]:
# 컬럼 순서 변경
df_final = df_final[['date', 'apartment_index','kospi_index','korea_rp',
                    'korea_1_year','korea_2_year','korea_3_year','korea_4_year','korea_5_year',
                    'korea_10_year','korea_20_year']]
df_final.head()

date  apartment_index  kospi_index  korea_rp  korea_1_year  \
0 2011-01-01             93.0      2051.00       2.5          2.81   
1 2011-01-02             93.0      2051.00       2.5          2.81   
2 2011-01-03             93.0      2070.08       2.5          2.81   
3 2011-01-04             93.0      2085.14       2.5          2.83   
4 2011-01-05             93.0      2082.55       2.5          2.80   

   korea_2_year  korea_3_year  korea_4_year  korea_5_year  korea_10_year  \
0          3.40         3.440          4.09          4.14           4.57   
1          3.40         3.440          4.09          4.14           4.57   
2          3.40         3.440          4.09          4.14           4.57   
3          3.37         3.495          4.16          4.20           4.58   
4          3.42         3.495          4.15          4.17           4.63   

   korea_20_year  
0           4.73  
1           4.73  
2           4.73  
3           4.74  
4           4.75

In [ ]:
# 년,월,일일 컬럼 생성
df_final['year'] = df_final['date'].dt.year
df_final['month'] = df_final['date'].dt.month
df_final['day'] = df_final['date'].dt.day
df_final.head()

date  apartment_index  kospi_index  korea_rp  korea_1_year  \
0 2011-01-01             93.0      2051.00       2.5          2.81   
1 2011-01-02             93.0      2051.00       2.5          2.81   
2 2011-01-03             93.0      2070.08       2.5          2.81   
3 2011-01-04             93.0      2085.14       2.5          2.83   
4 2011-01-05             93.0      2082.55       2.5          2.80   

   korea_2_year  korea_3_year  korea_4_year  korea_5_year  korea_10_year  \
0          3.40         3.440          4.09          4.14           4.57   
1          3.40         3.440          4.09          4.14           4.57   
2          3.40         3.440          4.09          4.14           4.57   
3          3.37         3.495          4.16          4.20           4.58   
4          3.42         3.495          4.15          4.17           4.63   

   korea_20_year  year  month  day  
0           4.73  2011      1    1  
1           4.73  2011      1    2  
2           4.73  2011      1    3  
3           4.74  2011      1    4  
4           4.75  2011      1    5

### 부동산지수와 한국국채금리 시각화

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_rp'],
                    mode='lines',
                    name='korea_rp',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_1_year'],
                    mode='lines',
                    name='korea_1_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_2_year'],
                    mode='lines',
                    name='korea_2_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_3_year'],
                    mode='lines',
                    name='korea_3_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_4_year'],
                    mode='lines',
                    name='korea_4_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_5_year'],
                    mode='lines',
                    name='korea_5_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_10_year'],
                    mode='lines',
                    name='korea_10_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_20_year'],
                    mode='lines',
                    name='korea_20_year',yaxis='y1'))

# 앞에서의 그래프들은 뒤집기
fig.update_layout(
    yaxis = dict(autorange="reversed")
)
fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['apartment_index'],
                    mode='lines',
                    name='apartment_index',
                    yaxis="y2"))
fig.update_layout(

   # create first Y-axis
   yaxis=dict(
      title="rate index",
      titlefont=dict(color="black"),
      tickfont=dict(color="black")
   ),

   # create second Y-axis
   yaxis2=dict(
      title="apartment index",
      overlaying="y",
      side="right")
)

- 한국국채금리(역)과 부동산지수는 연관이 있는듯

In [ ]:
# 금리들이 얼추 비슷한 흐름을 보임으로 국채에서 3년과 10년만 사용
df_final = df_final[['date','year','month','day','apartment_index','kospi_index','korea_rp',
                    'korea_3_year','korea_10_year']]
df_final.head()

date  year  month  day  apartment_index  kospi_index  korea_rp  \
0 2011-01-01  2011      1    1             93.0      2051.00       2.5   
1 2011-01-02  2011      1    2             93.0      2051.00       2.5   
2 2011-01-03  2011      1    3             93.0      2070.08       2.5   
3 2011-01-04  2011      1    4             93.0      2085.14       2.5   
4 2011-01-05  2011      1    5             93.0      2082.55       2.5   

   korea_3_year  korea_10_year  
0         3.440           4.57  
1         3.440           4.57  
2         3.440           4.57  
3         3.495           4.58  
4         3.495           4.63

## 미국금채 금리 데이터프레임 생성

- 한국국채금리 데이터프레임 생성과정과 거의 동일

In [ ]:
# 변수들 초기화
dir_path = "/content/drive/MyDrive/house_price/original_data/us_bond"
file_list = os.listdir(dir_path)
file_list.sort()
name_list = list()
df_list = list()

# 해당 폴더 안에 있는 csv 파일들을 읽어서 리스트 안에 데이터프레임들을 담음
for csv_file in file_list:
    df_list.append(pd.read_csv(dir_path+"/"+csv_file , encoding='UTF8'))
    name_list.append(csv_file.split('.')[0])
for i in range(len(df_list)):
    df_us = df_list[i]
    df_us=df_us.sort_index(ascending=False) # 날짜가 역순으로 되어 있어서 정렬
    df_us.reset_index(drop=True, inplace=True) # index 재설정
    df_us = df_us[['날짜','종가']]
    df_us.columns = ['us_date',name_list[i]]
    df_us['us_date'] = pd.to_datetime(df_us['us_date'])
    df_final=pd.merge(df_final, df_us, left_on='date', right_on='us_date', how='left')
    df_final[name_list[i]]=df_final[name_list[i]].fillna(method='ffill') # 중간 공휴일들을 처리
    df_final[name_list[i]]=df_final[name_list[i]].fillna(method='bfill') # 제일 위의 있는 값을 근처 값으로 처리
    df_final = df_final.drop(['us_date'], axis=1)

In [ ]:
df_final.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4383 entries, 0 to 4382
Data columns (total 17 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   date             4383 non-null   datetime64[ns]
 1   year             4383 non-null   int64         
 2   month            4383 non-null   int64         
 3   day              4383 non-null   int64         
 4   apartment_index  4383 non-null   float64       
 5   kospi_index      4383 non-null   float64       
 6   korea_rp         4383 non-null   float64       
 7   korea_3_year     4383 non-null   float64       
 8   korea_10_year    4383 non-null   float64       
 9   us_10_year       4383 non-null   float64       
 10  us_1_month       4383 non-null   float64       
 11  us_2_year        4383 non-null   float64       
 12  us_30_year       4383 non-null   float64       
 13  us_3_month       4383 non-null   float64       
 14  us_3_year        4383 non-null   float64

In [ ]:
df_final = df_final[['date','year','month','day','apartment_index','kospi_index','korea_rp',
                    'korea_3_year','korea_10_year','us_1_month','us_3_month',
                    'us_6_month','us_2_year', 'us_3_year', 'us_5_year',
                    'us_10_year','us_30_year']]

In [ ]:
df_final.head()

date  year  month  day  apartment_index  kospi_index  korea_rp  \
0 2011-01-01  2011      1    1             93.0      2051.00       2.5   
1 2011-01-02  2011      1    2             93.0      2051.00       2.5   
2 2011-01-03  2011      1    3             93.0      2070.08       2.5   
3 2011-01-04  2011      1    4             93.0      2085.14       2.5   
4 2011-01-05  2011      1    5             93.0      2082.55       2.5   

   korea_3_year  korea_10_year  us_1_month  us_3_month  us_6_month  us_2_year  \
0         3.440           4.57       0.096       0.124       0.183      0.601   
1         3.440           4.57       0.096       0.124       0.183      0.601   
2         3.440           4.57       0.096       0.124       0.183      0.601   
3         3.495           4.58       0.106       0.142       0.187      0.621   
4         3.495           4.63       0.129       0.142       0.184      0.708   

   us_3_year  us_5_year  us_10_year  us_30_year  
0      1.006      2.011       3.334       4.401  
1      1.006      2.011       3.334       4.401  
2      1.006      2.011       3.334       4.401  
3      1.026      2.016       3.338       4.422  
4      1.129      2.133       3.463       4.541

### 미국국채금리와 부동산 지수 비교

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_1_month'],
                    mode='lines',
                    name='us_1_month',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_3_month'],
                    mode='lines',
                    name='us_3_month',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_6_month'],
                    mode='lines',
                    name='us_6_month',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_2_year'],
                    mode='lines',
                    name='us_2_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_3_year'],
                    mode='lines',
                    name='us_3_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_5_year'],
                    mode='lines',
                    name='us_5_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_10_year'],
                    mode='lines',
                    name='us_10_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_30_year'],
                    mode='lines',
                    name='us_30_year',yaxis='y1'))

# 앞에서의 그래프들은 뒤집기
fig.update_layout(
    yaxis = dict(autorange="reversed")
)
fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['apartment_index'],
                    mode='lines',
                    name='apartment_index',
                    yaxis="y2"))
fig.update_layout(

   # create first Y-axis
   yaxis=dict(
      title="rate index",
      titlefont=dict(color="black"),
      tickfont=dict(color="black")
   ),

   # create second Y-axis
   yaxis2=dict(
      title="apartment index",
      overlaying="y",
      side="right")
)

- 미국 국채금리(역)은 한국 국채금리(역)보다는 부동산지수와 어느정도 연관이 있는듯?

In [ ]:
# 금리들이 얼추 비슷한 흐름을 보임으로 국채에서 3개월, 2년, 10년 데이터프레임을 생성
df_final = df_final[['date','year','month','day','apartment_index','kospi_index','korea_rp',
                    'korea_3_year','korea_10_year','us_3_month', 'us_2_year', 'us_10_year']]
df_final.head()

date  year  month  day  apartment_index  kospi_index  korea_rp  \
0 2011-01-01  2011      1    1             93.0      2051.00       2.5   
1 2011-01-02  2011      1    2             93.0      2051.00       2.5   
2 2011-01-03  2011      1    3             93.0      2070.08       2.5   
3 2011-01-04  2011      1    4             93.0      2085.14       2.5   
4 2011-01-05  2011      1    5             93.0      2082.55       2.5   

   korea_3_year  korea_10_year  us_3_month  us_2_year  us_10_year  
0         3.440           4.57       0.124      0.601       3.334  
1         3.440           4.57       0.124      0.601       3.334  
2         3.440           4.57       0.124      0.601       3.334  
3         3.495           4.58       0.142      0.621       3.338  
4         3.495           4.63       0.142      0.708       3.463


## 금리차 컬럼들 추가

In [ ]:
# 금리차 컬럼들을 추가
df_final['korea_10-3_year'] = df_final['korea_10_year'] - df_final['korea_3_year']
df_final['us_10-2_year'] = df_final['us_10_year'] - df_final['us_2_year']
df_final['us_10-3_year_month'] = df_final['us_10_year'] - df_final['us_3_month']
df_final

date  year  month  day  apartment_index  kospi_index  korea_rp  \
0    2011-01-01  2011      1    1             93.0      2051.00      2.50   
1    2011-01-02  2011      1    2             93.0      2051.00      2.50   
2    2011-01-03  2011      1    3             93.0      2070.08      2.50   
3    2011-01-04  2011      1    4             93.0      2085.14      2.50   
4    2011-01-05  2011      1    5             93.0      2082.55      2.50   
...         ...   ...    ...  ...              ...          ...       ...   
4378 2022-12-27  2022     12   27            104.4      2332.79      3.25   
4379 2022-12-28  2022     12   28            104.4      2280.45      3.25   
4380 2022-12-29  2022     12   29            104.4      2236.40      3.25   
4381 2022-12-30  2022     12   30            104.4      2236.40      3.25   
4382 2022-12-31  2022     12   31            104.4      2236.40      3.25   

      korea_3_year  korea_10_year  us_3_month  us_2_year  us_10_year  \
0            3.440          4.570       0.124     0.6010       3.334   
1            3.440          4.570       0.124     0.6010       3.334   
2            3.440          4.570       0.124     0.6010       3.334   
3            3.495          4.580       0.142     0.6210       3.338   
4            3.495          4.630       0.142     0.7080       3.463   
...            ...            ...         ...        ...         ...   
4378         3.661          3.612       4.311     4.3827       3.849   
4379         3.668          3.675       4.457     4.3574       3.886   
4380         3.718          3.723       4.423     4.3656       3.820   
4381         3.725          3.735       4.405     4.4279       3.879   
4382         3.725          3.735       4.405     4.4279       3.879   

      korea_10-3_year  us_10-2_year  us_10-3_year_month  
0               1.130        2.7330               3.210  
1               1.130        2.7330               3.210  
2               1.130        2.7330               3.210  
3               1.085        2.7170               3.196  
4               1.135        2.7550               3.321  
...               ...           ...                 ...  
4378           -0.049       -0.5337              -0.462  
4379            0.007       -0.4714              -0.571  
4380            0.005       -0.5456              -0.603  
4381            0.010       -0.5489              -0.526  
4382            0.010       -0.5489              -0.526  

[4383 rows x 15 columns]

## 아파트 분양 공급 데이터프레임 생성

- https://asil.kr/asil/sub/movein.jsp 사이트를 통해서 아파트 공급량의 정보를 확보

In [ ]:
# txt 파일을 불러옴옴
df_apartment_supply = pd.read_csv("/content/drive/MyDrive/house_price/original_data/apartment_supply.txt",  encoding='UTF8',sep="\t")
df_apartment_supply.head()

위치                단지명       입주년월     총세대수
0  서울 서대문구 홍은동       e편한세상홍제가든플라츠  2022년 12월    481세대
1   서울 서초구 잠원동              르엘신반포  2022년 12월    280세대
2   서울 마포구 아현동             마포더클래시  2022년 12월  1,419세대
3   서울 중랑구 면목동  봄작시티201(민간임대,도시형)  2022년 12월    128세대
4  서울 서대문구 홍은동        힐스테이트홍은포레스트  2022년 11월    623세대

In [ ]:
df_apartment_supply.info() # 데이터프레임 정보 확인 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1003 entries, 0 to 1002
Data columns (total 4 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   위치      1003 non-null   object
 1   단지명     1003 non-null   object
 2   입주년월    1003 non-null   object
 3   총세대수    1003 non-null   object
dtypes: object(4)
memory usage: 31.5+ KB


In [ ]:
# 년, 월 컬럼들 생성
# ' ' 을 기준으로 잘라서 컬럼들을 생성
df_apartment_supply['year'] =df_apartment_supply['입주년월'].str.split(' ',expand=True)[0]
df_apartment_supply['month'] =df_apartment_supply['입주년월'].str.split(' ',expand=True)[1]

In [ ]:
df_apartment_supply.head()

위치                단지명       입주년월     총세대수   year month
0  서울 서대문구 홍은동       e편한세상홍제가든플라츠  2022년 12월    481세대  2022년   12월
1   서울 서초구 잠원동              르엘신반포  2022년 12월    280세대  2022년   12월
2   서울 마포구 아현동             마포더클래시  2022년 12월  1,419세대  2022년   12월
3   서울 중랑구 면목동  봄작시티201(민간임대,도시형)  2022년 12월    128세대  2022년   12월
4  서울 서대문구 홍은동        힐스테이트홍은포레스트  2022년 11월    623세대  2022년   11월

In [ ]:
df_apartment_supply.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1003 entries, 0 to 1002
Data columns (total 6 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   위치      1003 non-null   object
 1   단지명     1003 non-null   object
 2   입주년월    1003 non-null   object
 3   총세대수    1003 non-null   object
 4   year    1003 non-null   object
 5   month   1003 non-null   object
dtypes: object(6)
memory usage: 47.1+ KB


In [ ]:
# 문자열 특정 문자들 수정
# 추후 데이터프레임 계산에 용이하게 문자들을 수정 
df_apartment_supply["year"] = df_apartment_supply["year"].str.replace("년", "")
df_apartment_supply["month"] = df_apartment_supply["month"].str.replace("월", "")
df_apartment_supply["apartment_supply"] = df_apartment_supply["총세대수"].str.replace("세대", "")
df_apartment_supply["apartment_supply"] = df_apartment_supply["apartment_supply"].str.replace(",", "")
df_apartment_supply.head()

위치                단지명       입주년월     총세대수  year month  \
0  서울 서대문구 홍은동       e편한세상홍제가든플라츠  2022년 12월    481세대  2022    12   
1   서울 서초구 잠원동              르엘신반포  2022년 12월    280세대  2022    12   
2   서울 마포구 아현동             마포더클래시  2022년 12월  1,419세대  2022    12   
3   서울 중랑구 면목동  봄작시티201(민간임대,도시형)  2022년 12월    128세대  2022    12   
4  서울 서대문구 홍은동        힐스테이트홍은포레스트  2022년 11월    623세대  2022    11   

  apartment_supply  
0              481  
1              280  
2             1419  
3              128  
4              623

In [ ]:
df_apartment_supply.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1003 entries, 0 to 1002
Data columns (total 7 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   위치                1003 non-null   object
 1   단지명               1003 non-null   object
 2   입주년월              1003 non-null   object
 3   총세대수              1003 non-null   object
 4   year              1003 non-null   object
 5   month             1003 non-null   object
 6   apartment_supply  1003 non-null   object
dtypes: object(7)
memory usage: 55.0+ KB


In [ ]:
# date 컬럼 생성
df_apartment_supply['date'] = pd.to_datetime(df_apartment_supply['year']+'-'+df_apartment_supply['month'], format="%Y-%m")

- 해당 달의 수치의 결과는 다음달에 발표한다고 가정(예를들어 2011년 1월의 거래수치는 2011년 1월동안에는 알 수 없고 2월이 되어야 1월의 결과를 종합해서 수치를 알 수 있다)

In [ ]:
# 다음 달에 지수가 발표한다고 가정
df_apartment_supply['date_column'] = df_apartment_supply['date'] + datetime.timedelta(days=32)
df_apartment_supply['announcement_year'] = df_apartment_supply['date_column'].dt.year
df_apartment_supply['announcement_month'] = df_apartment_supply['date_column'].dt.month

In [ ]:
df_apartment_supply.head()

위치                단지명       입주년월     총세대수  year month  \
0  서울 서대문구 홍은동       e편한세상홍제가든플라츠  2022년 12월    481세대  2022    12   
1   서울 서초구 잠원동              르엘신반포  2022년 12월    280세대  2022    12   
2   서울 마포구 아현동             마포더클래시  2022년 12월  1,419세대  2022    12   
3   서울 중랑구 면목동  봄작시티201(민간임대,도시형)  2022년 12월    128세대  2022    12   
4  서울 서대문구 홍은동        힐스테이트홍은포레스트  2022년 11월    623세대  2022    11   

  apartment_supply       date date_column  announcement_year  \
0              481 2022-12-01  2023-01-02               2023   
1              280 2022-12-01  2023-01-02               2023   
2             1419 2022-12-01  2023-01-02               2023   
3              128 2022-12-01  2023-01-02               2023   
4              623 2022-11-01  2022-12-03               2022   

   announcement_month  
0                   1  
1                   1  
2                   1  
3                   1  
4                  12

In [ ]:
df_apartment_supply.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1003 entries, 0 to 1002
Data columns (total 11 columns):
 #   Column              Non-Null Count  Dtype         
---  ------              --------------  -----         
 0   위치                  1003 non-null   object        
 1   단지명                 1003 non-null   object        
 2   입주년월                1003 non-null   object        
 3   총세대수                1003 non-null   object        
 4   year                1003 non-null   object        
 5   month               1003 non-null   object        
 6   apartment_supply    1003 non-null   object        
 7   date                1003 non-null   datetime64[ns]
 8   date_column         1003 non-null   datetime64[ns]
 9   announcement_year   1003 non-null   int64         
 10  announcement_month  1003 non-null   int64         
dtypes: datetime64[ns](2), int64(2), object(7)
memory usage: 86.3+ KB


In [ ]:
# 사용할 컬럼만을 거른 후, 타입 변경
df_apartment_supply = df_apartment_supply[['announcement_year','announcement_month','apartment_supply']]
df_apartment_supply = df_apartment_supply.astype({'apartment_supply': 'int64'})
df_apartment_supply.head()

announcement_year  announcement_month  apartment_supply
0               2023                   1               481
1               2023                   1               280
2               2023                   1              1419
3               2023                   1               128
4               2022                  12               623

In [ ]:
df_apartment_supply.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1003 entries, 0 to 1002
Data columns (total 3 columns):
 #   Column              Non-Null Count  Dtype
---  ------              --------------  -----
 0   announcement_year   1003 non-null   int64
 1   announcement_month  1003 non-null   int64
 2   apartment_supply    1003 non-null   int64
dtypes: int64(3)
memory usage: 23.6 KB


In [ ]:
# 연, 월별 분양공급량을 group by를 통해서 구한 후, reset_index를 통해서 다시 컬럼화
df_apartment_supply=df_apartment_supply.groupby(['announcement_year','announcement_month'])['apartment_supply'].agg('sum')
df_apartment_supply = df_apartment_supply.reset_index(['announcement_year','announcement_month'])
df_apartment_supply.head()

announcement_year  announcement_month  apartment_supply
0               2011                   2              5342
1               2011                   3              3494
2               2011                   4              1511
3               2011                   5               709
4               2011                   6              1507

## 아파트 미분양 데이터 프레임 생성

- https://data.kbland.kr/publicdata/unsold-apartments 사이트를 통해서 미분양 데이터 정보를 확보

In [ ]:
df_apartment_unsold = pd.read_excel("/content/drive/MyDrive/house_price/original_data/unsold/서울 미분양 현황.xlsx")
df_apartment_unsold.index = df_apartment_unsold['구분']
df_apartment_unsold=df_apartment_unsold.drop('구분',axis=1)
df_apartment_unsold.head()

'07.01  '07.02  '07.03  '07.04  '07.05  '07.06  '07.07  '07.08  '07.09  \
구분                                                                           
미분양    697  590.00  687.00  685.00  704.00  778.00  840.00   730.0  724.00   
변동률      -  -15.35   16.44   -0.29    2.77   10.51    7.97   -13.1   -0.82   

     '07.10  ...  '22.02  '22.03  '22.04  '22.05  '22.06  '22.07  '22.08  \
구분           ...                                                           
미분양  977.00  ...      47  180.00     360  688.00  719.00  592.00  610.00   
변동률   34.94  ...       0  282.98     100   91.11    4.51  -17.66    3.04   

     '22.09  '22.10  '22.11  
구분                           
미분양  719.00  866.00  865.00  
변동률   17.87   20.45   -0.12  

[2 rows x 191 columns]

In [ ]:
# T 매소드를 통해서 row와 column을 교환환
df_apartment_unsold=df_apartment_unsold.T
df_apartment_unsold.head()

구분        미분양    변동률
'07.01    697      -
'07.02  590.0 -15.35
'07.03  687.0  16.44
'07.04  685.0  -0.29
'07.05  704.0   2.77

In [ ]:
df_apartment_unsold.info()

<class 'pandas.core.frame.DataFrame'>
Index: 191 entries, '07.01 to '22.11
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   미분양     191 non-null    object
 1   변동률     191 non-null    object
dtypes: object(2)
memory usage: 8.5+ KB


In [ ]:
# index가 날짜의 정보를 가지고 있음으로 reset_index를 통해서 날짜 정보를 컬럼으로 생성성
df_apartment_unsold = df_apartment_unsold.reset_index()
df_apartment_unsold.head()

구분   index    미분양    변동률
0   '07.01    697      -
1   '07.02  590.0 -15.35
2   '07.03  687.0  16.44
3   '07.04  685.0  -0.29
4   '07.05  704.0   2.77

In [ ]:
# 컬럼명 수정정
df_apartment_unsold.columns=['year_month','unsold_count','ratio']
df_apartment_unsold.head()

year_month unsold_count  ratio
0     '07.01          697      -
1     '07.02        590.0 -15.35
2     '07.03        687.0  16.44
3     '07.04        685.0  -0.29
4     '07.05        704.0   2.77

In [ ]:
# year_month 컬럼에서 ' 부분을 제거
df_apartment_unsold["year_month"] = df_apartment_unsold["year_month"].str.replace("'", "")
df_apartment_unsold.head()

year_month unsold_count  ratio
0      07.01          697      -
1      07.02        590.0 -15.35
2      07.03        687.0  16.44
3      07.04        685.0  -0.29
4      07.05        704.0   2.77

In [ ]:
# 연, 월 컬럼 생성성
df_apartment_unsold['year'] =df_apartment_unsold["year_month"].str.split('.',expand=True)[0]
df_apartment_unsold['month'] =df_apartment_unsold["year_month"].str.split('.',expand=True)[1]
df_apartment_unsold.head()

year_month unsold_count  ratio year month
0      07.01          697      -   07    01
1      07.02        590.0 -15.35   07    02
2      07.03        687.0  16.44   07    03
3      07.04        685.0  -0.29   07    04
4      07.05        704.0   2.77   07    05

In [ ]:
# 연 컬럼 수정 및 사용할 컬럼 선택택
df_apartment_unsold['year'] = '20'+df_apartment_unsold['year']
df_apartment_unsold = df_apartment_unsold[['year','month','unsold_count']]
df_apartment_unsold.head()

year month unsold_count
0  2007    01          697
1  2007    02        590.0
2  2007    03        687.0
3  2007    04        685.0
4  2007    05        704.0

In [ ]:
df_apartment_unsold.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 191 entries, 0 to 190
Data columns (total 3 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   year          191 non-null    object
 1   month         191 non-null    object
 2   unsold_count  191 non-null    object
dtypes: object(3)
memory usage: 4.6+ KB


In [ ]:
# 미분양에 대한 정보는 한달이 지나야 결과를 알 수 있다 가정정
df_apartment_unsold['date'] = pd.to_datetime(df_apartment_unsold['year']+'-'+df_apartment_unsold['month'], format="%Y-%m")
df_apartment_unsold['date_column'] = df_apartment_unsold['date'] + datetime.timedelta(days=32)
df_apartment_unsold['announcement_year'] = df_apartment_unsold['date_column'].dt.year
df_apartment_unsold['announcement_month'] = df_apartment_unsold['date_column'].dt.month
df_apartment_unsold = df_apartment_unsold[['announcement_year','announcement_month','unsold_count']]
df_apartment_unsold = df_apartment_unsold.astype({'unsold_count': 'int64'})
df_apartment_unsold.head()

announcement_year  announcement_month  unsold_count
0               2007                   2           697
1               2007                   3           590
2               2007                   4           687
3               2007                   5           685
4               2007                   6           704

In [ ]:
# 사용할 연도의의 범위만을 설정 
df_apartment_unsold=df_apartment_unsold[df_apartment_unsold['announcement_year']>=2011]
df_apartment_unsold.head()

announcement_year  announcement_month  unsold_count
47               2011                   1          2729
48               2011                   2          2269
49               2011                   3          2216
50               2011                   4          2104
51               2011                   5          1855

In [ ]:
df_apartment_unsold.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 144 entries, 47 to 190
Data columns (total 3 columns):
 #   Column              Non-Null Count  Dtype
---  ------              --------------  -----
 0   announcement_year   144 non-null    int64
 1   announcement_month  144 non-null    int64
 2   unsold_count        144 non-null    int64
dtypes: int64(3)
memory usage: 4.5 KB


## 아파트 분양 & 미분양 데이터 프레임 병합 

In [ ]:
df_apartment_supply.tail()

announcement_year  announcement_month  apartment_supply
139               2022                   9              1853
140               2022                  10              1552
141               2022                  11              1265
142               2022                  12              1759
143               2023                   1              2308

In [ ]:
df_apartment_supply.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 144 entries, 0 to 143
Data columns (total 3 columns):
 #   Column              Non-Null Count  Dtype
---  ------              --------------  -----
 0   announcement_year   144 non-null    int64
 1   announcement_month  144 non-null    int64
 2   apartment_supply    144 non-null    int64
dtypes: int64(3)
memory usage: 3.5 KB


In [ ]:
df_apartment_unsold.tail()

announcement_year  announcement_month  unsold_count
186               2022                   8           592
187               2022                   9           610
188               2022                  10           719
189               2022                  11           866
190               2022                  12           865

In [ ]:
df_apartment_unsold.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 144 entries, 47 to 190
Data columns (total 3 columns):
 #   Column              Non-Null Count  Dtype
---  ------              --------------  -----
 0   announcement_year   144 non-null    int64
 1   announcement_month  144 non-null    int64
 2   unsold_count        144 non-null    int64
dtypes: int64(3)
memory usage: 4.5 KB


In [ ]:
# 데이터 프레임 병합합
df_apartment_supply_unsold=pd.merge(df_apartment_supply, df_apartment_unsold, on=['announcement_year','announcement_month'], how='inner')
df_apartment_supply_unsold.tail()

announcement_year  announcement_month  apartment_supply  unsold_count
138               2022                   8              1736           592
139               2022                   9              1853           610
140               2022                  10              1552           719
141               2022                  11              1265           866
142               2022                  12              1759           865

In [ ]:
df_apartment_supply_unsold.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 143 entries, 0 to 142
Data columns (total 4 columns):
 #   Column              Non-Null Count  Dtype
---  ------              --------------  -----
 0   announcement_year   143 non-null    int64
 1   announcement_month  143 non-null    int64
 2   apartment_supply    143 non-null    int64
 3   unsold_count        143 non-null    int64
dtypes: int64(4)
memory usage: 5.6 KB


### 미분양 비율 컬럼 추가

In [ ]:
# 미분양 비율을 구함
df_apartment_supply_unsold['unsold_ratio'] = 100*(df_apartment_supply_unsold['unsold_count'] / df_apartment_supply_unsold['apartment_supply'])
df_apartment_supply_unsold.head()

announcement_year  announcement_month  apartment_supply  unsold_count  \
0               2011                   2              5342          2269   
1               2011                   3              3494          2216   
2               2011                   4              1511          2104   
3               2011                   5               709          1855   
4               2011                   6              1507          1785   

   unsold_ratio  
0     42.474729  
1     63.423011  
2    139.245533  
3    261.636107  
4    118.447246

In [ ]:
df_apartment_supply_unsold.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 143 entries, 0 to 142
Data columns (total 5 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   announcement_year   143 non-null    int64  
 1   announcement_month  143 non-null    int64  
 2   apartment_supply    143 non-null    int64  
 3   unsold_count        143 non-null    int64  
 4   unsold_ratio        143 non-null    float64
dtypes: float64(1), int64(4)
memory usage: 6.7 KB


## 최종 테이블에 병합

In [ ]:
# 데이터 병합
df_final=pd.merge(df_final, df_apartment_supply_unsold, left_on=['year','month'], right_on=['announcement_year','announcement_month'], how='left')
df_final = df_final.drop(["announcement_year", "announcement_month"], axis=1)
df_final.head()

date  year  month  day  apartment_index  kospi_index  korea_rp  \
0 2011-01-01  2011      1    1             93.0      2051.00       2.5   
1 2011-01-02  2011      1    2             93.0      2051.00       2.5   
2 2011-01-03  2011      1    3             93.0      2070.08       2.5   
3 2011-01-04  2011      1    4             93.0      2085.14       2.5   
4 2011-01-05  2011      1    5             93.0      2082.55       2.5   

   korea_3_year  korea_10_year  us_3_month  us_2_year  us_10_year  \
0         3.440           4.57       0.124      0.601       3.334   
1         3.440           4.57       0.124      0.601       3.334   
2         3.440           4.57       0.124      0.601       3.334   
3         3.495           4.58       0.142      0.621       3.338   
4         3.495           4.63       0.142      0.708       3.463   

   korea_10-3_year  us_10-2_year  us_10-3_year_month  apartment_supply  \
0            1.130         2.733               3.210               NaN   
1            1.130         2.733               3.210               NaN   
2            1.130         2.733               3.210               NaN   
3            1.085         2.717               3.196               NaN   
4            1.135         2.755               3.321               NaN   

   unsold_count  unsold_ratio  
0           NaN           NaN  
1           NaN           NaN  
2           NaN           NaN  
3           NaN           NaN  
4           NaN           NaN

In [ ]:
df_final.info() # 데이터프레임 정보 확인

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4383 entries, 0 to 4382
Data columns (total 18 columns):
 #   Column              Non-Null Count  Dtype         
---  ------              --------------  -----         
 0   date                4383 non-null   datetime64[ns]
 1   year                4383 non-null   int64         
 2   month               4383 non-null   int64         
 3   day                 4383 non-null   int64         
 4   apartment_index     4383 non-null   float64       
 5   kospi_index         4383 non-null   float64       
 6   korea_rp            4383 non-null   float64       
 7   korea_3_year        4383 non-null   float64       
 8   korea_10_year       4383 non-null   float64       
 9   us_3_month          4383 non-null   float64       
 10  us_2_year           4383 non-null   float64       
 11  us_10_year          4383 non-null   float64       
 12  korea_10-3_year     4383 non-null   float64       
 13  us_10-2_year        4383 non-null   float64     

In [ ]:
df_final.isnull().sum() # null data 있는지 확인

date                   0
year                   0
month                  0
day                    0
apartment_index        0
kospi_index            0
korea_rp               0
korea_3_year           0
korea_10_year          0
us_3_month             0
us_2_year              0
us_10_year             0
korea_10-3_year        0
us_10-2_year           0
us_10-3_year_month     0
apartment_supply      31
unsold_count          31
unsold_ratio          31
dtype: int64

In [ ]:
df_final = df_final.dropna(subset=['apartment_supply']) # 해당 컬럼에 null 값이 있기에 제거
df_final.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4352 entries, 31 to 4382
Data columns (total 18 columns):
 #   Column              Non-Null Count  Dtype         
---  ------              --------------  -----         
 0   date                4352 non-null   datetime64[ns]
 1   year                4352 non-null   int64         
 2   month               4352 non-null   int64         
 3   day                 4352 non-null   int64         
 4   apartment_index     4352 non-null   float64       
 5   kospi_index         4352 non-null   float64       
 6   korea_rp            4352 non-null   float64       
 7   korea_3_year        4352 non-null   float64       
 8   korea_10_year       4352 non-null   float64       
 9   us_3_month          4352 non-null   float64       
 10  us_2_year           4352 non-null   float64       
 11  us_10_year          4352 non-null   float64       
 12  korea_10-3_year     4352 non-null   float64       
 13  us_10-2_year        4352 non-null   float64    

In [ ]:
df_final.to_csv('/content/drive/MyDrive/house_price/after_data/ver_4/economic_data.csv',index=False)

# economic_data2 파일 생성 


In [ ]:
import pandas as pd
import numpy as np
# 데이터들 불러오기
df_deal = pd.read_csv("/content/drive/MyDrive/house_price/after_data/ver_4/apartment_deal.csv",  encoding='UTF8')
df_month_rent = pd.read_csv("/content/drive/MyDrive/house_price/after_data/ver_4/apartment_month_rent.csv",  encoding='UTF8')
df_full_rent = pd.read_csv("/content/drive/MyDrive/house_price/after_data/ver_4/apartment_full_rent.csv",  encoding='UTF8')
df_economic = pd.read_csv("/content/drive/MyDrive/house_price/after_data/ver_4/economic_data.csv",  encoding='UTF8')

- economic_data2 파일은 economic_data 파일에 월별 아파트 거래체결량들(매매체결량, 전세체결량,월세체결량) 정보를 추가한 파일
- '아파트 거래' 는 '아파트 매매', '아파트 전세', '아파트 월세' 를 합친 개념
- 아파트 월별 거래량은 해당 달에 체결된 서울 총 아파트 거래량을 의미

## 아파트 매매 체결량 데이터프레임 생성

In [ ]:
df_deal.head()

date  year  month  day address_0 address_1 address_2  address_3  \
0  2011-07-09  2011      7    9     서울특별시       강남구       개포동      655.0   
1  2011-07-28  2011      7   28     서울특별시       강남구       개포동      655.0   
2  2011-01-19  2011      1   19     서울특별시       강남구       개포동      658.0   
3  2011-09-02  2011      9    2     서울특별시       강남구       개포동      658.0   
4  2011-12-17  2011     12   17     서울특별시       강남구       개포동      658.0   

   address_4            name   area  deal_price  
0        2.0  개포2차현대아파트(220)  77.75       64000  
1        2.0  개포2차현대아파트(220)  77.75       65500  
2        1.0  개포6차우성아파트1동~8동  67.28       70500  
3        1.0  개포6차우성아파트1동~8동  79.97       85000  
4        1.0  개포6차우성아파트1동~8동  67.28       68000

In [ ]:
df_deal.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 882185 entries, 0 to 882184
Data columns (total 12 columns):
 #   Column      Non-Null Count   Dtype  
---  ------      --------------   -----  
 0   date        882185 non-null  object 
 1   year        882185 non-null  int64  
 2   month       882185 non-null  int64  
 3   day         882185 non-null  int64  
 4   address_0   882185 non-null  object 
 5   address_1   882185 non-null  object 
 6   address_2   882185 non-null  object 
 7   address_3   882185 non-null  float64
 8   address_4   882185 non-null  float64
 9   name        882185 non-null  object 
 10  area        882185 non-null  float64
 11  deal_price  882185 non-null  int64  
dtypes: float64(3), int64(4), object(5)
memory usage: 80.8+ MB


In [ ]:
# 서울 아파트 월별 거래량을 group by를 이용하여여 계산
df_count = df_deal.groupby(["year","month"])["name"].agg('count').copy()
df_count = df_count.reset_index(["year","month"]) # index로 있던 컬럼들을 다시 컬럼화
df_count.columns = ["year","month","deal_count"] # 컬럼명들 수정정
df_count

year  month  deal_count
0    2011      1        7179
1    2011      2        6026
2    2011      3        5419
3    2011      4        4028
4    2011      5        3836
..    ...    ...         ...
139  2022      8         760
140  2022      9         649
141  2022     10         574
142  2022     11         750
143  2022     12         888

[144 rows x 3 columns]

In [ ]:
df_count.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 144 entries, 0 to 143
Data columns (total 3 columns):
 #   Column      Non-Null Count  Dtype
---  ------      --------------  -----
 0   year        144 non-null    int64
 1   month       144 non-null    int64
 2   deal_count  144 non-null    int64
dtypes: int64(3)
memory usage: 3.5 KB


## 아파트 전세 체결량 데이터프레임 추가

- 아파트 매매 체결량 부분 참조

In [ ]:
df_full_rent.head()

date  year  month  day address_0 address_1 address_2  address_3  \
0  2011-01-05  2011      1    5     서울특별시       강남구       개포동      655.0   
1  2011-01-18  2011      1   18     서울특별시       강남구       개포동      655.0   
2  2011-02-01  2011      2    1     서울특별시       강남구       개포동      655.0   
3  2011-02-11  2011      2   11     서울특별시       강남구       개포동      655.0   
4  2011-02-24  2011      2   24     서울특별시       강남구       개포동      655.0   

   address_4            name   area  full_rent_price  
0        2.0  개포2차현대아파트(220)  77.75            35000  
1        2.0  개포2차현대아파트(220)  77.75            20000  
2        2.0  개포2차현대아파트(220)  77.75            24000  
3        2.0  개포2차현대아파트(220)  77.75            31000  
4        2.0  개포2차현대아파트(220)  77.75            30500

In [ ]:
df_temp = df_full_rent.groupby(["year","month"])["name"].agg('count').copy()
df_temp = df_temp.reset_index(["year","month"])
df_temp.columns = ["year","month","full_rent_count"]
df_temp

year  month  full_rent_count
0    2011      1            12336
1    2011      2            12261
2    2011      3            12121
3    2011      4             9754
4    2011      5             9280
..    ...    ...              ...
139  2022      8            11341
140  2022      9            10258
141  2022     10            10559
142  2022     11             8890
143  2022     12             8783

[144 rows x 3 columns]

In [ ]:
# 아파트 매매 체결량 데이터프레임과 아파트 전세 체결량 데이터프레임임을 병합합
df_count=pd.merge(df_count,df_temp, left_on=["year","month"], right_on=["year","month"], how="inner")
df_count.head()

year  month  deal_count  full_rent_count
0  2011      1        7179            12336
1  2011      2        6026            12261
2  2011      3        5419            12121
3  2011      4        4028             9754
4  2011      5        3836             9280

In [ ]:
df_count.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 144 entries, 0 to 143
Data columns (total 4 columns):
 #   Column           Non-Null Count  Dtype
---  ------           --------------  -----
 0   year             144 non-null    int64
 1   month            144 non-null    int64
 2   deal_count       144 non-null    int64
 3   full_rent_count  144 non-null    int64
dtypes: int64(4)
memory usage: 5.6 KB


## 아파트 월세 체결량 데이터프레임 추가

- 아파트 매매 체결량 데이터프레임 참조

In [ ]:
df_month_rent.head()

date  year  month  day address_0 address_1 address_2  address_3  \
0  2011-03-18  2011      3   18     서울특별시       강남구       개포동      658.0   
1  2011-04-09  2011      4    9     서울특별시       강남구       개포동      658.0   
2  2011-07-09  2011      7    9     서울특별시       강남구       개포동      658.0   
3  2011-09-19  2011      9   19     서울특별시       강남구       개포동      658.0   
4  2011-09-20  2011      9   20     서울특별시       강남구       개포동      658.0   

   address_4            name   area  rent_deposit  month_rent_price  
0        1.0  개포6차우성아파트1동~8동  79.97         19000                63  
1        1.0  개포6차우성아파트1동~8동  79.97         21000                35  
2        1.0  개포6차우성아파트1동~8동  79.97          3000               160  
3        1.0  개포6차우성아파트1동~8동  79.97          6000               140  
4        1.0  개포6차우성아파트1동~8동  79.97          5000               160

In [ ]:
df_temp = df_month_rent.groupby(["year","month"])["name"].agg('count').copy()
df_temp = df_temp.reset_index(["year","month"])
df_temp.columns = ["year","month","month_rent_count"]
df_temp

year  month  month_rent_count
0    2011      1              2514
1    2011      2              2711
2    2011      3              2775
3    2011      4              2210
4    2011      5              2168
..    ...    ...               ...
139  2022      8              7415
140  2022      9              7793
141  2022     10              7694
142  2022     11              7709
143  2022     12              8588

[144 rows x 3 columns]

In [ ]:
# 아파트 월세 거래량 데이터프레임을 추가하여 병합합
df_count=pd.merge(df_count,df_temp, left_on=["year","month"], right_on=["year","month"], how="inner")
df_count.head()

year  month  deal_count  full_rent_count  month_rent_count
0  2011      1        7179            12336              2514
1  2011      2        6026            12261              2711
2  2011      3        5419            12121              2775
3  2011      4        4028             9754              2210
4  2011      5        3836             9280              2168

In [ ]:
df_count.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 144 entries, 0 to 143
Data columns (total 5 columns):
 #   Column            Non-Null Count  Dtype
---  ------            --------------  -----
 0   year              144 non-null    int64
 1   month             144 non-null    int64
 2   deal_count        144 non-null    int64
 3   full_rent_count   144 non-null    int64
 4   month_rent_count  144 non-null    int64
dtypes: int64(5)
memory usage: 6.8 KB


## 월 정보들 shift

- 해당 달의 거래량은 다음달에 알 수 있음으로 한칸씩 shift(1달씩 미룸)

In [ ]:
df_count['deal_count'] = df_count['deal_count'].shift(1)
df_count['month_rent_count'] = df_count['month_rent_count'].shift(1)
df_count['full_rent_count'] = df_count['full_rent_count'].shift(1)

# 컬럼명 수정
df_count.columns = ['year','month','last_month_total_deal_count','last_month_total_full_rent_count', 'last_month_total_month_rent_count']
df_count

year  month  last_month_total_deal_count  \
0    2011      1                          NaN   
1    2011      2                       7179.0   
2    2011      3                       6026.0   
3    2011      4                       5419.0   
4    2011      5                       4028.0   
..    ...    ...                          ...   
139  2022      8                        688.0   
140  2022      9                        760.0   
141  2022     10                        649.0   
142  2022     11                        574.0   
143  2022     12                        750.0   

     last_month_total_full_rent_count  last_month_total_month_rent_count  
0                                 NaN                                NaN  
1                             12336.0                             2514.0  
2                             12261.0                             2711.0  
3                             12121.0                             2775.0  
4                              9754.0                             2210.0  
..                                ...                                ...  
139                           11654.0                             8916.0  
140                           11341.0                             7415.0  
141                           10258.0                             7793.0  
142                           10559.0                             7694.0  
143                            8890.0                             7709.0  

[144 rows x 5 columns]

In [ ]:
df_count.dropna(axis=0,inplace=True)
df_count.reset_index(inplace=True,drop=True)
df_count

year  month  last_month_total_deal_count  \
0    2011      2                       7179.0   
1    2011      3                       6026.0   
2    2011      4                       5419.0   
3    2011      5                       4028.0   
4    2011      6                       3836.0   
..    ...    ...                          ...   
138  2022      8                        688.0   
139  2022      9                        760.0   
140  2022     10                        649.0   
141  2022     11                        574.0   
142  2022     12                        750.0   

     last_month_total_full_rent_count  last_month_total_month_rent_count  
0                             12336.0                             2514.0  
1                             12261.0                             2711.0  
2                             12121.0                             2775.0  
3                              9754.0                             2210.0  
4                              9280.0                             2168.0  
..                                ...                                ...  
138                           11654.0                             8916.0  
139                           11341.0                             7415.0  
140                           10258.0                             7793.0  
141                           10559.0                             7694.0  
142                            8890.0                             7709.0  

[143 rows x 5 columns]

In [ ]:
df_count.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 143 entries, 0 to 142
Data columns (total 5 columns):
 #   Column                             Non-Null Count  Dtype  
---  ------                             --------------  -----  
 0   year                               143 non-null    int64  
 1   month                              143 non-null    int64  
 2   last_month_total_deal_count        143 non-null    float64
 3   last_month_total_full_rent_count   143 non-null    float64
 4   last_month_total_month_rent_count  143 non-null    float64
dtypes: float64(3), int64(2)
memory usage: 5.7 KB


## economic_data 와의 통합 

In [ ]:
df_economic.head()

date  year  month  day  apartment_index  kospi_index  korea_rp  \
0  2011-02-01  2011      2    1             93.0      2072.03      2.75   
1  2011-02-02  2011      2    2             93.0      2072.03      2.75   
2  2011-02-03  2011      2    3             93.0      2072.03      2.75   
3  2011-02-04  2011      2    4             93.0      2072.03      2.75   
4  2011-02-05  2011      2    5             93.0      2072.03      2.75   

   korea_3_year  korea_10_year  us_3_month  us_2_year  us_10_year  \
0          3.97           4.71       0.157      0.605       3.435   
1          3.97           4.71       0.157      0.664       3.479   
2          3.97           4.71       0.152      0.712       3.547   
3          3.97           4.71       0.152      0.752       3.638   
4          3.97           4.71       0.152      0.752       3.638   

   korea_10-3_year  us_10-2_year  us_10-3_year_month  apartment_supply  \
0             0.74         2.830               3.278            5342.0   
1             0.74         2.815               3.322            5342.0   
2             0.74         2.835               3.395            5342.0   
3             0.74         2.886               3.486            5342.0   
4             0.74         2.886               3.486            5342.0   

   unsold_count  unsold_ratio  
0        2269.0     42.474729  
1        2269.0     42.474729  
2        2269.0     42.474729  
3        2269.0     42.474729  
4        2269.0     42.474729

In [ ]:
# 거시경제 지표가 모든 날짜들에 대한 정보를 가지고 있음으로, year과 month를 통해서 병합
df_economic=pd.merge(df_economic, df_count, left_on=["year","month"], right_on=["year","month"], how="inner")
df_economic.head()

date  year  month  day  apartment_index  kospi_index  korea_rp  \
0  2011-02-01  2011      2    1             93.0      2072.03      2.75   
1  2011-02-02  2011      2    2             93.0      2072.03      2.75   
2  2011-02-03  2011      2    3             93.0      2072.03      2.75   
3  2011-02-04  2011      2    4             93.0      2072.03      2.75   
4  2011-02-05  2011      2    5             93.0      2072.03      2.75   

   korea_3_year  korea_10_year  us_3_month  ...  us_10_year  korea_10-3_year  \
0          3.97           4.71       0.157  ...       3.435             0.74   
1          3.97           4.71       0.157  ...       3.479             0.74   
2          3.97           4.71       0.152  ...       3.547             0.74   
3          3.97           4.71       0.152  ...       3.638             0.74   
4          3.97           4.71       0.152  ...       3.638             0.74   

   us_10-2_year  us_10-3_year_month  apartment_supply  unsold_count  \
0         2.830               3.278            5342.0        2269.0   
1         2.815               3.322            5342.0        2269.0   
2         2.835               3.395            5342.0        2269.0   
3         2.886               3.486            5342.0        2269.0   
4         2.886               3.486            5342.0        2269.0   

   unsold_ratio  last_month_total_deal_count  \
0     42.474729                       7179.0   
1     42.474729                       7179.0   
2     42.474729                       7179.0   
3     42.474729                       7179.0   
4     42.474729                       7179.0   

   last_month_total_full_rent_count  last_month_total_month_rent_count  
0                           12336.0                             2514.0  
1                           12336.0                             2514.0  
2                           12336.0                             2514.0  
3                           12336.0                             2514.0  
4                           12336.0                             2514.0  

[5 rows x 21 columns]

In [ ]:
df_economic.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4352 entries, 0 to 4351
Data columns (total 21 columns):
 #   Column                             Non-Null Count  Dtype  
---  ------                             --------------  -----  
 0   date                               4352 non-null   object 
 1   year                               4352 non-null   int64  
 2   month                              4352 non-null   int64  
 3   day                                4352 non-null   int64  
 4   apartment_index                    4352 non-null   float64
 5   kospi_index                        4352 non-null   float64
 6   korea_rp                           4352 non-null   float64
 7   korea_3_year                       4352 non-null   float64
 8   korea_10_year                      4352 non-null   float64
 9   us_3_month                         4352 non-null   float64
 10  us_2_year                          4352 non-null   float64
 11  us_10_year                         4352 non-null   float

In [ ]:
# 컬럼명이 헷갈리는 요소가 있어어

df_economic = df_economic.rename(columns={'apartment_supply':  'last_month_total_apartment_supply', 'unsold_count' : 'last_month_total_unsold_count', 
                                          'unsold_ratio' : 'last_month_total_unsold_ratio'})

df_economic.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4352 entries, 0 to 4351
Data columns (total 21 columns):
 #   Column                             Non-Null Count  Dtype  
---  ------                             --------------  -----  
 0   date                               4352 non-null   object 
 1   year                               4352 non-null   int64  
 2   month                              4352 non-null   int64  
 3   day                                4352 non-null   int64  
 4   apartment_index                    4352 non-null   float64
 5   kospi_index                        4352 non-null   float64
 6   korea_rp                           4352 non-null   float64
 7   korea_3_year                       4352 non-null   float64
 8   korea_10_year                      4352 non-null   float64
 9   us_3_month                         4352 non-null   float64
 10  us_2_year                          4352 non-null   float64
 11  us_10_year                         4352 non-null   float

In [ ]:
# 데이터프레임 타입 변경 
df_economic=df_economic.astype({'year': 'int16','month': 'int16',
                    'last_month_total_apartment_supply': 'int32',
                    'last_month_total_unsold_count': 'int32',
                    'last_month_total_deal_count': 'int32',
                    'last_month_total_full_rent_count': 'int32',
                    'last_month_total_month_rent_count': 'int32'})

In [ ]:
df_economic.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 143 entries, 0 to 142
Data columns (total 19 columns):
 #   Column                             Non-Null Count  Dtype  
---  ------                             --------------  -----  
 0   year                               143 non-null    int16  
 1   month                              143 non-null    int16  
 2   apartment_index                    143 non-null    float64
 3   kospi_index                        143 non-null    float64
 4   korea_rp                           143 non-null    float64
 5   korea_3_year                       143 non-null    float64
 6   korea_10_year                      143 non-null    float64
 7   us_3_month                         143 non-null    float64
 8   us_2_year                          143 non-null    float64
 9   us_10_year                         143 non-null    float64
 10  korea_10-3_year                    143 non-null    float64
 11  us_10-2_year                       143 non-null    float64

In [ ]:
df_economic.head()

date  year  month  day  apartment_index  kospi_index  korea_rp  \
0  2011-02-01  2011      2    1             93.0      2072.03      2.75   
1  2011-02-02  2011      2    2             93.0      2072.03      2.75   
2  2011-02-03  2011      2    3             93.0      2072.03      2.75   
3  2011-02-04  2011      2    4             93.0      2072.03      2.75   
4  2011-02-05  2011      2    5             93.0      2072.03      2.75   

   korea_3_year  korea_10_year  us_3_month  ...  us_10_year  korea_10-3_year  \
0          3.97           4.71       0.157  ...       3.435             0.74   
1          3.97           4.71       0.157  ...       3.479             0.74   
2          3.97           4.71       0.152  ...       3.547             0.74   
3          3.97           4.71       0.152  ...       3.638             0.74   
4          3.97           4.71       0.152  ...       3.638             0.74   

   us_10-2_year  us_10-3_year_month  last_month_total_apartment_supply  \
0         2.830               3.278                               5342   
1         2.815               3.322                               5342   
2         2.835               3.395                               5342   
3         2.886               3.486                               5342   
4         2.886               3.486                               5342   

   last_month_total_unsold_count  last_month_total_unsold_ratio  \
0                           2269                      42.474729   
1                           2269                      42.474729   
2                           2269                      42.474729   
3                           2269                      42.474729   
4                           2269                      42.474729   

   last_month_total_deal_count  last_month_total_full_rent_count  \
0                         7179                             12336   
1                         7179                             12336   
2                         7179                             12336   
3                         7179                             12336   
4                         7179                             12336   

   last_month_total_month_rent_count  
0                               2514  
1                               2514  
2                               2514  
3                               2514  
4                               2514  

[5 rows x 21 columns]

In [ ]:
# csv 파일 저장
df_economic.to_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/economic_data2.pkl')

# final_economic 파일 생성

- economic_data2 은 '해당 일자'에 대한 거시경제 지표들을 가지고 있다. 
- final_economic 파일은 economic_data2 파일에 추가적으로 과거 수치대비 변화에 대한 정보들을 추가한 파일

## 기본정보 파악

In [ ]:
import pandas as pd
# 데이터 프레임 불러오기기
df_economic = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/economic_data2.pkl')
df_economic.head()

date  year  month  day  apartment_index  kospi_index  korea_rp  \
0  2011-02-01  2011      2    1             93.0      2072.03      2.75   
1  2011-02-02  2011      2    2             93.0      2072.03      2.75   
2  2011-02-03  2011      2    3             93.0      2072.03      2.75   
3  2011-02-04  2011      2    4             93.0      2072.03      2.75   
4  2011-02-05  2011      2    5             93.0      2072.03      2.75   

   korea_3_year  korea_10_year  us_3_month  ...  us_10_year  korea_10-3_year  \
0          3.97           4.71       0.157  ...       3.435             0.74   
1          3.97           4.71       0.157  ...       3.479             0.74   
2          3.97           4.71       0.152  ...       3.547             0.74   
3          3.97           4.71       0.152  ...       3.638             0.74   
4          3.97           4.71       0.152  ...       3.638             0.74   

   us_10-2_year  us_10-3_year_month  last_month_total_apartment_supply  \
0         2.830               3.278                               5342   
1         2.815               3.322                               5342   
2         2.835               3.395                               5342   
3         2.886               3.486                               5342   
4         2.886               3.486                               5342   

   last_month_total_unsold_count  last_month_total_unsold_ratio  \
0                           2269                      42.474729   
1                           2269                      42.474729   
2                           2269                      42.474729   
3                           2269                      42.474729   
4                           2269                      42.474729   

   last_month_total_deal_count  last_month_total_full_rent_count  \
0                         7179                             12336   
1                         7179                             12336   
2                         7179                             12336   
3                         7179                             12336   
4                         7179                             12336   

   last_month_total_month_rent_count  
0                               2514  
1                               2514  
2                               2514  
3                               2514  
4                               2514  

[5 rows x 21 columns]

In [ ]:
df_economic.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4352 entries, 0 to 4351
Data columns (total 21 columns):
 #   Column                             Non-Null Count  Dtype  
---  ------                             --------------  -----  
 0   date                               4352 non-null   object 
 1   year                               4352 non-null   int16  
 2   month                              4352 non-null   int16  
 3   day                                4352 non-null   int64  
 4   apartment_index                    4352 non-null   float64
 5   kospi_index                        4352 non-null   float64
 6   korea_rp                           4352 non-null   float64
 7   korea_3_year                       4352 non-null   float64
 8   korea_10_year                      4352 non-null   float64
 9   us_3_month                         4352 non-null   float64
 10  us_2_year                          4352 non-null   float64
 11  us_10_year                         4352 non-null   float

## 6,12개월 전 대비 변화정도 계산

In [ ]:
# 월별 평균 값을 구한 데이터프레임 2개 구함(추후 병합에 사용)
df_economic_6m_before = df_economic.drop(['date','day','apartment_index'],axis=1).copy()
df_economic_6m_before = df_economic_6m_before.groupby(['year','month']).agg('mean').reset_index()


df_economic_12m_before = df_economic.drop(['date','day','apartment_index'],axis=1).copy()
df_economic_12m_before = df_economic_6m_before.groupby(['year','month']).agg('mean').reset_index()

df_economic_6m_before.head()

year  month  kospi_index  korea_rp  korea_3_year  korea_10_year  \
0  2011      2  2011.301786  2.750000      3.939286       4.745714   
1  2011      3  1999.638710  2.927419      3.745968       4.518387   
2  2011      4  2152.758000  3.000000      3.747000       4.483333   
3  2011      5  2126.069355  3.000000      3.673710       4.347742   
4  2011      6  2074.891667  3.175000      3.638500       4.240667   

   us_3_month  us_2_year  us_10_year  korea_10-3_year  us_10-2_year  \
0    0.127536   0.762071    3.565429         0.806429      2.803357   
1    0.095839   0.679452    3.404226         0.772419      2.724774   
2    0.056200   0.719767    3.434600         0.736333      2.714833   
3    0.035581   0.536161    3.152774         0.674032      2.616613   
4    0.032667   0.402067    2.976833         0.602167      2.574767   

   us_10-3_year_month  last_month_total_apartment_supply  \
0            3.437893                             5342.0   
1            3.308387                             3494.0   
2            3.378400                             1511.0   
3            3.117194                              709.0   
4            2.944167                             1507.0   

   last_month_total_unsold_count  last_month_total_unsold_ratio  \
0                         2269.0                      42.474729   
1                         2216.0                      63.423011   
2                         2104.0                     139.245533   
3                         1855.0                     261.636107   
4                         1785.0                     118.447246   

   last_month_total_deal_count  last_month_total_full_rent_count  \
0                       7179.0                           12336.0   
1                       6026.0                           12261.0   
2                       5419.0                           12121.0   
3                       4028.0                            9754.0   
4                       3836.0                            9280.0   

   last_month_total_month_rent_count  
0                             2514.0  
1                             2711.0  
2                             2775.0  
3                             2210.0  
4                             2168.0

In [ ]:
# 6달전 날짜들 구한
df_economic.loc[df_economic['month']<7, '6m_before_year'] = df_economic['year']-1
df_economic.loc[df_economic['month']<7, '6m_before_month'] = 12-(6-df_economic['month'])
df_economic.loc[df_economic['month']>=7, '6m_before_year'] = df_economic['year']
df_economic.loc[df_economic['month']>=7, '6m_before_month'] = df_economic['month']-6

# 12달전 날짜들 구한
df_economic.loc[:, '12m_before_year'] = df_economic['year']-1
df_economic.loc[:, '12m_before_month'] = df_economic['month']

df_economic=df_economic.astype({'6m_before_year': 'int16','6m_before_month': 'int16'})
df_economic.head()

date  year  month  day  apartment_index  kospi_index  korea_rp  \
0  2011-02-01  2011      2    1             93.0      2072.03      2.75   
1  2011-02-02  2011      2    2             93.0      2072.03      2.75   
2  2011-02-03  2011      2    3             93.0      2072.03      2.75   
3  2011-02-04  2011      2    4             93.0      2072.03      2.75   
4  2011-02-05  2011      2    5             93.0      2072.03      2.75   

   korea_3_year  korea_10_year  us_3_month  ...  \
0          3.97           4.71       0.157  ...   
1          3.97           4.71       0.157  ...   
2          3.97           4.71       0.152  ...   
3          3.97           4.71       0.152  ...   
4          3.97           4.71       0.152  ...   

   last_month_total_apartment_supply  last_month_total_unsold_count  \
0                               5342                           2269   
1                               5342                           2269   
2                               5342                           2269   
3                               5342                           2269   
4                               5342                           2269   

   last_month_total_unsold_ratio  last_month_total_deal_count  \
0                      42.474729                         7179   
1                      42.474729                         7179   
2                      42.474729                         7179   
3                      42.474729                         7179   
4                      42.474729                         7179   

   last_month_total_full_rent_count  last_month_total_month_rent_count  \
0                             12336                               2514   
1                             12336                               2514   
2                             12336                               2514   
3                             12336                               2514   
4                             12336                               2514   

   6m_before_year  6m_before_month  12m_before_year  12m_before_month  
0            2010                8             2010                 2  
1            2010                8             2010                 2  
2            2010                8             2010                 2  
3            2010                8             2010                 2  
4            2010                8             2010                 2  

[5 rows x 25 columns]

In [ ]:
# 추가할 컬럼들의 컬럼명들을 생성
temp_column_total_list = list()
month_num_list = [6,12] # 1개월,3개월,6개월,12개월 이전 자료들 생성
for i in month_num_list:
    column_list = list()
    column_list.append('year_'+str(i)+'m_before')
    column_list.append('month_'+str(i)+'m_before')
    column_list.append('kospi_index_'+str(i)+'m_before')
    column_list.append('korea_rp_'+str(i)+'m_before')
    column_list.append('korea_3_year_'+str(i)+'m_before')
    column_list.append('korea_10_year_'+str(i)+'m_before')
    column_list.append('us_3_month_'+str(i)+'m_before')
    column_list.append('us_2_year_'+str(i)+'m_before')
    column_list.append('us_10_year_'+str(i)+'m_before')
    column_list.append('korea_10-3_year_'+str(i)+'m_before')
    column_list.append('us_10-2_year_'+str(i)+'m_before')
    column_list.append('us_10-3_year_month_'+str(i)+'m_before')
    column_list.append('last_month_total_apartment_supply_'+str(i)+'m_before')
    column_list.append('last_month_total_unsold_count_'+str(i)+'m_before')
    column_list.append('last_month_total_unsold_ratio_'+str(i)+'m_before')
    column_list.append('last_month_total_deal_count_'+str(i)+'m_before')
    column_list.append('last_month_total_full_rent_count_'+str(i)+'m_before')
    column_list.append('last_month_total_month_rent_count_'+str(i)+'m_before')
    temp_column_total_list.append(column_list)

In [ ]:
temp_column_total_list[0]

['year_6m_before',
 'month_6m_before',
 'kospi_index_6m_before',
 'korea_rp_6m_before',
 'korea_3_year_6m_before',
 'korea_10_year_6m_before',
 'us_3_month_6m_before',
 'us_2_year_6m_before',
 'us_10_year_6m_before',
 'korea_10-3_year_6m_before',
 'us_10-2_year_6m_before',
 'us_10-3_year_month_6m_before',
 'last_month_total_apartment_supply_6m_before',
 'last_month_total_unsold_count_6m_before',
 'last_month_total_unsold_ratio_6m_before',
 'last_month_total_deal_count_6m_before',
 'last_month_total_full_rent_count_6m_before',
 'last_month_total_month_rent_count_6m_before']

In [ ]:
df_economic_6m_before.columns = temp_column_total_list[0]
df_economic_12m_before.columns = temp_column_total_list[1]

In [ ]:
pd.set_option('display.max_columns', 100)
df_economic = pd.merge(df_economic, df_economic_6m_before, left_on=['6m_before_year', '6m_before_month'], right_on=['year_6m_before','month_6m_before'], how='inner')
df_economic = pd.merge(df_economic, df_economic_12m_before, left_on=['12m_before_year', '12m_before_month'], right_on=['year_12m_before','month_12m_before'], how='inner')
df_economic = df_economic.drop(["6m_before_year", "6m_before_month", "12m_before_year", "12m_before_month", "year_6m_before", "month_6m_before","year_12m_before", "month_12m_before"], axis=1)
df_economic.head(20)

date  year  month  day  apartment_index  kospi_index  korea_rp  \
0   2012-02-01  2012      2    1             86.8      1959.24      3.25   
1   2012-02-02  2012      2    2             86.8      1984.30      3.25   
2   2012-02-03  2012      2    3             86.8      1972.34      3.25   
3   2012-02-04  2012      2    4             86.8      1972.34      3.25   
4   2012-02-05  2012      2    5             86.8      1972.34      3.25   
5   2012-02-06  2012      2    6             86.8      1973.13      3.25   
6   2012-02-07  2012      2    7             86.8      1981.59      3.25   
7   2012-02-08  2012      2    8             86.8      2003.73      3.25   
8   2012-02-09  2012      2    9             86.8      2014.62      3.25   
9   2012-02-10  2012      2   10             86.8      1993.71      3.25   
10  2012-02-11  2012      2   11             86.8      1993.71      3.25   
11  2012-02-12  2012      2   12             86.8      1993.71      3.25   
12  2012-02-13  2012      2   13             86.8      2005.74      3.25   
13  2012-02-14  2012      2   14             86.8      2002.64      3.25   
14  2012-02-15  2012      2   15             86.8      2025.32      3.25   
15  2012-02-16  2012      2   16             86.8      1997.45      3.25   
16  2012-02-17  2012      2   17             86.8      2023.47      3.25   
17  2012-02-18  2012      2   18             86.8      2023.47      3.25   
18  2012-02-19  2012      2   19             86.8      2023.47      3.25   
19  2012-02-20  2012      2   20             86.8      2024.90      3.25   

    korea_3_year  korea_10_year  us_3_month  us_2_year  us_10_year  \
0          3.380           3.75       0.061      0.226       1.830   
1          3.380           3.76       0.084      0.226       1.823   
2          3.380           3.76       0.079      0.238       1.924   
3          3.380           3.76       0.079      0.238       1.924   
4          3.380           3.76       0.079      0.238       1.924   
5          3.390           3.78       0.086      0.234       1.901   
6          3.410           3.81       0.081      0.250       1.977   
7          3.440           3.83       0.081      0.258       1.982   
8          3.450           3.81       0.091      0.266       2.036   
9          3.455           3.82       0.089      0.278       1.984   
10         3.455           3.82       0.089      0.278       1.984   
11         3.455           3.82       0.089      0.278       1.984   
12         3.440           3.83       0.102      0.290       1.978   
13         3.445           3.82       0.117      0.290       1.938   
14         3.445           3.83       0.112      0.270       1.933   
15         3.375           3.81       0.104      0.294       1.984   
16         3.455           3.83       0.081      0.294       2.000   
17         3.455           3.83       0.081      0.294       2.000   
18         3.455           3.83       0.081      0.294       2.000   
19         3.470           3.85       0.076      0.294       2.038   

    korea_10-3_year  us_10-2_year  us_10-3_year_month  \
0             0.370         1.604               1.769   
1             0.380         1.597               1.739   
2             0.380         1.686               1.845   
3             0.380         1.686               1.845   
4             0.380         1.686               1.845   
5             0.390         1.667               1.815   
6             0.400         1.727               1.896   
7             0.390         1.724               1.901   
8             0.360         1.770               1.945   
9             0.365         1.706               1.895   
10            0.365         1.706               1.895   
11            0.365         1.706               1.895   
12            0.390         1.688               1.876   
13            0.375         1.648               1.821   
14            0.385         1.663               1.821   
15            0.435         1.

- 처음에 변화율을 구하려 했지만, 수치가 0인 값들이 있어서 계산을 할 때 null이나 inf가 되는 경우들이 있어서 변화율보다는 변화정도로 진행을 하기로 함

>> 계산식을 생성할 때, 0으로 나누거나 나누어지는 경우들에 대해서 조심해야 한다

In [ ]:
column_list = list()
column_list.append(['kospi_index', 'korea_rp',
       'korea_3_year', 'korea_10_year', 'us_3_month', 'us_2_year',
       'us_10_year', 'korea_10-3_year', 'us_10-2_year', 'us_10-3_year_month',
       'last_month_total_apartment_supply', 'last_month_total_unsold_count',
       'last_month_total_unsold_ratio', 'last_month_total_deal_count',
       'last_month_total_full_rent_count', 'last_month_total_month_rent_count'])
column_list

[['kospi_index',
  'korea_rp',
  'korea_3_year',
  'korea_10_year',
  'us_3_month',
  'us_2_year',
  'us_10_year',
  'korea_10-3_year',
  'us_10-2_year',
  'us_10-3_year_month',
  'last_month_total_apartment_supply',
  'last_month_total_unsold_count',
  'last_month_total_unsold_ratio',
  'last_month_total_deal_count',
  'last_month_total_full_rent_count',
  'last_month_total_month_rent_count']]

In [ ]:
column_list.append(temp_column_total_list[0][2:])
column_list.append(temp_column_total_list[1][2:])
column_list

[['kospi_index',
  'korea_rp',
  'korea_3_year',
  'korea_10_year',
  'us_3_month',
  'us_2_year',
  'us_10_year',
  'korea_10-3_year',
  'us_10-2_year',
  'us_10-3_year_month',
  'last_month_total_apartment_supply',
  'last_month_total_unsold_count',
  'last_month_total_unsold_ratio',
  'last_month_total_deal_count',
  'last_month_total_full_rent_count',
  'last_month_total_month_rent_count'],
 ['kospi_index_6m_before',
  'korea_rp_6m_before',
  'korea_3_year_6m_before',
  'korea_10_year_6m_before',
  'us_3_month_6m_before',
  'us_2_year_6m_before',
  'us_10_year_6m_before',
  'korea_10-3_year_6m_before',
  'us_10-2_year_6m_before',
  'us_10-3_year_month_6m_before',
  'last_month_total_apartment_supply_6m_before',
  'last_month_total_unsold_count_6m_before',
  'last_month_total_unsold_ratio_6m_before',
  'last_month_total_deal_count_6m_before',
  'last_month_total_full_rent_count_6m_before',
  'last_month_total_month_rent_count_6m_before'],
 ['kospi_index_12m_before',
  'korea_rp_12m_

In [ ]:
# 변화정도 = 현재데이터 - 과거데이터 
for i in range(len(column_list[0])):
  df_economic[column_list[1][i]] = df_economic[column_list[0][i]] - df_economic[column_list[1][i]]
  df_economic[column_list[2][i]] = df_economic[column_list[0][i]] - df_economic[column_list[2][i]]
df_economic

date  year  month  day  apartment_index  kospi_index  korea_rp  \
0     2012-02-01  2012      2    1             86.8      1959.24      3.25   
1     2012-02-02  2012      2    2             86.8      1984.30      3.25   
2     2012-02-03  2012      2    3             86.8      1972.34      3.25   
3     2012-02-04  2012      2    4             86.8      1972.34      3.25   
4     2012-02-05  2012      2    5             86.8      1972.34      3.25   
...          ...   ...    ...  ...              ...          ...       ...   
3982  2022-12-27  2022     12   27            104.4      2332.79      3.25   
3983  2022-12-28  2022     12   28            104.4      2280.45      3.25   
3984  2022-12-29  2022     12   29            104.4      2236.40      3.25   
3985  2022-12-30  2022     12   30            104.4      2236.40      3.25   
3986  2022-12-31  2022     12   31            104.4      2236.40      3.25   

      korea_3_year  korea_10_year  us_3_month  us_2_year  us_10_year  \
0            3.380          3.750       0.061     0.2260       1.830   
1            3.380          3.760       0.084     0.2260       1.823   
2            3.380          3.760       0.079     0.2380       1.924   
3            3.380          3.760       0.079     0.2380       1.924   
4            3.380          3.760       0.079     0.2380       1.924   
...            ...            ...         ...        ...         ...   
3982         3.661          3.612       4.311     4.3827       3.849   
3983         3.668          3.675       4.457     4.3574       3.886   
3984         3.718          3.723       4.423     4.3656       3.820   
3985         3.725          3.735       4.405     4.4279       3.879   
3986         3.725          3.735       4.405     4.4279       3.879   

      korea_10-3_year  us_10-2_year  us_10-3_year_month  \
0               0.370        1.6040               1.769   
1               0.380        1.5970               1.739   
2               0.380        1.6860               1.845   
3               0.380        1.6860               1.845   
4               0.380        1.6860               1.845   
...               ...           ...                 ...   
3982           -0.049       -0.5337              -0.462   
3983            0.007       -0.4714              -0.571   
3984            0.005       -0.5456              -0.603   
3985            0.010       -0.5489              -0.526   
3986            0.010       -0.5489              -0.526   

      last_month_total_apartment_supply  last_month_total_unsold_count  \
0                                  1822                           1890   
1                                  1822                           1890   
2                                  1822                           1890   
3                                  1822                           1890   
4                                  1822                           1890   
...                                 ...                            ...   
3982                               1759                            865   
3983                               1759                            865   
3984                               1759                            865   
3985                               1759                            865   
3986                               1759                            865   

      last_month_total_unsold_ratio  last_month_total_deal_count  \
0                        103.732162                         2786   
1                        103.732162                         2786   
2                        103.732162                         2786   
3                        103.732162                         2786   
4                        103.732162                         2786   
...                             ...                          ...   
3982                      49.175668                          750   
3983                      49.175668                          750   


In [ ]:
# inf 값들을 null값로 수정한 후, null 값을 구해서 inf값과 null 값을 동시에 구함
import numpy as np
df_economic.replace([np.inf, -np.inf], np.nan, inplace=True)
var = df_economic.isnull().sum()
print(var.to_string())

date                                            0
year                                            0
month                                           0
day                                             0
apartment_index                                 0
kospi_index                                     0
korea_rp                                        0
korea_3_year                                    0
korea_10_year                                   0
us_3_month                                      0
us_2_year                                       0
us_10_year                                      0
korea_10-3_year                                 0
us_10-2_year                                    0
us_10-3_year_month                              0
last_month_total_apartment_supply               0
last_month_total_unsold_count                   0
last_month_total_unsold_ratio                   0
last_month_total_deal_count                     0
last_month_total_full_rent_count                0


In [ ]:
df_economic.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3987 entries, 0 to 3986
Data columns (total 53 columns):
 #   Column                                        Non-Null Count  Dtype  
---  ------                                        --------------  -----  
 0   date                                          3987 non-null   object 
 1   year                                          3987 non-null   int16  
 2   month                                         3987 non-null   int16  
 3   day                                           3987 non-null   int64  
 4   apartment_index                               3987 non-null   float64
 5   kospi_index                                   3987 non-null   float64
 6   korea_rp                                      3987 non-null   float64
 7   korea_3_year                                  3987 non-null   float64
 8   korea_10_year                                 3987 non-null   float64
 9   us_3_month                                    3987 non-null   f

In [ ]:
# type 이 floay64 인 컬럼을 float32로 변경, 메모리 사용량을 줄이기 위해서서
df_economic_columns = list(df_economic.columns)
for df_economic_column in df_economic_columns:
    if df_economic[df_economic_column].dtypes =='float64':
        df_economic[df_economic_column]=df_economic[df_economic_column].astype('float32')
    else:
        pass

In [ ]:
df_economic.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3987 entries, 0 to 3986
Data columns (total 53 columns):
 #   Column                                        Non-Null Count  Dtype  
---  ------                                        --------------  -----  
 0   date                                          3987 non-null   object 
 1   year                                          3987 non-null   int16  
 2   month                                         3987 non-null   int16  
 3   day                                           3987 non-null   int64  
 4   apartment_index                               3987 non-null   float32
 5   kospi_index                                   3987 non-null   float32
 6   korea_rp                                      3987 non-null   float32
 7   korea_3_year                                  3987 non-null   float32
 8   korea_10_year                                 3987 non-null   float32
 9   us_3_month                                    3987 non-null   f

In [ ]:
df_economic

date  year  month  day  apartment_index  kospi_index  korea_rp  \
0     2012-02-01  2012      2    1        86.800003  1959.239990      3.25   
1     2012-02-02  2012      2    2        86.800003  1984.300049      3.25   
2     2012-02-03  2012      2    3        86.800003  1972.339966      3.25   
3     2012-02-04  2012      2    4        86.800003  1972.339966      3.25   
4     2012-02-05  2012      2    5        86.800003  1972.339966      3.25   
...          ...   ...    ...  ...              ...          ...       ...   
3982  2022-12-27  2022     12   27       104.400002  2332.790039      3.25   
3983  2022-12-28  2022     12   28       104.400002  2280.449951      3.25   
3984  2022-12-29  2022     12   29       104.400002  2236.399902      3.25   
3985  2022-12-30  2022     12   30       104.400002  2236.399902      3.25   
3986  2022-12-31  2022     12   31       104.400002  2236.399902      3.25   

      korea_3_year  korea_10_year  us_3_month  us_2_year  us_10_year  \
0            3.380          3.750       0.061     0.2260       1.830   
1            3.380          3.760       0.084     0.2260       1.823   
2            3.380          3.760       0.079     0.2380       1.924   
3            3.380          3.760       0.079     0.2380       1.924   
4            3.380          3.760       0.079     0.2380       1.924   
...            ...            ...         ...        ...         ...   
3982         3.661          3.612       4.311     4.3827       3.849   
3983         3.668          3.675       4.457     4.3574       3.886   
3984         3.718          3.723       4.423     4.3656       3.820   
3985         3.725          3.735       4.405     4.4279       3.879   
3986         3.725          3.735       4.405     4.4279       3.879   

      korea_10-3_year  us_10-2_year  us_10-3_year_month  \
0               0.370        1.6040               1.769   
1               0.380        1.5970               1.739   
2               0.380        1.6860               1.845   
3               0.380        1.6860               1.845   
4               0.380        1.6860               1.845   
...               ...           ...                 ...   
3982           -0.049       -0.5337              -0.462   
3983            0.007       -0.4714              -0.571   
3984            0.005       -0.5456              -0.603   
3985            0.010       -0.5489              -0.526   
3986            0.010       -0.5489              -0.526   

      last_month_total_apartment_supply  last_month_total_unsold_count  \
0                                  1822                           1890   
1                                  1822                           1890   
2                                  1822                           1890   
3                                  1822                           1890   
4                                  1822                           1890   
...                                 ...                            ...   
3982                               1759                            865   
3983                               1759                            865   
3984                               1759                            865   
3985                               1759                            865   
3986                               1759                            865   

      last_month_total_unsold_ratio  last_month_total_deal_count  \
0                        103.732162                         2786   
1                        103.732162                         2786   
2                        103.732162                         2786   
3                        103.732162                         2786   
4                        103.732162                         2786   
...                             ...                          ...   
3982                      49.175667                          750   
3983                      49.175667                          750   


In [ ]:
# null 값이나 inf 값들을 확인
import numpy as np
df_economic.replace([np.inf, -np.inf], np.nan, inplace=True)
var = df_economic.isnull().sum()
print(var.to_string())

date                                            0
year                                            0
month                                           0
day                                             0
apartment_index                                 0
kospi_index                                     0
korea_rp                                        0
korea_3_year                                    0
korea_10_year                                   0
us_3_month                                      0
us_2_year                                       0
us_10_year                                      0
korea_10-3_year                                 0
us_10-2_year                                    0
us_10-3_year_month                              0
last_month_total_apartment_supply               0
last_month_total_unsold_count                   0
last_month_total_unsold_ratio                   0
last_month_total_deal_count                     0
last_month_total_full_rent_count                0


In [ ]:
df_economic.to_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/final_economic.pkl')

>> 메모리 용량을 줄이기 위해서 타입들을 변환할 수도 있다.

>> 값들을 병합하거나 수정한 후, null 값이나 inf 값들이 존재하는 확인을 해야 한다 -> 나중에 진행이 된 다음에 발견을 하면 많은 부분을 수정해야 한다

# df_area_deal, df_area_full_rent, df_area_year_rent 파일들 생성

- '아파트 거래'가 체결된 날 이외의 날들은 가장 최근에 체결된 거래가격이 유지된다고 가정

## 필요한 데이터들 불러오기

In [ ]:
import pandas as pd
import numpy as np
# 데이터들 불러오기
df_deal = pd.read_csv("/content/drive/MyDrive/house_price/after_data/ver_4/apartment_deal.csv",  encoding='UTF8')
df_month_rent = pd.read_csv("/content/drive/MyDrive/house_price/after_data/ver_4/apartment_month_rent.csv",  encoding='UTF8')
df_full_rent = pd.read_csv("/content/drive/MyDrive/house_price/after_data/ver_4/apartment_full_rent.csv",  encoding='UTF8')

## df_area_deal 파일 생성

### 아파트 월별 매매 피봇 테이블 생성

In [ ]:
# 대표 데이터 파악
df_deal.head()

date  year  month  day address_0 address_1 address_2  address_3  \
0  2011-07-09  2011      7    9     서울특별시       강남구       개포동      655.0   
1  2011-07-28  2011      7   28     서울특별시       강남구       개포동      655.0   
2  2011-01-19  2011      1   19     서울특별시       강남구       개포동      658.0   
3  2011-09-02  2011      9    2     서울특별시       강남구       개포동      658.0   
4  2011-12-17  2011     12   17     서울특별시       강남구       개포동      658.0   

   address_4            name   area  deal_price  
0        2.0  개포2차현대아파트(220)  77.75       64000  
1        2.0  개포2차현대아파트(220)  77.75       65500  
2        1.0  개포6차우성아파트1동~8동  67.28       70500  
3        1.0  개포6차우성아파트1동~8동  79.97       85000  
4        1.0  개포6차우성아파트1동~8동  67.28       68000

In [ ]:
df_deal.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 882185 entries, 0 to 882184
Data columns (total 13 columns):
 #   Column           Non-Null Count   Dtype  
---  ------           --------------   -----  
 0   date             882185 non-null  object 
 1   year             882185 non-null  int64  
 2   month            882185 non-null  int64  
 3   day              882185 non-null  int64  
 4   address_0        882185 non-null  object 
 5   address_1        882185 non-null  object 
 6   address_2        882185 non-null  object 
 7   address_3        882185 non-null  float64
 8   address_4        882185 non-null  float64
 9   name             882185 non-null  object 
 10  area             882185 non-null  float64
 11  deal_price       882185 non-null  int64  
 12  area_deal_price  882185 non-null  float64
dtypes: float64(4), int64(4), object(5)
memory usage: 87.5+ MB


In [ ]:
# 면적당 가격 컬럼을 추가
df_deal['area_deal_price'] = df_deal['deal_price'] / df_deal['area']
df_deal.head()

date  year  month  day address_0 address_1 address_2  address_3  \
0  2011-07-09  2011      7    9     서울특별시       강남구       개포동      655.0   
1  2011-07-28  2011      7   28     서울특별시       강남구       개포동      655.0   
2  2011-01-19  2011      1   19     서울특별시       강남구       개포동      658.0   
3  2011-09-02  2011      9    2     서울특별시       강남구       개포동      658.0   
4  2011-12-17  2011     12   17     서울특별시       강남구       개포동      658.0   

   address_4            name   area  deal_price  area_deal_price  
0        2.0  개포2차현대아파트(220)  77.75       64000       823.151125  
1        2.0  개포2차현대아파트(220)  77.75       65500       842.443730  
2        1.0  개포6차우성아파트1동~8동  67.28       70500      1047.859691  
3        1.0  개포6차우성아파트1동~8동  79.97       85000      1062.898587  
4        1.0  개포6차우성아파트1동~8동  67.28       68000      1010.701546

In [ ]:
# 최근에 체결된 가격이 계속 유지된다고 생각을 하고 모든 날짜의 가격들을 결정
# 이를 위해서 그룹
import numpy as np
pivot_table_area_deal = df_deal.pivot_table(index=['year','month','day'], columns=['address_1','address_2','address_3','address_4'], values='area_deal_price')
pivot_table_area_deal


address_1               강남구                                                   \
address_2               개포동                                                    
address_3             12.0              138.0 140.0        141.0 166.0 172.0   
address_4              0.0  2.0          0.0   0.0          0.0   4.0   3.0    
year month day                                                                 
2011 1     1            NaN  NaN          NaN   NaN          NaN   NaN   NaN   
           2            NaN  NaN          NaN   NaN          NaN   NaN   NaN   
           3            NaN  NaN          NaN   NaN          NaN   NaN   NaN   
           4    1018.685955  NaN          NaN   NaN          NaN   NaN   NaN   
           5    1087.781432  NaN  2101.057579   NaN  1887.191539   NaN   NaN   
...                     ...  ...          ...   ...          ...   ...   ...   
2022 12    27           NaN  NaN          NaN   NaN          NaN   NaN   NaN   
           28           NaN  NaN          NaN   NaN          NaN   NaN   NaN   
           29           NaN  NaN          NaN   NaN          NaN   NaN   NaN   
           30           NaN  NaN          NaN   NaN          NaN   NaN   NaN   
           31           NaN  NaN          NaN   NaN          NaN   NaN   NaN   

address_1                         ...   중랑구                                \
address_2                         ...   중화동                                 
address_3      176.0 177.0 179.0  ... 307.0 314.0 318.0 331.0 413.0 438.0   
address_4       1.0   0.0   0.0   ...  76.0  1.0   81.0  64.0  8.0   0.0    
year month day                    ...                                       
2011 1     1     NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           2     NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           3     NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           4     NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           5     NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
...              ...   ...   ...  ...   ...   ...   ...   ...   ...   ...   
2022 12    27    NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           28    NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           29    NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           30    NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           31    NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   

address_1                                     
address_2                                     
address_3            450.0 452.0 453.0 454.0  
address_4             0.0   0.0   0.0   0.0   
year month day                                
2011 1     1           NaN   NaN   NaN   NaN  
           2    431.726908   NaN   NaN   NaN  
           3           NaN   NaN   NaN   NaN  
           4           NaN   NaN   NaN   NaN  
           5           NaN   NaN   NaN   NaN  
...                    ...   ...   ...   ...  
2022 12    27          NaN   NaN   NaN   NaN  
           28          NaN   NaN   NaN   NaN  
           29          NaN   NaN   NaN   NaN  
           30          NaN   NaN   NaN   NaN  
           31          NaN   NaN   NaN   NaN  

[4381 rows x 8860 columns]

In [ ]:
pivot_table_area_deal.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 4381 entries, (2011, 1, 1) to (2022, 12, 31)
Columns: 8860 entries, ('강남구', '개포동', 12.0, 0.0) to ('중랑구', '중화동', 454.0, 0.0)
dtypes: float64(8860)
memory usage: 296.2 MB


In [ ]:
from datetime import datetime, timedelta

start_date = datetime(2011, 1, 1)  # 시작 날짜
end_date = datetime(2022, 12, 31)  # 끝 날짜

date_list = []
current_date = start_date
while current_date <= end_date:
    date_tuple = (current_date.year, current_date.month, current_date.day)
    date_list.append(date_tuple)
    current_date += timedelta(days=1)

print(date_list)

[(2011, 1, 1), (2011, 1, 2), (2011, 1, 3), (2011, 1, 4), (2011, 1, 5), (2011, 1, 6), (2011, 1, 7), (2011, 1, 8), (2011, 1, 9), (2011, 1, 10), (2011, 1, 11), (2011, 1, 12), (2011, 1, 13), (2011, 1, 14), (2011, 1, 15), (2011, 1, 16), (2011, 1, 17), (2011, 1, 18), (2011, 1, 19), (2011, 1, 20), (2011, 1, 21), (2011, 1, 22), (2011, 1, 23), (2011, 1, 24), (2011, 1, 25), (2011, 1, 26), (2011, 1, 27), (2011, 1, 28), (2011, 1, 29), (2011, 1, 30), (2011, 1, 31), (2011, 2, 1), (2011, 2, 2), (2011, 2, 3), (2011, 2, 4), (2011, 2, 5), (2011, 2, 6), (2011, 2, 7), (2011, 2, 8), (2011, 2, 9), (2011, 2, 10), (2011, 2, 11), (2011, 2, 12), (2011, 2, 13), (2011, 2, 14), (2011, 2, 15), (2011, 2, 16), (2011, 2, 17), (2011, 2, 18), (2011, 2, 19), (2011, 2, 20), (2011, 2, 21), (2011, 2, 22), (2011, 2, 23), (2011, 2, 24), (2011, 2, 25), (2011, 2, 26), (2011, 2, 27), (2011, 2, 28), (2011, 3, 1), (2011, 3, 2), (2011, 3, 3), (2011, 3, 4), (2011, 3, 5), (2011, 3, 6), (2011, 3, 7), (2011, 3, 8), (2011, 3, 9), (2011,

In [ ]:
len(date_list)

4383

In [ ]:
pivot_table_area_deal.index

MultiIndex([(2011,  1,  1),
            (2011,  1,  2),
            (2011,  1,  3),
            (2011,  1,  4),
            (2011,  1,  5),
            (2011,  1,  6),
            (2011,  1,  7),
            (2011,  1,  8),
            (2011,  1,  9),
            (2011,  1, 10),
            ...
            (2022, 12, 22),
            (2022, 12, 23),
            (2022, 12, 24),
            (2022, 12, 25),
            (2022, 12, 26),
            (2022, 12, 27),
            (2022, 12, 28),
            (2022, 12, 29),
            (2022, 12, 30),
            (2022, 12, 31)],
           names=['year', 'month', 'day'], length=4381)

In [ ]:
# 기간 내 모든 날짜들에서 '거래날짜'들 빼서 '거래날짜'에서 없는 날짜들을 고름
print(set(date_list) - set(pivot_table_area_deal.index)) # '모든날짜'에 있고 '거래날짜'에 없는 날짜
print(set(pivot_table_area_deal.index) - set(date_list)) # 잘못 추가 생성된 날짜 

{(2016, 2, 9), (2022, 9, 11)}
set()


In [ ]:
# 빈 날짜 들(거래날짜에서 포함되지 않은 날짜의 거래가격들)을 null 로 채워서 row로 추가
pivot_table_area_deal.loc[(2016, 2, 9)]=np.nan
pivot_table_area_deal.loc[(2022, 9, 11)]=np.nan

In [ ]:
# 연, 월, 일 로 정렬을 함 - 정렬을 하지 않으면 바로 위에서 추가한 row들이 적절한 위치에 들어가 있지 않는다
pivot_table_area_deal = pivot_table_area_deal.sort_values(by=['year','month','day'])
pivot_table_area_deal

address_1               강남구                                                   \
address_2               개포동                                                    
address_3             12.0              138.0 140.0        141.0 166.0 172.0   
address_4              0.0  2.0          0.0   0.0          0.0   4.0   3.0    
year month day                                                                 
2011 1     1            NaN  NaN          NaN   NaN          NaN   NaN   NaN   
           2            NaN  NaN          NaN   NaN          NaN   NaN   NaN   
           3            NaN  NaN          NaN   NaN          NaN   NaN   NaN   
           4    1018.685955  NaN          NaN   NaN          NaN   NaN   NaN   
           5    1087.781432  NaN  2101.057579   NaN  1887.191539   NaN   NaN   
...                     ...  ...          ...   ...          ...   ...   ...   
2022 12    27           NaN  NaN          NaN   NaN          NaN   NaN   NaN   
           28           NaN  NaN          NaN   NaN          NaN   NaN   NaN   
           29           NaN  NaN          NaN   NaN          NaN   NaN   NaN   
           30           NaN  NaN          NaN   NaN          NaN   NaN   NaN   
           31           NaN  NaN          NaN   NaN          NaN   NaN   NaN   

address_1                         ...   중랑구                                \
address_2                         ...   중화동                                 
address_3      176.0 177.0 179.0  ... 307.0 314.0 318.0 331.0 413.0 438.0   
address_4       1.0   0.0   0.0   ...  76.0  1.0   81.0  64.0  8.0   0.0    
year month day                    ...                                       
2011 1     1     NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           2     NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           3     NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           4     NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           5     NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
...              ...   ...   ...  ...   ...   ...   ...   ...   ...   ...   
2022 12    27    NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           28    NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           29    NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           30    NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   
           31    NaN   NaN   NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   

address_1                                     
address_2                                     
address_3            450.0 452.0 453.0 454.0  
address_4             0.0   0.0   0.0   0.0   
year month day                                
2011 1     1           NaN   NaN   NaN   NaN  
           2    431.726908   NaN   NaN   NaN  
           3           NaN   NaN   NaN   NaN  
           4           NaN   NaN   NaN   NaN  
           5           NaN   NaN   NaN   NaN  
...                    ...   ...   ...   ...  
2022 12    27          NaN   NaN   NaN   NaN  
           28          NaN   NaN   NaN   NaN  
           29          NaN   NaN   NaN   NaN  
           30          NaN   NaN   NaN   NaN  
           31          NaN   NaN   NaN   NaN  

[4383 rows x 8860 columns]

In [ ]:
# 가장 최근에 체결된 값이 거래가격으로 유지 됨으로 ffill()을 사용
pivot_table_area_deal=pivot_table_area_deal.ffill()
pivot_table_area_deal

address_1               강남구                                         \
address_2               개포동                                          
address_3             12.0                      138.0        140.0   
address_4              0.0          2.0          0.0          0.0    
year month day                                                       
2011 1     1            NaN          NaN          NaN          NaN   
           2            NaN          NaN          NaN          NaN   
           3            NaN          NaN          NaN          NaN   
           4    1018.685955          NaN          NaN          NaN   
           5    1087.781432          NaN  2101.057579          NaN   
...                     ...          ...          ...          ...   
2022 12    27   2085.840353  1779.004227  2888.242098  2487.219819   
           28   2085.840353  1779.004227  2888.242098  2487.219819   
           29   2085.840353  1779.004227  2888.242098  2487.219819   
           30   2085.840353  1779.004227  2888.242098  2487.219819   
           31   2085.840353  1779.004227  2888.242098  2487.219819   

address_1                                                           \
address_2                                                            
address_3             141.0        166.0        172.0        176.0   
address_4              0.0          4.0          3.0          1.0    
year month day                                                       
2011 1     1            NaN          NaN          NaN          NaN   
           2            NaN          NaN          NaN          NaN   
           3            NaN          NaN          NaN          NaN   
           4            NaN          NaN          NaN          NaN   
           5    1887.191539          NaN          NaN          NaN   
...                     ...          ...          ...          ...   
2022 12    27   4324.324324  1413.594063  1342.758827  2172.968275   
           28   4324.324324  1413.594063  1342.758827  2172.968275   
           29   4324.324324  1413.594063  1342.758827  2172.968275   
           30   4324.324324  1413.594063  1342.758827  2172.968275   
           31   4324.324324  1413.594063  1342.758827  2172.968275   

address_1                                 ...         중랑구              \
address_2                                 ...         중화동               
address_3             177.0        179.0  ...       307.0       314.0   
address_4              0.0          0.0   ...        76.0        1.0    
year month day                            ...                           
2011 1     1            NaN          NaN  ...         NaN         NaN   
           2            NaN          NaN  ...         NaN         NaN   
           3            NaN          NaN  ...         NaN         NaN   
           4            NaN          NaN  ...         NaN         NaN   
           5            NaN          NaN  ...         NaN         NaN   
...                     ...          ...  ...         ...         ...   
2022 12    27   2380.225816  3014.696646  ...  457.073761  872.199239   
           28   2380.225816  3014.696646  ...  457.073761  872.199239   
           29   2380.225816  3014.696646  ...  457.073761  872.199239   
           30   2380.225816  3014.696646  ...  457.073761  872.199239   
           31   2380.225816  3014.696646  ...  457.073761  872.199239   

address_1                                                                   \
address_2                                                                    
address_3            318.0       331.0       413.0      438.0        450.0   
address_4             81.0        64.0        8.0        0.0          0.0    
year month day                                                               
2011 1     1           NaN         NaN         NaN        NaN          NaN   
           2           NaN         NaN         NaN        NaN   431.726908   
           3           NaN         NaN     

In [ ]:
# null 값을 채움 - 값을 채우지 않으면 추후 stack을 할 때 null 값을 계산을 안함
pivot_table_area_deal = pivot_table_area_deal.fillna(0)
pivot_table_area_deal

address_1               강남구                                         \
address_2               개포동                                          
address_3             12.0                      138.0        140.0   
address_4              0.0          2.0          0.0          0.0    
year month day                                                       
2011 1     1       0.000000     0.000000     0.000000     0.000000   
           2       0.000000     0.000000     0.000000     0.000000   
           3       0.000000     0.000000     0.000000     0.000000   
           4    1018.685955     0.000000     0.000000     0.000000   
           5    1087.781432     0.000000  2101.057579     0.000000   
...                     ...          ...          ...          ...   
2022 12    27   2085.840353  1779.004227  2888.242098  2487.219819   
           28   2085.840353  1779.004227  2888.242098  2487.219819   
           29   2085.840353  1779.004227  2888.242098  2487.219819   
           30   2085.840353  1779.004227  2888.242098  2487.219819   
           31   2085.840353  1779.004227  2888.242098  2487.219819   

address_1                                                           \
address_2                                                            
address_3             141.0        166.0        172.0        176.0   
address_4              0.0          4.0          3.0          1.0    
year month day                                                       
2011 1     1       0.000000     0.000000     0.000000     0.000000   
           2       0.000000     0.000000     0.000000     0.000000   
           3       0.000000     0.000000     0.000000     0.000000   
           4       0.000000     0.000000     0.000000     0.000000   
           5    1887.191539     0.000000     0.000000     0.000000   
...                     ...          ...          ...          ...   
2022 12    27   4324.324324  1413.594063  1342.758827  2172.968275   
           28   4324.324324  1413.594063  1342.758827  2172.968275   
           29   4324.324324  1413.594063  1342.758827  2172.968275   
           30   4324.324324  1413.594063  1342.758827  2172.968275   
           31   4324.324324  1413.594063  1342.758827  2172.968275   

address_1                                 ...         중랑구              \
address_2                                 ...         중화동               
address_3             177.0        179.0  ...       307.0       314.0   
address_4              0.0          0.0   ...        76.0        1.0    
year month day                            ...                           
2011 1     1       0.000000     0.000000  ...    0.000000    0.000000   
           2       0.000000     0.000000  ...    0.000000    0.000000   
           3       0.000000     0.000000  ...    0.000000    0.000000   
           4       0.000000     0.000000  ...    0.000000    0.000000   
           5       0.000000     0.000000  ...    0.000000    0.000000   
...                     ...          ...  ...         ...         ...   
2022 12    27   2380.225816  3014.696646  ...  457.073761  872.199239   
           28   2380.225816  3014.696646  ...  457.073761  872.199239   
           29   2380.225816  3014.696646  ...  457.073761  872.199239   
           30   2380.225816  3014.696646  ...  457.073761  872.199239   
           31   2380.225816  3014.696646  ...  457.073761  872.199239   

address_1                                                                   \
address_2                                                                    
address_3            318.0       331.0       413.0      438.0        450.0   
address_4             81.0        64.0        8.0        0.0          0.0    
year month day                                                               
2011 1     1      0.000000    0.000000    0.000000    0.00000     0.000000   
           2      0.000000    0.000000    0.000000    0.00000   431.726908   
           3      0.000000    0.000000    0

>> stack을 할 때 null 값을 계산을 안함으로, 계산 시 값 변경을 예방하기 위해서 null 값들을 채워야 한다

### 피봇테이블 -> 데이터프레임

In [ ]:
# 컬럼을 slice해서 값을 처리할 때, 컬럼의 개수가 많으면, row가 많을 때 보다 메모리를 많이 소모함으로 전치를 시킴킴
pivot_table_area_deal = pivot_table_area_deal.T
pivot_table_area_deal

year                                    2011                          \
month                                     1                            
day                                       1           2           3    
address_1 address_2 address_3 address_4                                
강남구       개포동       12.0      0.0        0.0    0.000000    0.000000   
                              2.0        0.0    0.000000    0.000000   
                    138.0     0.0        0.0    0.000000    0.000000   
                    140.0     0.0        0.0    0.000000    0.000000   
                    141.0     0.0        0.0    0.000000    0.000000   
...                                      ...         ...         ...   
중랑구       중화동       438.0     0.0        0.0    0.000000    0.000000   
                    450.0     0.0        0.0  431.726908  431.726908   
                    452.0     0.0        0.0    0.000000    0.000000   
                    453.0     0.0        0.0    0.000000    0.000000   
                    454.0     0.0        0.0    0.000000    0.000000   

year                                                               \
month                                                               
day                                               4            5    
address_1 address_2 address_3 address_4                             
강남구       개포동       12.0      0.0        1018.685955  1087.781432   
                              2.0           0.000000     0.000000   
                    138.0     0.0           0.000000  2101.057579   
                    140.0     0.0           0.000000     0.000000   
                    141.0     0.0           0.000000  1887.191539   
...                                              ...          ...   
중랑구       중화동       438.0     0.0           0.000000     0.000000   
                    450.0     0.0         431.726908   431.726908   
                    452.0     0.0           0.000000     0.000000   
                    453.0     0.0           0.000000     0.000000   
                    454.0     0.0           0.000000     0.000000   

year                                                               \
month                                                               
day                                               6            7    
address_1 address_2 address_3 address_4                             
강남구       개포동       12.0      0.0        1040.914561  1054.852321   
                              2.0           0.000000     0.000000   
                    138.0     0.0        2101.057579  2101.057579   
                    140.0     0.0           0.000000     0.000000   
                    141.0     0.0        1887.191539  1887.191539   
...                                              ...          ...   
중랑구       중화동       438.0     0.0           0.000000     0.000000   
                    450.0     0.0         485.274431   485.274431   
                    452.0     0.0           0.000000     0.000000   
                    453.0     0.0           0.000000     0.000000   
                    454.0     0.0           0.000000     0.000000   

year                                                               \
month                                                               
day                                               8            9    
address_1 address_2 address_3 address_4                             
강남구       개포동       12.0      0.0        1054.852321  1054.852321   
                              2.0           0.000000     0.000000   
                    138.0     0.0        2101.057579  2101.057579   
                    140.0     0.0           0.000000  1565.991903   
                    141.0     0.0        1887.191539  1887.191539   
...                                              ...          ...   
중랑구       중화동       438.0     0.0           0.000000     0.000000   
                    450.0     0.0         485.274431   485.274431   
                   

In [ ]:
# 피봇테이블을 일반데이터프레임화 
df_area_deal = pivot_table_area_deal.stack(level=[0,1,2])
df_area_deal =df_area_deal.reset_index()
df_area_deal

address_1 address_2  address_3  address_4  year  month  day  \
0              강남구       개포동       12.0        0.0  2011      1    1   
1              강남구       개포동       12.0        0.0  2011      1    2   
2              강남구       개포동       12.0        0.0  2011      1    3   
3              강남구       개포동       12.0        0.0  2011      1    4   
4              강남구       개포동       12.0        0.0  2011      1    5   
...            ...       ...        ...        ...   ...    ...  ...   
38833375       중랑구       중화동      454.0        0.0  2022     12   27   
38833376       중랑구       중화동      454.0        0.0  2022     12   28   
38833377       중랑구       중화동      454.0        0.0  2022     12   29   
38833378       중랑구       중화동      454.0        0.0  2022     12   30   
38833379       중랑구       중화동      454.0        0.0  2022     12   31   

                    0  
0            0.000000  
1            0.000000  
2            0.000000  
3         1018.685955  
4         1087.781432  
...               ...  
38833375  1131.141746  
38833376  1131.141746  
38833377  1131.141746  
38833378  1131.141746  
38833379  1131.141746  

[38833380 rows x 8 columns]

In [ ]:
df_area_deal.columns = ['address_1','address_2','address_3','address_4','year','month','day','area_deal'] # 컬럼명 수정 
df_area_deal = df_area_deal.astype({'address_3': 'int16', 'address_4': 'int16','year':'int16', 'month':'int16', 'day':'int16', 'area_deal':'float32'})
df_area_deal = df_area_deal.drop(df_area_deal[df_area_deal.area_deal == 0].index) # 위에서 값이 null인 값들을 0으로 처리했으므로, 0인 값들을 제거한다 
df_area_deal

address_1 address_2  address_3  address_4  year  month  day  \
3              강남구       개포동         12          0  2011      1    4   
4              강남구       개포동         12          0  2011      1    5   
5              강남구       개포동         12          0  2011      1    6   
6              강남구       개포동         12          0  2011      1    7   
7              강남구       개포동         12          0  2011      1    8   
...            ...       ...        ...        ...   ...    ...  ...   
38833375       중랑구       중화동        454          0  2022     12   27   
38833376       중랑구       중화동        454          0  2022     12   28   
38833377       중랑구       중화동        454          0  2022     12   29   
38833378       중랑구       중화동        454          0  2022     12   30   
38833379       중랑구       중화동        454          0  2022     12   31   

            area_deal  
3         1018.685974  
4         1087.781372  
5         1040.914551  
6         1054.852295  
7         1054.852295  
...               ...  
38833375  1131.141724  
38833376  1131.141724  
38833377  1131.141724  
38833378  1131.141724  
38833379  1131.141724  

[32844450 rows x 8 columns]

In [ ]:
df_area_deal.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 32844450 entries, 3 to 38833379
Data columns (total 8 columns):
 #   Column     Dtype  
---  ------     -----  
 0   address_1  object 
 1   address_2  object 
 2   address_3  int16  
 3   address_4  int16  
 4   year       int16  
 5   month      int16  
 6   day        int16  
 7   area_deal  float32
dtypes: float32(1), int16(5), object(2)
memory usage: 1.2+ GB


### 파일저장

In [ ]:
df_area_deal.to_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/df_area_deal.pkl')

## df_area_full_rent 파일 생성

- df_area_deal 파일생성 부분 참조

In [ ]:
df_full_rent.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1448686 entries, 0 to 1448685
Data columns (total 12 columns):
 #   Column           Non-Null Count    Dtype  
---  ------           --------------    -----  
 0   date             1448686 non-null  object 
 1   year             1448686 non-null  int64  
 2   month            1448686 non-null  int64  
 3   day              1448686 non-null  int64  
 4   address_0        1448686 non-null  object 
 5   address_1        1448686 non-null  object 
 6   address_2        1448686 non-null  object 
 7   address_3        1448686 non-null  float64
 8   address_4        1448686 non-null  float64
 9   name             1448686 non-null  object 
 10  area             1448686 non-null  float64
 11  full_rent_price  1448686 non-null  int64  
dtypes: float64(3), int64(4), object(5)
memory usage: 132.6+ MB


In [ ]:
import numpy as np
# 면적당 가격을 추가
df_full_rent['area_full_rent_price'] = df_full_rent['full_rent_price'] / df_full_rent['area']
pivot_table_area_full_rent = df_full_rent.pivot_table(index=['year','month','day'], columns=['address_1','address_2','address_3','address_4'], values='area_full_rent_price')
pivot_table_area_full_rent

address_1              강남구                                                   \
address_2              개포동                                                    
address_3            12.0                     138.0       140.0       141.0   
address_4             0.0         2.0          0.0         0.0         0.0    
year month day                                                                
2011 1     1           NaN         NaN          NaN         NaN         NaN   
           2           NaN         NaN          NaN         NaN         NaN   
           3    430.053124  469.099032          NaN         NaN  190.044764   
           4    416.009890         NaN          NaN  259.109312  159.620342   
           5           NaN         NaN   217.090981  267.487606  212.476466   
...                    ...         ...          ...         ...         ...   
2022 12    27          NaN         NaN  1518.178671         NaN         NaN   
           28   834.176956         NaN          NaN         NaN         NaN   
           29          NaN         NaN          NaN         NaN         NaN   
           30          NaN         NaN          NaN         NaN         NaN   
           31   743.348983         NaN          NaN         NaN         NaN   

address_1                                          ...   중랑구        \
address_2                                          ...   중화동         
address_3      166.0 172.0 176.0 177.0      179.0  ... 307.0 314.0   
address_4       4.0   3.0   1.0   0.0        0.0   ...  76.0  1.0    
year month day                                     ...               
2011 1     1     NaN   NaN   NaN   NaN        NaN  ...   NaN   NaN   
           2     NaN   NaN   NaN   NaN        NaN  ...   NaN   NaN   
           3     NaN   NaN   NaN   NaN        NaN  ...   NaN   NaN   
           4     NaN   NaN   NaN   NaN        NaN  ...   NaN   NaN   
           5     NaN   NaN   NaN   NaN        NaN  ...   NaN   NaN   
...              ...   ...   ...   ...        ...  ...   ...   ...   
2022 12    27    NaN   NaN   NaN   NaN        NaN  ...   NaN   NaN   
           28    NaN   NaN   NaN   NaN        NaN  ...   NaN   NaN   
           29    NaN   NaN   NaN   NaN  854.16405  ...   NaN   NaN   
           30    NaN   NaN   NaN   NaN        NaN  ...   NaN   NaN   
           31    NaN   NaN   NaN   NaN        NaN  ...   NaN   NaN   

address_1                                                                   
address_2                                                                   
address_3            318.0 331.0 413.0 438.0       450.0 452.0 453.0 454.0  
address_4             81.0  64.0  8.0   0.0         0.0   0.0   0.0   0.0   
year month day                                                              
2011 1     1           NaN   NaN   NaN   NaN         NaN   NaN   NaN   NaN  
           2           NaN   NaN   NaN   NaN         NaN   NaN   NaN   NaN  
           3           NaN   NaN   NaN   NaN         NaN   NaN   NaN   NaN  
           4    203.665988   NaN   NaN   NaN  251.004016   NaN   NaN   NaN  
           5           NaN   NaN   NaN   NaN  190.408188   NaN   NaN   NaN  
...                    ...   ...   ...   ...         ...   ...   ...   ...  
2022 12    27          NaN   NaN   NaN   NaN         NaN   NaN   NaN   NaN  
           28          NaN   NaN   NaN   NaN         NaN   NaN   NaN   NaN  
           29          NaN   NaN   NaN   NaN         NaN   NaN   NaN   NaN  
           30          NaN   NaN   NaN   NaN         NaN   NaN   NaN   NaN  
           31          NaN   NaN   NaN   NaN         NaN   NaN   NaN   NaN  

[4383 rows x 9258 columns]

In [ ]:
from datetime import datetime, timedelta

start_date = datetime(2011, 1, 1)  # 시작 날짜
end_date = datetime(2022, 12, 31)  # 끝 날짜

date_list = []
current_date = start_date
while current_date <= end_date:
    date_tuple = (current_date.year, current_date.month, current_date.day)
    date_list.append(date_tuple)
    current_date += timedelta(days=1)

# 기간 내 모든 날짜들에서 '거래날짜'들 빼서 '거래날짜'에서 없는 날짜들을 고름
print(set(date_list) - set(pivot_table_area_full_rent.index)) # '모든날짜'에 있고 '거래날짜'에 없는 날짜
print(set(pivot_table_area_full_rent.index) - set(date_list)) # 잘못 추가 생성된 날짜 

set()
set()


In [ ]:
pivot_table_area_full_rent = pivot_table_area_full_rent.ffill()
pivot_table_area_full_rent = pivot_table_area_full_rent.fillna(0)
pivot_table_area_full_rent = pivot_table_area_full_rent.T
df_area_full_rent = pivot_table_area_full_rent.stack(level=[0,1,2])
df_area_full_rent =df_area_full_rent.reset_index()
df_area_full_rent.columns = ['address_1','address_2','address_3','address_4','year','month','day','area_full_rent'] # 컬럼명 수정 
df_area_full_rent = df_area_full_rent.drop(df_area_full_rent[df_area_full_rent.area_full_rent == 0].index) # 위에서 값이 null인 값들을 0으로 처리했으므로, 0인 값들을 제거한다 
df_area_full_rent = df_area_full_rent.astype({'address_3': 'int16', 'address_4': 'int16','year':'int16', 'month':'int16', 'day':'int16', 'area_full_rent':'float32'})
df_area_full_rent

address_1 address_2  address_3  address_4  year  month  day  \
2              강남구       개포동         12          0  2011      1    3   
3              강남구       개포동         12          0  2011      1    4   
4              강남구       개포동         12          0  2011      1    5   
5              강남구       개포동         12          0  2011      1    6   
6              강남구       개포동         12          0  2011      1    7   
...            ...       ...        ...        ...   ...    ...  ...   
40577809       중랑구       중화동        454          0  2022     12   27   
40577810       중랑구       중화동        454          0  2022     12   28   
40577811       중랑구       중화동        454          0  2022     12   29   
40577812       중랑구       중화동        454          0  2022     12   30   
40577813       중랑구       중화동        454          0  2022     12   31   

          area_full_rent  
2             430.053131  
3             416.009888  
4             416.009888  
5             416.009888  
6             400.000000  
...                  ...  
40577809      472.645630  
40577810      472.645630  
40577811      472.645630  
40577812      472.645630  
40577813      472.645630  

[34514890 rows x 8 columns]

In [ ]:
df_area_full_rent.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 34514890 entries, 2 to 40577813
Data columns (total 8 columns):
 #   Column          Dtype  
---  ------          -----  
 0   address_1       object 
 1   address_2       object 
 2   address_3       int16  
 3   address_4       int16  
 4   year            int16  
 5   month           int16  
 6   day             int16  
 7   area_full_rent  float32
dtypes: float32(1), int16(5), object(2)
memory usage: 1.2+ GB


In [ ]:
df_area_full_rent.to_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/df_area_full_rent.pkl')

## df_area_year_rent 파일 생성

- df_area_deal 파일 생성 참조
- 아파트월세 피봇테이블 -> 아파트 월별 연세 피봇테이블
- 보증금은 계약시의 상황마다 다를 것
- 전월세전환률을 적용하여서 월세에서의 보증금을 변환
- 거래들마다 상황에 따라 보증금과 월세금액은 다를 수 있음으로, 보증금의 5.8% 값에 월세*12을 더하여 1년간 들어가는 금액인 연세를 계산

In [ ]:
df_month_rent.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 637088 entries, 0 to 637087
Data columns (total 13 columns):
 #   Column            Non-Null Count   Dtype  
---  ------            --------------   -----  
 0   date              637088 non-null  object 
 1   year              637088 non-null  int64  
 2   month             637088 non-null  int64  
 3   day               637088 non-null  int64  
 4   address_0         637088 non-null  object 
 5   address_1         637088 non-null  object 
 6   address_2         637088 non-null  object 
 7   address_3         637088 non-null  float64
 8   address_4         637088 non-null  float64
 9   name              637088 non-null  object 
 10  area              637088 non-null  float64
 11  rent_deposit      637088 non-null  int64  
 12  month_rent_price  637088 non-null  int64  
dtypes: float64(3), int64(5), object(5)
memory usage: 63.2+ MB


In [ ]:
# 보증금의 5.8% 값에 월세*12을 더하여 1년간 들어가는 금액인 연세를 계산
df_month_rent['year_rent_price'] = (df_month_rent['rent_deposit']*0.058)+(df_month_rent['month_rent_price']*12)
df_month_rent['area_year_rent_price'] = df_month_rent['year_rent_price'] / df_month_rent['area']
pivot_table_area_year_rent = df_month_rent.pivot_table(index=['year','month','day'], columns=['address_1','address_2','address_3','address_4'], values='area_year_rent_price')
pivot_table_area_year_rent

address_1             강남구                                                      \
address_2             개포동                                                       
address_3           12.0            138.0 140.0 141.0 172.0 176.0 177.0 179.0   
address_4            0.0  2.0        0.0   0.0   0.0   3.0   1.0   0.0   0.0    
year month day                                                                  
2011 1     1          NaN  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           2          NaN  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           3          NaN  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           4          NaN  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           5          NaN  NaN  18.284371   NaN   NaN   NaN   NaN   NaN   NaN   
...                   ...  ...        ...   ...   ...   ...   ...   ...   ...   
2022 12    27         NaN  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           28   44.925792  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           29   39.566973  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           30   46.355226  NaN  66.807854   NaN   NaN   NaN   NaN   NaN   NaN   
           31         NaN  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   

address_1                  ...   중랑구                                          \
address_2                  ...   중화동                                           
address_3           185.0  ... 307.0      314.0 318.0 331.0 438.0      450.0   
address_4            0.0   ...  6.0  76.0  1.0   81.0  64.0  0.0        0.0    
year month day             ...                                                 
2011 1     1          NaN  ...   NaN  NaN   NaN   NaN   NaN   NaN        NaN   
           2          NaN  ...   NaN  NaN   NaN   NaN   NaN   NaN        NaN   
           3          NaN  ...   NaN  NaN   NaN   NaN   NaN   NaN        NaN   
           4    29.702312  ...   NaN  NaN   NaN   NaN   NaN   NaN        NaN   
           5          NaN  ...   NaN  NaN   NaN   NaN   NaN   NaN        NaN   
...                   ...  ...   ...  ...   ...   ...   ...   ...        ...   
2022 12    27         NaN  ...   NaN  NaN   NaN   NaN   NaN   NaN        NaN   
           28   28.144544  ...   NaN  NaN   NaN   NaN   NaN   NaN  24.872069   
           29         NaN  ...   NaN  NaN   NaN   NaN   NaN   NaN        NaN   
           30   39.502450  ...   NaN  NaN   NaN   NaN   NaN   NaN        NaN   
           31         NaN  ...   NaN  NaN   NaN   NaN   NaN   NaN        NaN   

address_1                         
address_2                         
address_3      452.0 453.0 454.0  
address_4       0.0   0.0   0.0   
year month day                    
2011 1     1     NaN   NaN   NaN  
           2     NaN   NaN   NaN  
           3     NaN   NaN   NaN  
           4     NaN   NaN   NaN  
           5     NaN   NaN   NaN  
...              ...   ...   ...  
2022 12    27    NaN   NaN   NaN  
           28    NaN   NaN   NaN  
           29    NaN   NaN   NaN  
           30    NaN   NaN   NaN  
           31    NaN   NaN   NaN  

[4383 rows x 8358 columns]

In [ ]:
from datetime import datetime, timedelta

start_date = datetime(2011, 1, 1)  # 시작 날짜
end_date = datetime(2022, 12, 31)  # 끝 날짜

date_list = []
current_date = start_date
while current_date <= end_date:
    date_tuple = (current_date.year, current_date.month, current_date.day)
    date_list.append(date_tuple)
    current_date += timedelta(days=1)

# 기간 내 모든 날짜들에서 '거래날짜'들 빼서 '거래날짜'에서 없는 날짜들을 고름
print(set(date_list) - set(pivot_table_area_year_rent.index)) # '모든날짜'에 있고 '거래날짜'에 없는 날짜
print(set(pivot_table_area_year_rent.index) - set(date_list)) # 잘못 추가 생성된 날짜

set()
set()


In [ ]:
pivot_table_area_year_rent=pivot_table_area_year_rent.ffill()
pivot_table_area_year_rent = pivot_table_area_year_rent.fillna(0)

# 피봇테이블을 일반데이터프레임화 
pivot_table_area_year_rent = pivot_table_area_year_rent.T
df_area_year_rent = pivot_table_area_year_rent.stack(level=[0,1,2])
df_area_year_rent = df_area_year_rent.reset_index()
df_area_year_rent.columns = ['address_1','address_2','address_3','address_4','year','month','day','area_year_rent'] # 컬럼명 수정 
df_area_year_rent = df_area_year_rent.drop(df_area_year_rent[df_area_year_rent.area_year_rent == 0].index) # 위에서 값이 null인 값들을 0으로 처리했으므로, 0인 값들을 제거한다
df_area_year_rent = df_area_year_rent.astype({'address_3': 'int16', 'address_4': 'int16','year':'int16', 'month':'int16', 'day':'int16', 'area_year_rent':'float32'}) 
df_area_year_rent

address_1 address_2  address_3  address_4  year  month  day  \
6              강남구       개포동         12          0  2011      1    7   
7              강남구       개포동         12          0  2011      1    8   
8              강남구       개포동         12          0  2011      1    9   
9              강남구       개포동         12          0  2011      1   10   
10             강남구       개포동         12          0  2011      1   11   
...            ...       ...        ...        ...   ...    ...  ...   
36633109       중랑구       중화동        454          0  2022     12   27   
36633110       중랑구       중화동        454          0  2022     12   28   
36633111       중랑구       중화동        454          0  2022     12   29   
36633112       중랑구       중화동        454          0  2022     12   30   
36633113       중랑구       중화동        454          0  2022     12   31   

          area_year_rent  
6              30.255503  
7              30.255503  
8              30.255503  
9              30.255503  
10             30.255503  
...                  ...  
36633109       22.199171  
36633110       22.199171  
36633111       22.199171  
36633112       22.199171  
36633113       22.199171  

[27244049 rows x 8 columns]

In [ ]:
df_area_year_rent.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 27244049 entries, 6 to 36633113
Data columns (total 8 columns):
 #   Column          Dtype  
---  ------          -----  
 0   address_1       object 
 1   address_2       object 
 2   address_3       int16  
 3   address_4       int16  
 4   year            int16  
 5   month           int16  
 6   day             int16  
 7   area_year_rent  float32
dtypes: float32(1), int16(5), object(2)
memory usage: 987.3+ MB


In [ ]:
df_area_year_rent.to_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/df_area_year_rent.pkl')

- deal_everyday 폴더에 있는 파일들은 apartment_deal 파일에 모든 날짜의 아파트매매가 현황 정보를 추가한 파일 
- full_rent_everyday 폴더에 있는 파일들은 apartment_full_rent 파일에 모든 날짜의 아파트전세가 현황 정보를 추가한 파일 
- year_rent_everyday 폴더에 있는 파일들은 apartment_month_rent 파일에 모든 날짜의 아파트월세가 현황 정보를 추가한 파일 

- 이전에 만들었던 apartment_deal, apartment_full_rent,apartment_month_rent 데이터프레임들은 거래가 체결된 날짜에 대한 정보만 데이터로 가지고 있다. 
- 거래가 체결된 날짜 외에 주어진 기간에 해당하는 모든 날짜들에 대한 매매, 전세, 연세 관련 정보들을 구하기 위해서 데이터프레임 생성
- 추후 데이터처리를 위해 위에서 생성한 피봇테이블들을 컬럼을 address_1, address_2, address_3, address_4, year, month, day, 거래가격(매매가격,전세가격,연세가격) 으로 재구조화 해야 함
- 하지만 피봇테이블들은 컬럼의 갯수가 너무 많기에 재구조화 하는 과정에서 메모리 부족 오류가 발생
- 메모리 부족 사태를 해결하기 위해서 다양한 방법 시도
- column의 개수가 너무 많을 경우, 테이블의 전치 기능을 활용하면 큰 도움이 됨

# df_area_micro 생성

## df_area_all 생성

### 3개의 파일 병합

- 가치평가 컬럼들을 구하기 위해서 merge를 통해, 매매가, 전세가, 연세가가 다 있는 정보들 만을 거름

In [ ]:
import pandas as pd

df_area_deal = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/df_area_deal.pkl')
df_area_full_rent = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/df_area_full_rent.pkl')

In [ ]:
df_area_deal_full_rent = pd.merge(df_area_deal,df_area_full_rent, on=['address_1', 'address_2', 'address_3', 'address_4', 'year', 'month','day'])

In [ ]:
df_area_deal_full_rent.to_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/df_area_deal_full_rent.pkl')

- 메모리 부족 이슈로 나누어서 실행

In [ ]:
import pandas as pd

df_area_deal_full_rent = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/df_area_deal_full_rent.pkl')
df_area_year_rent = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/df_area_year_rent.pkl')

In [ ]:
df_area_all = pd.merge(df_area_deal_full_rent, df_area_year_rent , on=['address_1', 'address_2', 'address_3', 'address_4', 'year', 'month','day'])

In [ ]:
df_area_all.to_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/df_area_all.pkl')

## 일별로 종합 수치들을 확인

- 추후 지역별을 추가하여서 그룹화 가능?

In [3]:
import pandas as pd

df_area_all = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/df_area_all.pkl')
df_area_all.head()

address_1 address_2  address_3  address_4  year  month  day    area_deal  \
0       강남구       개포동         12          0  2011      1    7  1054.852295   
1       강남구       개포동         12          0  2011      1    8  1054.852295   
2       강남구       개포동         12          0  2011      1    9  1054.852295   
3       강남구       개포동         12          0  2011      1   10  1054.852295   
4       강남구       개포동         12          0  2011      1   11  1006.830261   

   area_full_rent  area_year_rent  
0      400.000000       30.255503  
1      400.000000       30.255503  
2      400.000000       30.255503  
3      420.425629       30.255503  
4      434.408142       30.255503

In [4]:
df_area_all.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 24144106 entries, 0 to 24144105
Data columns (total 10 columns):
 #   Column          Dtype  
---  ------          -----  
 0   address_1       object 
 1   address_2       object 
 2   address_3       int16  
 3   address_4       int16  
 4   year            int16  
 5   month           int16  
 6   day             int16  
 7   area_deal       float32
 8   area_full_rent  float32
 9   area_year_rent  float32
dtypes: float32(3), int16(5), object(2)
memory usage: 1.0+ GB


In [5]:
df_area_micro=df_area_all.groupby(["year","month","day"])[["area_deal","area_full_rent","area_year_rent"]].mean()
df_area_micro

area_deal  area_full_rent  area_year_rent
year month day                                             
2011 1     2     595.000000      259.771637       18.880535
           3     519.548096      274.167999       16.547453
           4     704.231018      326.309021       21.519497
           5     768.772095      326.750854       21.022175
           6     709.595642      303.017273       19.990875
...                     ...             ...             ...
2022 12    27   1058.162842      602.649963       30.011925
           28   1057.969971      602.549805       29.991238
           29   1057.233032      602.409302       30.016970
           30   1056.862427      602.243958       30.012321
           31   1056.697632      601.962585       30.021296

[4382 rows x 3 columns]

In [6]:
df_area_micro.reset_index(inplace=True)
df_area_micro

year  month  day    area_deal  area_full_rent  area_year_rent
0     2011      1    2   595.000000      259.771637       18.880535
1     2011      1    3   519.548096      274.167999       16.547453
2     2011      1    4   704.231018      326.309021       21.519497
3     2011      1    5   768.772095      326.750854       21.022175
4     2011      1    6   709.595642      303.017273       19.990875
...    ...    ...  ...          ...             ...             ...
4377  2022     12   27  1058.162842      602.649963       30.011925
4378  2022     12   28  1057.969971      602.549805       29.991238
4379  2022     12   29  1057.233032      602.409302       30.016970
4380  2022     12   30  1056.862427      602.243958       30.012321
4381  2022     12   31  1056.697632      601.962585       30.021296

[4382 rows x 6 columns]

In [7]:
df_area_micro = df_area_micro.drop([0,1])
df_area_micro

year  month  day    area_deal  area_full_rent  area_year_rent
2     2011      1    4   704.231018      326.309021       21.519497
3     2011      1    5   768.772095      326.750854       21.022175
4     2011      1    6   709.595642      303.017273       19.990875
5     2011      1    7   727.185974      301.825531       20.578035
6     2011      1    8   713.546570      302.605042       20.582342
...    ...    ...  ...          ...             ...             ...
4377  2022     12   27  1058.162842      602.649963       30.011925
4378  2022     12   28  1057.969971      602.549805       29.991238
4379  2022     12   29  1057.233032      602.409302       30.016970
4380  2022     12   30  1056.862427      602.243958       30.012321
4381  2022     12   31  1056.697632      601.962585       30.021296

[4380 rows x 6 columns]

### 가치평가 지표 컬럼 추가

In [8]:
df_area_micro['deal_full_rent_rate'] = 100*(df_area_micro['area_full_rent'] / df_area_micro['area_deal'])
df_area_micro['deal_year_rent_multiple'] = df_area_micro['area_deal']/ df_area_micro['area_year_rent']
df_area_micro

year  month  day    area_deal  area_full_rent  area_year_rent  \
2     2011      1    4   704.231018      326.309021       21.519497   
3     2011      1    5   768.772095      326.750854       21.022175   
4     2011      1    6   709.595642      303.017273       19.990875   
5     2011      1    7   727.185974      301.825531       20.578035   
6     2011      1    8   713.546570      302.605042       20.582342   
...    ...    ...  ...          ...             ...             ...   
4377  2022     12   27  1058.162842      602.649963       30.011925   
4378  2022     12   28  1057.969971      602.549805       29.991238   
4379  2022     12   29  1057.233032      602.409302       30.016970   
4380  2022     12   30  1056.862427      602.243958       30.012321   
4381  2022     12   31  1056.697632      601.962585       30.021296   

      deal_full_rent_rate  deal_year_rent_multiple  
2               46.335510                32.725254  
3               42.502956                36.569580  
4               42.702808                35.495975  
5               41.505962                35.337971  
6               42.408592                34.667900  
...                   ...                      ...  
4377            56.952477                35.258080  
4378            56.953396                35.275970  
4379            56.979805                35.221176  
4380            56.984138                35.214283  
4381            56.966400                35.198269  

[4380 rows x 8 columns]

- 과거 데이터들을은 월별로 그룹화 해서 비교 하자 ㄱㄱ
- 만든 후에 이상치 처리


## 월별 평균 종합 수치들을 확인

In [9]:
df_area_micro_month = df_area_micro.groupby(["year","month"])[["area_deal","area_full_rent","area_year_rent"]].mean().copy()
df_area_micro_month.reset_index(inplace=True)
df_area_micro_month

year  month    area_deal  area_full_rent  area_year_rent
0    2011      1   681.403809      307.047913       20.981915
1    2011      2   641.325623      300.576172       20.937654
2    2011      3   615.491150      297.227692       20.475676
3    2011      4   600.585022      295.111023       20.246986
4    2011      5   589.073303      295.179962       20.066994
..    ...    ...          ...             ...             ...
139  2022      8  1083.606689      618.873352       29.926113
140  2022      9  1079.784546      619.757629       30.158903
141  2022     10  1075.312866      618.263733       30.377937
142  2022     11  1068.705444      612.513855       30.278233
143  2022     12  1060.324219      605.178101       30.066116

[144 rows x 5 columns]

In [10]:
df_area_micro_month['area_deal'] = df_area_micro_month['area_deal'].shift(1)
df_area_micro_month['area_full_rent'] = df_area_micro_month['area_full_rent'].shift(1)
df_area_micro_month['area_year_rent'] = df_area_micro_month['area_year_rent'].shift(1)
df_area_micro_month = df_area_micro_month.dropna()
df_area_micro_month.columns = ['year','month','last_month_area_deal','last_month_area_full_count', 'last_month_area_year_rent']
df_area_micro_month

year  month  last_month_area_deal  last_month_area_full_count  \
1    2011      2            681.403809                  307.047913   
2    2011      3            641.325623                  300.576172   
3    2011      4            615.491150                  297.227692   
4    2011      5            600.585022                  295.111023   
5    2011      6            589.073303                  295.179962   
..    ...    ...                   ...                         ...   
139  2022      8           1086.855713                  617.645264   
140  2022      9           1083.606689                  618.873352   
141  2022     10           1079.784546                  619.757629   
142  2022     11           1075.312866                  618.263733   
143  2022     12           1068.705444                  612.513855   

     last_month_area_year_rent  
1                    20.981915  
2                    20.937654  
3                    20.475676  
4                    20.246986  
5                    20.066994  
..                         ...  
139                  29.700731  
140                  29.926113  
141                  30.158903  
142                  30.377937  
143                  30.278233  

[143 rows x 5 columns]

## 6개월전 종합 수치 병합

In [11]:
# df_area_micro_month의 6개월 후, 달을 컬럼으로 구한후, df_area_micro의 year, month와 merge 하면 6개월 전 수치들을 구할 수 있음 
df_area_micro_month_6m = df_area_micro_month.copy()
df_area_micro_month_6m.loc[df_area_micro_month_6m['month']<7, '6m_after_year'] = df_area_micro_month_6m['year'] 
df_area_micro_month_6m.loc[df_area_micro_month_6m['month']<7, '6m_after_month'] = df_area_micro_month_6m['month'] + 6
df_area_micro_month_6m.loc[df_area_micro_month_6m['month']>=7, '6m_after_year'] = df_area_micro_month_6m['year'] + 1
df_area_micro_month_6m.loc[df_area_micro_month_6m['month']>=7, '6m_after_month'] = df_area_micro_month_6m['month'] - 6

df_area_micro_month_6m



year  month  last_month_area_deal  last_month_area_full_count  \
1    2011      2            681.403809                  307.047913   
2    2011      3            641.325623                  300.576172   
3    2011      4            615.491150                  297.227692   
4    2011      5            600.585022                  295.111023   
5    2011      6            589.073303                  295.179962   
..    ...    ...                   ...                         ...   
139  2022      8           1086.855713                  617.645264   
140  2022      9           1083.606689                  618.873352   
141  2022     10           1079.784546                  619.757629   
142  2022     11           1075.312866                  618.263733   
143  2022     12           1068.705444                  612.513855   

     last_month_area_year_rent  6m_after_year  6m_after_month  
1                    20.981915         2011.0             8.0  
2                    20.937654         2011.0             9.0  
3                    20.475676         2011.0            10.0  
4                    20.246986         2011.0            11.0  
5                    20.066994         2011.0            12.0  
..                         ...            ...             ...  
139                  29.700731         2023.0             2.0  
140                  29.926113         2023.0             3.0  
141                  30.158903         2023.0             4.0  
142                  30.377937         2023.0             5.0  
143                  30.278233         2023.0             6.0  

[143 rows x 7 columns]

In [12]:
df_area_micro_month_6m = df_area_micro_month_6m.drop(['year','month'],axis=1)
df_area_micro_month_6m = df_area_micro_month_6m.astype({'6m_after_year':'int16', '6m_after_month' : 'int16'})
df_area_micro_month_6m.rename(columns = {'last_month_area_deal' : '6m_before_area_deal_mean', 'last_month_area_full_count' : '6m_before_area_full_rent_mean', 
                                      'last_month_area_year_rent' : '6m_before_area_year_rent_mean'}, inplace = True)
df_area_micro_month_6m

6m_before_area_deal_mean  6m_before_area_full_rent_mean  \
1                  681.403809                     307.047913   
2                  641.325623                     300.576172   
3                  615.491150                     297.227692   
4                  600.585022                     295.111023   
5                  589.073303                     295.179962   
..                        ...                            ...   
139               1086.855713                     617.645264   
140               1083.606689                     618.873352   
141               1079.784546                     619.757629   
142               1075.312866                     618.263733   
143               1068.705444                     612.513855   

     6m_before_area_year_rent_mean  6m_after_year  6m_after_month  
1                        20.981915           2011               8  
2                        20.937654           2011               9  
3                        20.475676           2011              10  
4                        20.246986           2011              11  
5                        20.066994           2011              12  
..                             ...            ...             ...  
139                      29.700731           2023               2  
140                      29.926113           2023               3  
141                      30.158903           2023               4  
142                      30.377937           2023               5  
143                      30.278233           2023               6  

[143 rows x 5 columns]

In [13]:
df_area_micro_month_6m['6m_before_deal_full_rent_rate'] = 100*(df_area_micro_month_6m['6m_before_area_full_rent_mean'] / df_area_micro_month_6m['6m_before_area_deal_mean'])
df_area_micro_month_6m['6m_before_deal_year_rent_multiple'] = df_area_micro_month_6m['6m_before_area_deal_mean']/ df_area_micro_month_6m['6m_before_area_year_rent_mean']
df_area_micro_month_6m

6m_before_area_deal_mean  6m_before_area_full_rent_mean  \
1                  681.403809                     307.047913   
2                  641.325623                     300.576172   
3                  615.491150                     297.227692   
4                  600.585022                     295.111023   
5                  589.073303                     295.179962   
..                        ...                            ...   
139               1086.855713                     617.645264   
140               1083.606689                     618.873352   
141               1079.784546                     619.757629   
142               1075.312866                     618.263733   
143               1068.705444                     612.513855   

     6m_before_area_year_rent_mean  6m_after_year  6m_after_month  \
1                        20.981915           2011               8   
2                        20.937654           2011               9   
3                        20.475676           2011              10   
4                        20.246986           2011              11   
5                        20.066994           2011              12   
..                             ...            ...             ...   
139                      29.700731           2023               2   
140                      29.926113           2023               3   
141                      30.158903           2023               4   
142                      30.377937           2023               5   
143                      30.278233           2023               6   

     6m_before_deal_full_rent_rate  6m_before_deal_year_rent_multiple  
1                        45.061077                          32.475769  
2                        46.867950                          30.630251  
3                        48.291142                          30.059626  
4                        49.137260                          29.662933  
5                        50.109207                          29.355333  
..                             ...                                ...  
139                      56.828636                          36.593567  
140                      57.112358                          36.209404  
141                      57.396420                          35.803177  
142                      57.496174                          35.397823  
143                      57.313625                          35.296162  

[143 rows x 7 columns]

In [14]:
df_area_micro = pd.merge(df_area_micro,df_area_micro_month_6m, left_on=['year','month'], right_on=['6m_after_year','6m_after_month'],how = 'left') # inner로 하면, 12개월 파트를 병합할 때 사라지는 데이터가 더 많아짐 ㅠㅠㅠ
df_area_micro

year  month  day    area_deal  area_full_rent  area_year_rent  \
0     2011      1    4   704.231018      326.309021       21.519497   
1     2011      1    5   768.772095      326.750854       21.022175   
2     2011      1    6   709.595642      303.017273       19.990875   
3     2011      1    7   727.185974      301.825531       20.578035   
4     2011      1    8   713.546570      302.605042       20.582342   
...    ...    ...  ...          ...             ...             ...   
4375  2022     12   27  1058.162842      602.649963       30.011925   
4376  2022     12   28  1057.969971      602.549805       29.991238   
4377  2022     12   29  1057.233032      602.409302       30.016970   
4378  2022     12   30  1056.862427      602.243958       30.012321   
4379  2022     12   31  1056.697632      601.962585       30.021296   

      deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
0               46.335510                32.725254                       NaN   
1               42.502956                36.569580                       NaN   
2               42.702808                35.495975                       NaN   
3               41.505962                35.337971                       NaN   
4               42.408592                34.667900                       NaN   
...                   ...                      ...                       ...   
4375            56.952477                35.258080               1089.359741   
4376            56.953396                35.275970               1089.359741   
4377            56.979805                35.221176               1089.359741   
4378            56.984138                35.214283               1089.359741   
4379            56.966400                35.198269               1089.359741   

      6m_before_area_full_rent_mean  6m_before_area_year_rent_mean  \
0                               NaN                            NaN   
1                               NaN                            NaN   
2                               NaN                            NaN   
3                               NaN                            NaN   
4                               NaN                            NaN   
...                             ...                            ...   
4375                     617.018433                      29.325336   
4376                     617.018433                      29.325336   
4377                     617.018433                      29.325336   
4378                     617.018433                      29.325336   
4379                     617.018433                      29.325336   

      6m_after_year  6m_after_month  6m_before_deal_full_rent_rate  \
0               NaN             NaN                            NaN   
1               NaN             NaN                            NaN   
2               NaN             NaN                            NaN   
3               NaN             NaN                            NaN   
4               NaN             NaN                            NaN   
...             ...             ...                            ...   
4375         2022.0            12.0                      56.640465   
4376         2022.0            12.0                      56.640465   
4377         2022.0            12.0                      56.640465   
4378         2022.0            12.0                      56.640465   
4379         2022.0            12.0                      56.640465   

      6m_before_deal_year_rent_multiple  
0                                   NaN  
1                                   NaN  
2                                   NaN  
3                                   NaN  
4                                   NaN  
...                                 ...  
4375                          37.147392  
4376                          37.147392  
4377                          37.147392  
4378                          37.147392  
4379                          37.147392  

[4380

## 12개월전 종합 수치 병합 

In [15]:
df_area_micro_month_12m = df_area_micro_month.copy()
df_area_micro_month_12m['12m_after_year'] = df_area_micro_month_12m['year']+1
df_area_micro_month_12m['12m_after_month'] = df_area_micro_month_12m['month']

df_area_micro_month_12m = df_area_micro_month_12m.drop(['year','month'],axis=1)
df_area_micro_month_12m = df_area_micro_month_12m.astype({'12m_after_year':'int16', '12m_after_month' : 'int16'})
df_area_micro_month_12m.rename(columns = {'last_month_area_deal' : '12m_before_area_deal_mean', 'last_month_area_full_count' : '12m_before_area_full_rent_mean', 
                                      'last_month_area_year_rent' : '12m_before_area_year_rent_mean'}, inplace = True)

df_area_micro_month_12m['12m_before_deal_full_rent_rate'] = 100*(df_area_micro_month_12m['12m_before_area_full_rent_mean'] / df_area_micro_month_12m['12m_before_area_deal_mean'])
df_area_micro_month_12m['12m_before_deal_year_rent_multiple'] =df_area_micro_month_12m['12m_before_area_deal_mean']/ df_area_micro_month_12m['12m_before_area_year_rent_mean']


df_area_micro = pd.merge(df_area_micro, df_area_micro_month_12m, left_on=['year','month'], right_on=['12m_after_year','12m_after_month'],how = 'left')
df_area_micro

year  month  day    area_deal  area_full_rent  area_year_rent  \
0     2011      1    4   704.231018      326.309021       21.519497   
1     2011      1    5   768.772095      326.750854       21.022175   
2     2011      1    6   709.595642      303.017273       19.990875   
3     2011      1    7   727.185974      301.825531       20.578035   
4     2011      1    8   713.546570      302.605042       20.582342   
...    ...    ...  ...          ...             ...             ...   
4375  2022     12   27  1058.162842      602.649963       30.011925   
4376  2022     12   28  1057.969971      602.549805       29.991238   
4377  2022     12   29  1057.233032      602.409302       30.016970   
4378  2022     12   30  1056.862427      602.243958       30.012321   
4379  2022     12   31  1056.697632      601.962585       30.021296   

      deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
0               46.335510                32.725254                       NaN   
1               42.502956                36.569580                       NaN   
2               42.702808                35.495975                       NaN   
3               41.505962                35.337971                       NaN   
4               42.408592                34.667900                       NaN   
...                   ...                      ...                       ...   
4375            56.952477                35.258080               1089.359741   
4376            56.953396                35.275970               1089.359741   
4377            56.979805                35.221176               1089.359741   
4378            56.984138                35.214283               1089.359741   
4379            56.966400                35.198269               1089.359741   

      6m_before_area_full_rent_mean  ...  6m_after_month  \
0                               NaN  ...             NaN   
1                               NaN  ...             NaN   
2                               NaN  ...             NaN   
3                               NaN  ...             NaN   
4                               NaN  ...             NaN   
...                             ...  ...             ...   
4375                     617.018433  ...            12.0   
4376                     617.018433  ...            12.0   
4377                     617.018433  ...            12.0   
4378                     617.018433  ...            12.0   
4379                     617.018433  ...            12.0   

      6m_before_deal_full_rent_rate  6m_before_deal_year_rent_multiple  \
0                               NaN                                NaN   
1                               NaN                                NaN   
2                               NaN                                NaN   
3                               NaN                                NaN   
4                               NaN                                NaN   
...                             ...                                ...   
4375                      56.640465                          37.147392   
4376                      56.640465                          37.147392   
4377                      56.640465                          37.147392   
4378                      56.640465                          37.147392   
4379                      56.640465                          37.147392   

      12m_before_area_deal_mean  12m_before_area_full_rent_mean  \
0                           NaN                             NaN   
1                           NaN                             NaN   
2                           NaN                             NaN   
3                           NaN                             NaN   
4                           NaN                             NaN   
...                         ...                             ...   
4375                1081.178589                      608.400085   
4376                1081.178589               

## df_area_micro 컬럼 수정

In [16]:
df_area_micro = df_area_micro.drop(['6m_after_year','6m_after_month', '12m_after_year', '12m_after_month'], axis=1)

df_area_micro['6m_before_area_deal_mean'] = 100*((df_area_micro['area_deal'] - df_area_micro['6m_before_area_deal_mean'])/ df_area_micro['6m_before_area_deal_mean'])
df_area_micro['6m_before_area_full_rent_mean'] = 100*((df_area_micro['area_full_rent'] - df_area_micro['6m_before_area_full_rent_mean'])/ df_area_micro['6m_before_area_full_rent_mean'])
df_area_micro['6m_before_area_year_rent_mean'] = 100*((df_area_micro['area_year_rent'] - df_area_micro['6m_before_area_year_rent_mean'])/ df_area_micro['6m_before_area_year_rent_mean'])
df_area_micro['6m_before_deal_full_rent_rate'] = 100*((df_area_micro['deal_full_rent_rate'] - df_area_micro['6m_before_deal_full_rent_rate'])/ df_area_micro['6m_before_deal_full_rent_rate'])
df_area_micro['6m_before_deal_year_rent_multiple'] = 100*((df_area_micro['deal_year_rent_multiple'] - df_area_micro['6m_before_deal_year_rent_multiple'])/ df_area_micro['6m_before_deal_year_rent_multiple'])


df_area_micro['12m_before_area_deal_mean'] = 100*((df_area_micro['area_deal'] - df_area_micro['12m_before_area_deal_mean'])/ df_area_micro['12m_before_area_deal_mean'])
df_area_micro['12m_before_area_full_rent_mean'] = 100*((df_area_micro['area_full_rent'] - df_area_micro['12m_before_area_full_rent_mean'])/ df_area_micro['12m_before_area_full_rent_mean'])
df_area_micro['12m_before_area_year_rent_mean'] = 100*((df_area_micro['area_year_rent'] - df_area_micro['12m_before_area_year_rent_mean'])/ df_area_micro['12m_before_area_year_rent_mean'])
df_area_micro['12m_before_deal_full_rent_rate'] = 100*((df_area_micro['deal_full_rent_rate'] - df_area_micro['12m_before_deal_full_rent_rate'])/ df_area_micro['12m_before_deal_full_rent_rate'])
df_area_micro['12m_before_deal_year_rent_multiple'] = 100*((df_area_micro['deal_year_rent_multiple'] - df_area_micro['12m_before_deal_year_rent_multiple'])/ df_area_micro['12m_before_deal_year_rent_multiple'])

df_area_micro.head()

year  month  day   area_deal  area_full_rent  area_year_rent  \
0  2011      1    4  704.231018      326.309021       21.519497   
1  2011      1    5  768.772095      326.750854       21.022175   
2  2011      1    6  709.595642      303.017273       19.990875   
3  2011      1    7  727.185974      301.825531       20.578035   
4  2011      1    8  713.546570      302.605042       20.582342   

   deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
0            46.335510                32.725254                       NaN   
1            42.502956                36.569580                       NaN   
2            42.702808                35.495975                       NaN   
3            41.505962                35.337971                       NaN   
4            42.408592                34.667900                       NaN   

   6m_before_area_full_rent_mean  6m_before_area_year_rent_mean  \
0                            NaN                            NaN   
1                            NaN                            NaN   
2                            NaN                            NaN   
3                            NaN                            NaN   
4                            NaN                            NaN   

   6m_before_deal_full_rent_rate  6m_before_deal_year_rent_multiple  \
0                            NaN                                NaN   
1                            NaN                                NaN   
2                            NaN                                NaN   
3                            NaN                                NaN   
4                            NaN                                NaN   

   12m_before_area_deal_mean  12m_before_area_full_rent_mean  \
0                        NaN                             NaN   
1                        NaN                             NaN   
2                        NaN                             NaN   
3                        NaN                             NaN   
4                        NaN                             NaN   

   12m_before_area_year_rent_mean  12m_before_deal_full_rent_rate  \
0                             NaN                             NaN   
1                             NaN                             NaN   
2                             NaN                             NaN   
3                             NaN                             NaN   
4                             NaN                             NaN   

   12m_before_deal_year_rent_multiple  
0                                 NaN  
1                                 NaN  
2                                 NaN  
3                                 NaN  
4                                 NaN

In [17]:
df_area_micro = df_area_micro.dropna()
df_area_micro.head()

year  month  day   area_deal  area_full_rent  area_year_rent  \
393  2012      2    1  552.710754      310.284698       20.539133   
394  2012      2    2  552.615540      310.167419       20.526850   
395  2012      2    3  552.451233      310.077454       20.524391   
396  2012      2    4  552.501587      310.777069       20.542120   
397  2012      2    5  552.668823      310.628754       20.545334   

     deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
393            56.138714                26.910131                 -4.511396   
394            56.127159                26.921595                 -4.527846   
395            56.127571                26.916815                 -4.556232   
396            56.249081                26.896036                 -4.547534   
397            56.205223                26.899967                 -4.518641   

     6m_before_area_full_rent_mean  6m_before_area_year_rent_mean  \
393                       3.613158                       2.636212   
394                       3.573995                       2.574831   
395                       3.543953                       2.562545   
396                       3.777575                       2.651138   
397                       3.728049                       2.667198   

     6m_before_deal_full_rent_rate  6m_before_deal_year_rent_multiple  \
393                       8.508401                          -6.964019   
394                       8.486068                          -6.924388   
395                       8.486864                          -6.940913   
396                       8.721725                          -7.012751   
397                       8.636954                          -6.999160   

     12m_before_area_deal_mean  12m_before_area_full_rent_mean  \
393                 -18.886459                        1.054163   
394                 -18.900433                        1.015967   
395                 -18.924545                        0.986667   
396                 -18.917156                        1.214519   
397                 -18.892612                        1.166216   

     12m_before_area_year_rent_mean  12m_before_deal_full_rent_rate  \
393                       -2.110301                       24.583603   
394                       -2.168843                       24.557962   
395                       -2.180561                       24.558876   
396                       -2.096065                       24.828531   
397                       -2.080748                       24.731203   

     12m_before_deal_year_rent_multiple  
393                          -17.137817  
394                          -17.102518  
395                          -17.117237  
396                          -17.181219  
397                          -17.169113

In [18]:
df_area_micro.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3987 entries, 393 to 4379
Data columns (total 18 columns):
 #   Column                              Non-Null Count  Dtype  
---  ------                              --------------  -----  
 0   year                                3987 non-null   int64  
 1   month                               3987 non-null   int64  
 2   day                                 3987 non-null   int64  
 3   area_deal                           3987 non-null   float32
 4   area_full_rent                      3987 non-null   float32
 5   area_year_rent                      3987 non-null   float32
 6   deal_full_rent_rate                 3987 non-null   float32
 7   deal_year_rent_multiple             3987 non-null   float32
 8   6m_before_area_deal_mean            3987 non-null   float32
 9   6m_before_area_full_rent_mean       3987 non-null   float32
 10  6m_before_area_year_rent_mean       3987 non-null   float32
 11  6m_before_deal_full_rent_rate       3987 

## 1년후 가격 병합

In [19]:
import pandas as pd
df_economic = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/final_economic.pkl')
df_economic.head()

date  year  month  day  apartment_index  kospi_index  korea_rp  \
0  2012-02-01  2012      2    1        86.800003  1959.239990      3.25   
1  2012-02-02  2012      2    2        86.800003  1984.300049      3.25   
2  2012-02-03  2012      2    3        86.800003  1972.339966      3.25   
3  2012-02-04  2012      2    4        86.800003  1972.339966      3.25   
4  2012-02-05  2012      2    5        86.800003  1972.339966      3.25   

   korea_3_year  korea_10_year  us_3_month  ...  us_10_year_12m_before  \
0          3.38           3.75       0.061  ...              -1.735429   
1          3.38           3.76       0.084  ...              -1.742429   
2          3.38           3.76       0.079  ...              -1.641429   
3          3.38           3.76       0.079  ...              -1.641429   
4          3.38           3.76       0.079  ...              -1.641429   

   korea_10-3_year_12m_before  us_10-2_year_12m_before  \
0                   -0.436429                -1.199357   
1                   -0.426429                -1.206357   
2                   -0.426429                -1.117357   
3                   -0.426429                -1.117357   
4                   -0.426429                -1.117357   

   us_10-3_year_month_12m_before  \
0                      -1.668893   
1                      -1.698893   
2                      -1.592893   
3                      -1.592893   
4                      -1.592893   

   last_month_total_apartment_supply_12m_before  \
0                                       -3520.0   
1                                       -3520.0   
2                                       -3520.0   
3                                       -3520.0   
4                                       -3520.0   

   last_month_total_unsold_count_12m_before  \
0                                    -379.0   
1                                    -379.0   
2                                    -379.0   
3                                    -379.0   
4                                    -379.0   

   last_month_total_unsold_ratio_12m_before  \
0                                 61.257435   
1                                 61.257435   
2                                 61.257435   
3                                 61.257435   
4                                 61.257435   

   last_month_total_deal_count_12m_before  \
0                                 -4393.0   
1                                 -4393.0   
2                                 -4393.0   
3                                 -4393.0   
4                                 -4393.0   

   last_month_total_full_rent_count_12m_before  \
0                                      -1891.0   
1                                      -1891.0   
2                                      -1891.0   
3                                      -1891.0   
4                                      -1891.0   

   last_month_total_month_rent_count_12m_before  
0                                        -237.0  
1                                        -237.0  
2                                        -237.0  
3                                        -237.0  
4                                        -237.0  

[5 rows x 53 columns]

In [20]:
df_original_dataset = pd.merge(df_area_micro,df_economic, on = ['year','month','day'])
df_original_dataset

year  month  day    area_deal  area_full_rent  area_year_rent  \
0     2012      2    1   552.710754      310.284698       20.539133   
1     2012      2    2   552.615540      310.167419       20.526850   
2     2012      2    3   552.451233      310.077454       20.524391   
3     2012      2    4   552.501587      310.777069       20.542120   
4     2012      2    5   552.668823      310.628754       20.545334   
...    ...    ...  ...          ...             ...             ...   
3982  2022     12   27  1058.162842      602.649963       30.011925   
3983  2022     12   28  1057.969971      602.549805       29.991238   
3984  2022     12   29  1057.233032      602.409302       30.016970   
3985  2022     12   30  1056.862427      602.243958       30.012321   
3986  2022     12   31  1056.697632      601.962585       30.021296   

      deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
0               56.138714                26.910131                 -4.511396   
1               56.127159                26.921595                 -4.527846   
2               56.127571                26.916815                 -4.556232   
3               56.249081                26.896036                 -4.547534   
4               56.205223                26.899967                 -4.518641   
...                   ...                      ...                       ...   
3982            56.952477                35.258080                 -2.863783   
3983            56.953396                35.275970                 -2.881488   
3984            56.979805                35.221176                 -2.949137   
3985            56.984138                35.214283                 -2.983157   
3986            56.966400                35.198269                 -2.998285   

      6m_before_area_full_rent_mean  ...  us_10_year_12m_before  \
0                          3.613158  ...              -1.735429   
1                          3.573995  ...              -1.742429   
2                          3.543953  ...              -1.641429   
3                          3.777575  ...              -1.641429   
4                          3.728049  ...              -1.641429   
...                             ...  ...                    ...   
3982                      -2.328694  ...               2.393742   
3983                      -2.344926  ...               2.430742   
3984                      -2.367698  ...               2.364742   
3985                      -2.394495  ...               2.423742   
3986                      -2.440097  ...               2.423742   

      korea_10-3_year_12m_before  us_10-2_year_12m_before  \
0                      -0.436429                -1.199357   
1                      -0.426429                -1.206357   
2                      -0.426429                -1.117357   
3                      -0.426429                -1.117357   
4                      -0.426429                -1.117357   
...                          ...                      ...   
3982                   -0.434968                -1.326813   
3983                   -0.378968                -1.264513   
3984                   -0.380968                -1.338713   
3985                   -0.375968                -1.342013   
3986                   -0.375968                -1.342013   

      us_10-3_year_month_12m_before  \
0                         -1.668893   
1                         -1.698893   
2                         -1.592893   
3                         -1.592893   
4                         -1.592893   
...                             ...   
3982                      -1.857890   
3983                      -1.966890   
3984                      -1.998890   
3985                      -1.921890   
3986                      -1.921890   

      last_month_total_apartment_supply_12m_before  \
0                                          -3520.0   
1                                          -3520.0   
2                      

In [21]:
df_original_dataset.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3987 entries, 0 to 3986
Data columns (total 68 columns):
 #   Column                                        Non-Null Count  Dtype  
---  ------                                        --------------  -----  
 0   year                                          3987 non-null   int64  
 1   month                                         3987 non-null   int64  
 2   day                                           3987 non-null   int64  
 3   area_deal                                     3987 non-null   float32
 4   area_full_rent                                3987 non-null   float32
 5   area_year_rent                                3987 non-null   float32
 6   deal_full_rent_rate                           3987 non-null   float32
 7   deal_year_rent_multiple                       3987 non-null   float32
 8   6m_before_area_deal_mean                      3987 non-null   float32
 9   6m_before_area_full_rent_mean                 3987 non-null   f

In [22]:
df_original_dataset['date'] = pd.to_datetime(df_original_dataset['date'])
df_original_dataset.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3987 entries, 0 to 3986
Data columns (total 68 columns):
 #   Column                                        Non-Null Count  Dtype         
---  ------                                        --------------  -----         
 0   year                                          3987 non-null   int64         
 1   month                                         3987 non-null   int64         
 2   day                                           3987 non-null   int64         
 3   area_deal                                     3987 non-null   float32       
 4   area_full_rent                                3987 non-null   float32       
 5   area_year_rent                                3987 non-null   float32       
 6   deal_full_rent_rate                           3987 non-null   float32       
 7   deal_year_rent_multiple                       3987 non-null   float32       
 8   6m_before_area_deal_mean                      3987 non-null   float3

In [23]:
df_future = df_original_dataset[['date','area_deal']].copy()
df_future.head()

date   area_deal
0 2012-02-01  552.710754
1 2012-02-02  552.615540
2 2012-02-03  552.451233
3 2012-02-04  552.501587
4 2012-02-05  552.668823

In [24]:
df_future['date'] = df_future['date'] - pd.Timedelta(days=365)
df_future.head()

date   area_deal
0 2011-02-01  552.710754
1 2011-02-02  552.615540
2 2011-02-03  552.451233
3 2011-02-04  552.501587
4 2011-02-05  552.668823

In [25]:
df_future['year'] = df_future['date'].dt.year
df_future['month'] = df_future['date'].dt.month
df_future['day'] = df_future['date'].dt.day
df_future.rename(columns = {'area_deal' : 'future_area_deal'}, inplace = True)
df_future.drop('date',axis=1,inplace=True)

df_future.head()

future_area_deal  year  month  day
0        552.710754  2011      2    1
1        552.615540  2011      2    2
2        552.451233  2011      2    3
3        552.501587  2011      2    4
4        552.668823  2011      2    5

In [26]:
df_original_dataset = pd.merge(df_original_dataset,df_future, on = ['year','month','day'])
df_original_dataset

year  month  day    area_deal  area_full_rent  area_year_rent  \
0     2012      2    1   552.710754      310.284698       20.539133   
1     2012      2    2   552.615540      310.167419       20.526850   
2     2012      2    3   552.451233      310.077454       20.524391   
3     2012      2    4   552.501587      310.777069       20.542120   
4     2012      2    5   552.668823      310.628754       20.545334   
...    ...    ...  ...          ...             ...             ...   
3617  2021     12   27  1083.472168      607.116211       28.811615   
3618  2021     12   28  1083.753906      606.659790       28.847986   
3619  2021     12   29  1083.566772      606.564270       28.837791   
3620  2021     12   30  1083.580566      606.848999       28.828548   
3621  2021     12   31  1083.398315      607.298218       28.820314   

      deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
0               56.138714                26.910131                 -4.511396   
1               56.127159                26.921595                 -4.527846   
2               56.127571                26.916815                 -4.556232   
3               56.249081                26.896036                 -4.547534   
4               56.205223                26.899967                 -4.518641   
...                   ...                      ...                       ...   
3617            56.034313                37.605396                  7.364027   
3618            55.977631                37.567749                  7.391945   
3619            55.978481                37.574539                  7.373402   
3620            56.004047                37.587067                  7.374769   
3621            56.054932                37.591480                  7.356709   

      6m_before_area_full_rent_mean  ...  korea_10-3_year_12m_before  \
0                          3.613158  ...                   -0.436429   
1                          3.573995  ...                   -0.426429   
2                          3.543953  ...                   -0.426429   
3                          3.777575  ...                   -0.426429   
4                          3.728049  ...                   -0.426429   
...                             ...  ...                         ...   
3617                       4.543994  ...                   -0.272226   
3618                       4.465400  ...                   -0.298226   
3619                       4.448951  ...                   -0.311226   
3620                       4.497981  ...                   -0.262226   
3621                       4.575335  ...                   -0.248226   

      us_10-2_year_12m_before  us_10-3_year_month_12m_before  \
0                   -1.199357                      -1.668893   
1                   -1.206357                      -1.698893   
2                   -1.117357                      -1.592893   
3                   -1.117357                      -1.592893   
4                   -1.117357                      -1.592893   
...                       ...                            ...   
3617                -0.024955                       0.574126   
3618                -0.069055                       0.576126   
3619                 0.006845                       0.658126   
3620                -0.020455                       0.614126   
3621                -0.019255                       0.612126   

      last_month_total_apartment_supply_12m_before  \
0                                          -3520.0   
1                                          -3520.0   
2                                          -3520.0   
3                                          -3520.0   
4                                          -3520.0   
...                                            ...   
3617                                         789.0   
3618                                         789.0   
3619                                         789.0   
3620              

In [27]:
df_original_dataset['future_change_rate'] = 100*((df_original_dataset['future_area_deal'] - df_original_dataset['area_deal'])/df_original_dataset['area_deal'])
df_original_dataset.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3622 entries, 0 to 3621
Data columns (total 70 columns):
 #   Column                                        Non-Null Count  Dtype         
---  ------                                        --------------  -----         
 0   year                                          3622 non-null   int64         
 1   month                                         3622 non-null   int64         
 2   day                                           3622 non-null   int64         
 3   area_deal                                     3622 non-null   float32       
 4   area_full_rent                                3622 non-null   float32       
 5   area_year_rent                                3622 non-null   float32       
 6   deal_full_rent_rate                           3622 non-null   float32       
 7   deal_year_rent_multiple                       3622 non-null   float32       
 8   6m_before_area_deal_mean                      3622 non-null   float3

## 파일 저장

In [28]:
df_original_dataset.to_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/df_original_dataset.pkl')

# 기계학습

- 앞에서의 기계학습 방법들을 적용시켰을 경우, 모델의 정확도가 너무 낮은 문제가 발생, 원래목표와의 다른 차선책으로 집값의 가격들의 합(지수처럼)의 변경을 예측하는 모델을 생성

## 데이터 불러오기

In [29]:
import pandas as pd

df_original_dataset = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/df_original_dataset.pkl')

## 학습용 원본 데이터셋 생성

In [32]:
pd.set_option('display.max_rows', 70)

df_original_dataset.corr()['future_change_rate'].sort_values(ascending=False).to_frame()

<ipython-input-32-dcaa0e08b7dc>:3: FutureWarning: The default value of numeric_only in DataFrame.corr is deprecated. In a future version, it will default to False. Select only valid columns or specify the value of numeric_only to silence this warning.
  df_original_dataset.corr()['future_change_rate'].sort_values(ascending=False).to_frame()


future_change_rate
future_change_rate                                      1.000000
apartment_index                                         0.755426
12m_before_deal_year_rent_multiple                      0.742933
6m_before_deal_year_rent_multiple                       0.696503
year                                                    0.668162
12m_before_area_deal_mean                               0.647811
6m_before_area_deal_mean                                0.636636
area_full_rent                                          0.584019
future_area_deal                                        0.573267
area_year_rent                                          0.480645
us_3_month                                              0.450130
area_deal                                               0.394647
us_2_year                                               0.382927
deal_year_rent_multiple                                 0.380459
last_month_total_month_rent_count                       0.348581
last_month_total_deal_count                             0.294960
korea_10-3_year_12m_before                              0.283052
korea_10-3_year_6m_before                               0.253250
last_month_total_apartment_supply                       0.252292
deal_full_rent_rate                                     0.226187
kospi_index_6m_before                                   0.193400
last_month_total_full_rent_count_12m_before             0.191232
6m_before_area_full_rent_mean                           0.179499
kospi_index                                             0.149904
us_10-2_year_12m_before                                 0.137463
korea_10_year_12m_before                                0.123279
12m_before_area_full_rent_mean                          0.119267
korea_10_year_6m_before                                 0.114440
6m_before_area_year_rent_mean                           0.106761
last_month_total_apartment_supply_12m_before            0.101814
us_10-2_year_6m_before                                  0.092196
12m_before_area_year_rent_mean                          0.079619
kospi_index_12m_before                                  0.065191
last_month_total_full_rent_count                        0.034470
us_10-3_year_month_12m_before                           0.033882
last_month_total_deal_count_12m_before                  0.020413
last_month_total_apartment_supply_6m_before             0.003940
korea_3_year_12m_before                                 0.003273
day                                                     0.002265
us_10-3_year_month_6m_before                           -0.000878
month                                                  -0.003869
last_month_total_full_rent_count_6m_before             -0.010587
korea_3_year_6m_before                                 -0.010788
korea_10-3_year                                        -0.022639
last_month_total_deal_count_6m_before                  -0.027249
last_month_total_month_rent_count_6m_before            -0.098185
last_month_total_unsold_ratio_6m_before                -0.102897
last_month_total_month_rent_count_12m_before           -0.112522
last_month_total_unsold_count_6m_before                -0.134540
korea_rp_6m_before                                     -0.142273
last_month_total_unsold_ratio_12m_before               -0.146984
last_month_total_unsold_count_12m_before               -0.180521
korea_rp_12m_before                                    -0.195297
us_10_year                                             -0.212083
us_10_year_12m_before                                  -0.215740
us_10_year_6m_before                                   -0.254929
us_3_month_12m_before                                  -0.258548
us_3_month_6m_before                                   -0.292268
us_2_year_12m_before                                   -0.336692
us_2_year_6m_before                                    -0.362473
last_month_total_unsold_ratio                          -0.542052
us_10-3_year_mon

In [56]:
df_corr = df_original_dataset.corr(numeric_only=False)['future_change_rate']
df_corr.head()

year              0.668162
month            -0.003869
day               0.002265
area_deal         0.394647
area_full_rent    0.584019
Name: future_change_rate, dtype: float64

In [57]:
df_corr.info()

<class 'pandas.core.series.Series'>
Index: 70 entries, year to future_change_rate
Series name: future_change_rate
Non-Null Count  Dtype  
--------------  -----  
70 non-null     float64
dtypes: float64(1)
memory usage: 3.1+ KB


In [58]:
df_corr.name = 'correlation'
df_corr.info()

<class 'pandas.core.series.Series'>
Index: 70 entries, year to future_change_rate
Series name: correlation
Non-Null Count  Dtype  
--------------  -----  
70 non-null     float64
dtypes: float64(1)
memory usage: 3.1+ KB


In [59]:
learning_feature_list = list(df_corr[(df_corr >= 0.6) | (df_corr <= -0.6)].index)
learning_feature_list

['year',
 '6m_before_area_deal_mean',
 '6m_before_deal_full_rent_rate',
 '6m_before_deal_year_rent_multiple',
 '12m_before_area_deal_mean',
 '12m_before_deal_full_rent_rate',
 '12m_before_deal_year_rent_multiple',
 'date',
 'apartment_index',
 'korea_rp',
 'korea_3_year',
 'korea_10_year',
 'us_10-2_year',
 'us_10-3_year_month',
 'last_month_total_unsold_count',
 'future_change_rate']

In [60]:
to_remove = ['year','date','apartment_index']
for x in to_remove:
    learning_feature_list.remove(x)
learning_feature_list

['6m_before_area_deal_mean',
 '6m_before_deal_full_rent_rate',
 '6m_before_deal_year_rent_multiple',
 '12m_before_area_deal_mean',
 '12m_before_deal_full_rent_rate',
 '12m_before_deal_year_rent_multiple',
 'korea_rp',
 'korea_3_year',
 'korea_10_year',
 'us_10-2_year',
 'us_10-3_year_month',
 'last_month_total_unsold_count',
 'future_change_rate']

In [63]:
df_train_test = df_original_dataset[learning_feature_list]
df_train_test

6m_before_area_deal_mean  6m_before_deal_full_rent_rate  \
0                    -4.511396                       8.508401   
1                    -4.527846                       8.486068   
2                    -4.556232                       8.486864   
3                    -4.547534                       8.721725   
4                    -4.518641                       8.636954   
...                        ...                            ...   
3617                  7.364027                      -2.626612   
3618                  7.391945                      -2.725111   
3619                  7.373402                      -2.723633   
3620                  7.374769                      -2.679206   
3621                  7.356709                      -2.590782   

      6m_before_deal_year_rent_multiple  12m_before_area_deal_mean  \
0                             -6.964019                 -18.886459   
1                             -6.924388                 -18.900433   
2                             -6.940913                 -18.924545   
3                             -7.012751                 -18.917156   
4                             -6.999160                 -18.892612   
...                                 ...                        ...   
3617                           0.973390                  15.883393   
3618                           0.872304                  15.913527   
3619                           0.890536                  15.893512   
3620                           0.924173                  15.894987   
3621                           0.936024                  15.875494   

      12m_before_deal_full_rent_rate  12m_before_deal_year_rent_multiple  \
0                          24.583603                          -17.137817   
1                          24.557962                          -17.102518   
2                          24.558876                          -17.117237   
3                          24.828531                          -17.181219   
4                          24.731203                          -17.169113   
...                              ...                                 ...   
3617                       -5.929564                            5.544213   
3618                       -6.024723                            5.438552   
3619                       -6.023295                            5.457609   
3620                       -5.980375                            5.492769   
3621                       -5.894950                            5.505156   

      korea_rp  korea_3_year  korea_10_year  us_10-2_year  us_10-3_year_month  \
0         3.25         3.380          3.750        1.6040               1.769   
1         3.25         3.380          3.760        1.5970               1.739   
2         3.25         3.380          3.760        1.6860               1.845   
3         3.25         3.380          3.760        1.6860               1.845   
4         3.25         3.380          3.760        1.6860               1.845   
...        ...           ...            ...           ...                 ...   
3617      1.00         1.776          2.212        0.7722               1.421   
3618      1.00         1.786          2.196        0.7281               1.423   
3619      1.00         1.783          2.180        0.8040               1.505   
3620      1.00         1.802          2.248        0.7767               1.461   
3621      1.00         1.795          2.255        0.7779               1.459   

      last_month_total_unsold_count  future_change_rate  
0                              1890           -7.197249  
1                              1890           -7.221528  
2                              1890           -7.166293  
3                              1890           -7.169163  
4                              1890           -7.180313  
...                             ...                 ...  
3617                             54           -2.335946  
3618                             5

In [64]:
df_train_test.to_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/df_train_test.pkl')

## 학습, 테스트 데이터 셋 생성

In [2]:
import pandas as pd

df_train_test = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/ver_4/df_train_test.pkl')
df_train_test.head()

6m_before_area_deal_mean  6m_before_deal_full_rent_rate  \
0                 -4.511396                       8.508401   
1                 -4.527846                       8.486068   
2                 -4.556232                       8.486864   
3                 -4.547534                       8.721725   
4                 -4.518641                       8.636954   

   6m_before_deal_year_rent_multiple  12m_before_area_deal_mean  \
0                          -6.964019                 -18.886459   
1                          -6.924388                 -18.900433   
2                          -6.940913                 -18.924545   
3                          -7.012751                 -18.917156   
4                          -6.999160                 -18.892612   

   12m_before_deal_full_rent_rate  12m_before_deal_year_rent_multiple  \
0                       24.583603                          -17.137817   
1                       24.557962                          -17.102518   
2                       24.558876                          -17.117237   
3                       24.828531                          -17.181219   
4                       24.731203                          -17.169113   

   korea_rp  korea_3_year  korea_10_year  us_10-2_year  us_10-3_year_month  \
0      3.25          3.38           3.75         1.604               1.769   
1      3.25          3.38           3.76         1.597               1.739   
2      3.25          3.38           3.76         1.686               1.845   
3      3.25          3.38           3.76         1.686               1.845   
4      3.25          3.38           3.76         1.686               1.845   

   last_month_total_unsold_count  future_change_rate  
0                           1890           -7.197249  
1                           1890           -7.221528  
2                           1890           -7.166293  
3                           1890           -7.169163  
4                           1890           -7.180313

In [3]:
df_train_test.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3622 entries, 0 to 3621
Data columns (total 13 columns):
 #   Column                              Non-Null Count  Dtype  
---  ------                              --------------  -----  
 0   6m_before_area_deal_mean            3622 non-null   float32
 1   6m_before_deal_full_rent_rate       3622 non-null   float32
 2   6m_before_deal_year_rent_multiple   3622 non-null   float32
 3   12m_before_area_deal_mean           3622 non-null   float32
 4   12m_before_deal_full_rent_rate      3622 non-null   float32
 5   12m_before_deal_year_rent_multiple  3622 non-null   float32
 6   korea_rp                            3622 non-null   float32
 7   korea_3_year                        3622 non-null   float32
 8   korea_10_year                       3622 non-null   float32
 9   us_10-2_year                        3622 non-null   float32
 10  us_10-3_year_month                  3622 non-null   float32
 11  last_month_total_unsold_count       3622 no

In [4]:
train_columns = list(df_train_test.columns)
train_columns.remove('future_change_rate')
print(train_columns)

['6m_before_area_deal_mean', '6m_before_deal_full_rent_rate', '6m_before_deal_year_rent_multiple', '12m_before_area_deal_mean', '12m_before_deal_full_rent_rate', '12m_before_deal_year_rent_multiple', 'korea_rp', 'korea_3_year', 'korea_10_year', 'us_10-2_year', 'us_10-3_year_month', 'last_month_total_unsold_count']


In [5]:
from sklearn.model_selection import train_test_split

final_df_train, final_df_test = train_test_split(df_train_test, test_size=0.3, random_state=42)

## 모델 적용

### 선형회귀 모델

#### 기본모델

In [6]:
# Importing required libraries
import pandas as pd
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np

# Splitting the data into training and testing sets
X_train = final_df_train[train_columns]
y_train = final_df_train['future_change_rate']

X_test = final_df_test[train_columns]
y_test = final_df_test['future_change_rate']
# Creating a Linear Regression model
model = LinearRegression()

# Training the model on the training set
model.fit(X_train, y_train)

# Making predictions on the testing set
y_pred = model.predict(X_test)

# Evaluating the model using Mean Squared Error (MSE)
mse = mean_squared_error(y_test, y_pred)
print('Mean Squared Error:', mse)
print('Root Mean Squared Error:', np.sqrt(mse))


Mean Squared Error: 6.080049670703312
Root Mean Squared Error: 2.4657756732321197


#### k-fold, validation 추가

NameError: ignored

### 다항회귀 모델

#### 기본 모델

In [8]:
# Importing required libraries
import pandas as pd
from sklearn.preprocessing import PolynomialFeatures
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np

# Splitting the data into training and testing sets
X_train = final_df_train[train_columns]
y_train = final_df_train['future_change_rate']

X_test = final_df_test[train_columns]
y_test = final_df_test['future_change_rate']

# Creating polynomial features
poly = PolynomialFeatures(degree=2)
X_train_poly = poly.fit_transform(X_train)
X_test_poly = poly.transform(X_test)

# Creating a Polynomial Regression model
model = LinearRegression()

# Training the model on the training set
model.fit(X_train_poly, y_train)

# Making predictions on the testing set
y_pred = model.predict(X_test_poly)

# Evaluating the model using Mean Squared Error (MSE)
mse = mean_squared_error(y_test, y_pred)
print('Mean Squared Error:', mse)
print('Root Mean Squared Error:', np.sqrt(mse))


Mean Squared Error: 0.4884238783233166
Root Mean Squared Error: 0.6988732920374884


In [9]:
# Importing required libraries
import pandas as pd
from sklearn.preprocessing import PolynomialFeatures
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np

# Splitting the data into training and testing sets
X_train = final_df_train[train_columns]
y_train = final_df_train['future_change_rate']

X_test = final_df_test[train_columns]
y_test = final_df_test['future_change_rate']

# Creating polynomial features
poly = PolynomialFeatures(degree=3)
X_train_poly = poly.fit_transform(X_train)
X_test_poly = poly.transform(X_test)

# Creating a Polynomial Regression model
model = LinearRegression()

# Training the model on the training set
model.fit(X_train_poly, y_train)

# Making predictions on the testing set
y_pred = model.predict(X_test_poly)

# Evaluating the model using Mean Squared Error (MSE)
mse = mean_squared_error(y_test, y_pred)
print('Mean Squared Error:', mse)
print('Root Mean Squared Error:', np.sqrt(mse))


Mean Squared Error: 0.05991033133674959
Root Mean Squared Error: 0.24476587044918985


In [10]:
# Importing required libraries
import pandas as pd
from sklearn.preprocessing import PolynomialFeatures
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np

# Splitting the data into training and testing sets
X_train = final_df_train[train_columns]
y_train = final_df_train['future_change_rate']

X_test = final_df_test[train_columns]
y_test = final_df_test['future_change_rate']

# Creating polynomial features
poly = PolynomialFeatures(degree=4)
X_train_poly = poly.fit_transform(X_train)
X_test_poly = poly.transform(X_test)

# Creating a Polynomial Regression model
model = LinearRegression()

# Training the model on the training set
model.fit(X_train_poly, y_train)

# Making predictions on the testing set
y_pred = model.predict(X_test_poly)

# Evaluating the model using Mean Squared Error (MSE)
mse = mean_squared_error(y_test, y_pred)
print('Mean Squared Error:', mse)
print('Root Mean Squared Error:', np.sqrt(mse))


Mean Squared Error: 0.06437315725753345
Root Mean Squared Error: 0.2537186576851089


In [13]:
# Importing required libraries
import pandas as pd
from sklearn.preprocessing import PolynomialFeatures
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np

# Splitting the data into training and testing sets
X_train = final_df_train[train_columns]
y_train = final_df_train['future_change_rate']

X_test = final_df_test[train_columns]
y_test = final_df_test['future_change_rate']

# Creating polynomial features
poly = PolynomialFeatures(degree=5)
X_train_poly = poly.fit_transform(X_train)
X_test_poly = poly.transform(X_test)

# Creating a Polynomial Regression model
model = LinearRegression()

# Training the model on the training set
model.fit(X_train_poly, y_train)

# Making predictions on the testing set
y_pred = model.predict(X_test_poly)

# Evaluating the model using Mean Squared Error (MSE)
mse = mean_squared_error(y_test, y_pred)
print('Mean Squared Error:', mse)
print('Root Mean Squared Error:', np.sqrt(mse))


Mean Squared Error: 0.5247150231218368
Root Mean Squared Error: 0.7243721578869778


### Gradient Boosting 모델

In [ ]:
# Importing required libraries
import pandas as pd
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np

# Splitting the data into training and testing sets
X_train = final_df_train[train_columns]
y_train = final_df_train['future_change_rate']

X_test = final_df_test[train_columns]
y_test = final_df_test['future_change_rate']

# Creating a Gradient Boosting model
model = GradientBoostingRegressor(n_estimators=100, learning_rate=0.1, max_depth=3, random_state=0)

# Training the model on the training set
model.fit(X_train, y_train)

# Making predictions on the testing set
y_pred = model.predict(X_test)

# Evaluating the model using Mean Squared Error (MSE)
mse = mean_squared_error(y_test, y_pred)
print('Mean Squared Error:', mse)
print('Root Mean Squared Error:', np.sqrt(mse))


Mean Squared Error: 2.382869559432075
Root Mean Squared Error: 1.5436546114439185


### XGBoost 모델

In [11]:
# Importing required libraries
import pandas as pd
import xgboost as xgb
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np

# Splitting the data into training and testing sets
X_train = final_df_train[train_columns]
y_train = final_df_train['future_change_rate']

X_test = final_df_test[train_columns]
y_test = final_df_test['future_change_rate']

# Creating an XGBoost model
model = xgb.XGBRegressor(objective ='reg:squarederror', n_estimators=100, learning_rate=0.1, max_depth=3, random_state=0)

# Training the model on the training set
model.fit(X_train, y_train)

# Making predictions on the testing set
y_pred = model.predict(X_test)

# Evaluating the model using Mean Squared Error (MSE)
mse = mean_squared_error(y_test, y_pred)
print('Mean Squared Error:', mse)
print('Root Mean Squared Error:', np.sqrt(mse))


Mean Squared Error: 0.230251
Root Mean Squared Error: 0.47984478


### RandomForest Regressor 모델



In [12]:
# Importing required libraries
import pandas as pd
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np



X_train = final_df_train[train_columns]
y_train = final_df_train['future_change_rate']

X_test = final_df_test[train_columns]
y_test = final_df_test['future_change_rate']

# Creating a Random Forest Regressor model
model = RandomForestRegressor(n_estimators=100, random_state=0)

# Training the model on the training set
model.fit(X_train, y_train)

# Making predictions on the testing set
y_pred = model.predict(X_test)

# Evaluating the model using Mean Squared Error (MSE)
mse = mean_squared_error(y_test, y_pred)
print('Mean Squared Error:', mse)
print('Root Mean Squared Error:', np.sqrt(mse))


Mean Squared Error: 0.055941418013142764
Root Mean Squared Error: 0.2365193818974309


# 결론

- 개별 아파트들의 집값 예측은 상당히 모델의 성능이 떨어졌음
- 개별 아파트 집값 예측의 성능이 떨어진 원인으로, 지역별로 전세가율, 집값 변화율 등이 적용되는게 다를 텐데 지역별 차등을 두지 않아서 그런게 아닌가 싶음
- 모든 집값의 합의 변화율은 학습 데이터셋이 너무 적기에 데이터의 양이 더 많아져야 할 것 같음
- 개별 아파트 집값 예측을 위해서 '월별'로 집값의 가격들을 구했으나, 데이터셋이 부족함으로 '일별'로 집값의 정보들을 수정할 필요성을 느낌